In [4]:
# @title
from datetime import datetime
from IPython.display import display, HTML

today_str = datetime.today().strftime('%Y%m%d')
notebook_name = f"{today_str}_Converting_Merging_RUL&FeatureCalculation.ipynb"

display(HTML(f'''
<div style="border: 2px solid #ff9800; background-color: #fff8e1; padding: 20px; border-radius: 10px; font-family: Arial, sans-serif;">
  <h2 style="color: #e65100; margin-top: 0;">⚠️🚨 <strong>WARNING!</strong> 🚨⚠️</h2>

  <h3>🆕 <strong>IF YOU ARE STARTING TO WORK WITH A NEW LAB FILE, PLEASE READ CAREFULLY:</strong></h3>

  <ul style="font-size: 15px; line-height: 1.6;">
    <li><strong>📌 Make sure your dataset in <code>.json</code> format has been converted to <code>.csv</code>.</strong><br>
        If not, run the notebook named <code><strong>convert</strong></code> to perform the conversion first.</li>
    <li><strong>✅ Do NOT proceed unless your dataset is in the correct <code>.csv</code> format.</strong></li>
  </ul>

  <p style="margin-top: 20px;"><strong>🗂️ Rename this notebook using today’s date in the following format:</strong></p>
  <pre style="background-color: #f5f5f5; padding: 12px; border-left: 5px solid #ff9800; font-size: 15px;">
📁 {notebook_name}
  </pre>
  <p style="font-size: 14px; color: #d84315;"><strong>📝 Replace <code>Lab_XX</code> with the correct lab number before saving!</strong></p>

  <p style="margin-top: 20px;"><strong>✅ Follow the steps in this notebook carefully and in the correct order.</strong></p>
  <p style="font-size: 15px;">🚀 You’re all set. Let’s get started!</p>
</div>
'''))


In [5]:
pip install pandas

Note: you may need to restart the kernel to use updated packages.


# <font color="red"><b>✅  CONVERTING and checking DATA FROM .json TO .csv FORMAT </b></font>

In [25]:
import json
import pandas as pd
from IPython.display import display
import ipywidgets as widgets
import io
import os

# Create and display the upload widget
upload = widgets.FileUpload(accept='.csv,.json', multiple=False)
display(upload)

# Define the upload callback
def on_upload_change(change):
    global history  
    
    if not upload.value:
        print(" No file uploaded.")
        return

    # Extract uploaded file
    uploaded_file = next(iter(upload.value.values()))
    filename = uploaded_file['metadata']['name']
    content = uploaded_file['content']
    extension = os.path.splitext(filename)[1].lower()

    # Automatically determine output filename
    base_name = os.path.splitext(filename)[0]
    output_csv_path = base_name + "_processed.csv"

    # Process JSON or CSV
    if extension == '.json':
        data = json.load(io.BytesIO(content))
        history_data = [entry["printHistory"] for entry in data if "printHistory" in entry]
        history = pd.json_normalize(history_data)

    elif extension == '.csv':
        history = pd.read_csv(io.BytesIO(content))
        if "printerName" not in history.columns:
            raise ValueError("CSV must have a 'printerName' column.")

    else:
        raise ValueError("Unsupported file type.")

    # Save the processed CSV
    history.to_csv(output_csv_path, index=False, encoding="utf-8")
    print(f" File saved as: {output_csv_path}")
    history.head()

# Bind the handler to the upload widget
upload.observe(on_upload_change, names='value')


FileUpload(value={}, accept='.csv,.json', description='Upload')

historyIndex                 printerID printerName  success     reason  \
0             0  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   
1             1  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   
2             2  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   
3             3  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   
4             4  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   

                     fileName                    filePath  \
0  CE3_Artem Apfel Gold.gcode  CE3_Artem Apfel Gold.gcode   
1      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode   
2      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode   
3      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode   
4      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode   

                    startDate                     endDate thumbnail  ...  \
0  Fri Dec 30 2022 - 20:27:00  Fri Dec 30 2022 - 20:27:18            ...   
1  Mon Jan 02 2023 - 11:30:34  Mon Jan 02 2023 - 11:32:30            ...   
2  Mon Jan 02 2023 - 11:38:33  Mon Jan 02 2023 - 11:42:42            ...   
3  Mon Jan 02 2023 - 11:49:40  Mon Jan 02 2023 - 12:06:06            ...   
4  Mon Jan 02 2023 - 12:24:14  Mon Jan 02 2023 - 12:29:39            ...   

   job.estimatedPrintTime job.averagePrintTime job.lastPrintTime  \
0             4712.663557                  NaN               NaN   
1             2757.763511                  NaN               NaN   
2             2757.763511                  NaN               NaN   
3             2757.763511                  NaN               NaN   
4             2757.763511                  NaN               NaN   

  job.filament.tool0.length job.filament.tool0.volume job.user  resends.count  \
0                3245.41067                       0.0      Sam              0   
1                1788.25864                       0.0      Sam              0   
2                1788.25864                       0.0      Sam              0   
3                1788.25864                       0.0      Sam              0   
4                1788.25864                       0.0      Sam              0   

   resends.transmitted  resends.ratio  job.filament  
0                   12              0           NaN  
1                 1551              0           NaN  
2                 3082              0           NaN  
3                 8701              0           NaN  
4                10292              0           NaN  

[5 rows x 38 columns]

In [27]:
def find_column(cols, keyword):
    for col in cols:
        if keyword.lower() in col.lower():
            return col
    return None

start_col = find_column(history.columns, 'start')
if start_col:
    history.rename(columns={start_col: 'startDate'}, inplace=True)
    end_col = find_column(history.columns, 'end')
if start_col:
    history.rename(columns={end_col: 'endDate'}, inplace=True)


# <font color="red"><b>🧾🔎 CHECK & VALIDATE HISTORY(LAB DATA) VARIABLE NAMES AND DATA TYPES</b></font>


Before any data processing, it's important to understand the structure of the dataset:

- 🧩 View all **column names** in the dataset.
- 🔠 Check each column’s **data type** to identify numerical, categorical, or object types.
- ✅ Helps ensure the data types are appropriate for analysis or modeling steps.

> 📌 Use this step to detect any potential issues like incorrect data formats or unexpected columns.


In [28]:
history.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 217 entries, 0 to 216
Data columns (total 38 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   historyIndex                   217 non-null    int64  
 1   printerID                      217 non-null    object 
 2   printerName                    217 non-null    object 
 3   success                        217 non-null    bool   
 4   reason                         85 non-null     object 
 5   fileName                       217 non-null    object 
 6   filePath                       217 non-null    object 
 7   startDate                      217 non-null    object 
 8   endDate                        217 non-null    object 
 9   thumbnail                      217 non-null    object 
 10  printTime                      217 non-null    int64  
 11  filamentSelection              217 non-null    object 
 12  previousFilamentSelection      217 non-null    obj

# <font color="red"><b>🧾🔎 LET'S GO TO CONVERT ERROR DATA</b></font>

In [14]:
# import json
# import pandas as pd
# import os
# from datetime import datetime
# from IPython.display import display, HTML
#
# # 1) File paths
# json_file_path     = "/content/drive/Shareddrives/PRAEDICTIO/Data/Gwindi_Data/Raw_Data/Gwindi_errorlogs.json"
# processed_data_dir = "/content/drive/Shareddrives/PRAEDICTIO/Data/Gwindi_Data/Processed_Data"
#
# # 2) Dynamic CSV naming
# today_stamp    = datetime.now().strftime("%Y%m%d")
# csv_filename   = f"{today_stamp}_Error.csv"
# csv_file_path  = os.path.join(processed_data_dir, csv_filename)
#
# # 3) Load & normalize JSON
# with open(json_file_path, "r", encoding="utf-8") as f:
#     data = json.load(f)
# error_logs = [e["errorLog"] for e in data if "errorLog" in e]
#
# if error_logs:
#     error = pd.json_normalize(error_logs)
#     # 4) Save to CSV
#     error.to_csv(csv_file_path, index=False, encoding="utf-8")
#
#     # 5) Reload from CSV (this is now safe)
#     error = pd.read_csv(csv_file_path, encoding="utf-8")
#
#     # 6) Compute directories for links
#     json_dir = os.path.dirname(json_file_path)
#     csv_dir  = os.path.dirname(csv_file_path)
#
#     # 7) Styled confirmation box with directory links
#     conversion_time = datetime.now().strftime("%Y-%m-%d %H:%M:%S")
#     json_file       = os.path.basename(json_file_path)
#     csv_file        = os.path.basename(csv_file_path)
#
#     display(HTML(f"""
#     <div style="border:2px solid #D32F2F;
#                 background-color:#FFEBEE;
#                 border-radius:5px;
#                 padding:20px;
#                 font-family:Arial, sans-serif;">
#
#       <h2 style="color:#388E3C;
#                  font-weight:bold;
#                  margin:0 0 10px;
#                  text-align:center;
#                  font-size:32px;">
#         🔄 <strong>CONVERTED {json_file} → {csv_file} ✅</strong>
#       </h2>
#
#       <p style="margin:8px 0; font-size:15px;">
#         📅 <strong>Conversion & Reload Time:</strong> {conversion_time}
#       </p>
#
#       <p style="margin:4px 0; font-size:15px;">
#         📂 <strong>Source JSON Directory:</strong>
#         <a href="file://{json_dir}" target="_blank" style="color:#1976D2; text-decoration:none;">
#           {json_dir}
#         </a>
#       </p>
#
#       <p style="margin:4px 0; font-size:15px;">
#         📂 <strong>Processed CSV Directory:</strong>
#         <a href="file://{csv_dir}" target="_blank" style="color:#1976D2; text-decoration:none;">
#           {csv_dir}
#         </a>
#       </p>
#
#       <p style="margin-top:12px;
#                 font-size:14px;
#                 color:#424242;">
#         The <code>error</code> DataFrame was extracted from <strong>{json_file}</strong>,
#         exported to <strong>{csv_file}</strong>, then reloaded for verification.
#       </p>
#
#     </div>
#     """))
# else:
#     display(HTML(f"""
#     <div style="border:2px solid #D32F2F;
#                 background-color:#FFF3E0;
#                 border-radius:5px;
#                 padding:20px;
#                 font-family:Arial, sans-serif;
#                 text-align:center;">
#       <h2 style="color:#D32F2F; font-size:28px; font-weight:bold;">
#         ❗ No error logs found in <code>{os.path.basename(json_file_path)}</code>
#       </h2>
#       <p style="font-size:16px; color:#424242;">
#         The source JSON file is empty or contains no <code>errorLog</code> entries.<br>
#         No CSV was generated.
#       </p>
#     </div>
#     """))


# <font color="red"><b>ℹ️ DISPLAYING ERROR DATAFRAME INFO</b></font>

This command executes **<code>error.info()</code>** to provide a concise summary of the <code>error</code> DataFrame,  
showing column data types, non-null counts, and overall memory usage.  
Use this overview to inspect the structure and completeness of your error logs dataset.


In [ ]:
#error.info()

# <font color="red"><b>ℹ️ STEP-1 : CLEANING HISTORY(LAB) DATA</b></font>

# <font color="red"><b>🔧 CONFIGURING DISPLAY OPTIONS FOR DATAFRAME</b></font>

As part of data visualization customization:

🛠️ **Set display options for the DataFrame**:
- **`display.max_columns`**: Configured to **None**, ensuring that **all columns** are shown in the output without truncation.
- **`display.max_rows`**: Set to **None**, allowing **all rows** to be displayed, even if the dataset is large.
- **`display.float_format`**: Specified a formatting option to **round floating-point numbers to 2 decimal places**, ensuring cleaner, more readable numerical data.

🧼 **This configuration enhances the display of the DataFrame**, enabling the user to view the complete data without any truncation, with proper formatting for numeric values, making it easier to analyze the dataset.


In [15]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.options.display.float_format = '{:.2f}'.format
history.head()

historyIndex                 printerID printerName  success     reason  \
0             0  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   
1             1  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   
2             2  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   
3             3  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   
4             4  63af118fd41d203cfc2d5193  Creality 1    False  cancelled   

                     fileName                    filePath  \
0  CE3_Artem Apfel Gold.gcode  CE3_Artem Apfel Gold.gcode   
1      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode   
2      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode   
3      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode   
4      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode   

                    startDate                     endDate thumbnail  \
0  Fri Dec 30 2022 - 20:27:00  Fri Dec 30 2022 - 20:27:18             
1  Mon Jan 02 2023 - 11:30:34  Mon Jan 02 2023 - 11:32:30             
2  Mon Jan 02 2023 - 11:38:33  Mon Jan 02 2023 - 11:42:42             
3  Mon Jan 02 2023 - 11:49:40  Mon Jan 02 2023 - 12:06:06             
4  Mon Jan 02 2023 - 12:24:14  Mon Jan 02 2023 - 12:29:39             

   printTime filamentSelection previousFilamentSelection notes snapshot  \
0         18                []                        []                  
1        117                []                        []                  
2        248                []                        []                  
3        985                []                        []                  
4        326                []                        []                  

  timelapse  costSettings.powerConsumption  costSettings.electricityCosts  \
0                                     0.50                           0.15   
1                                     0.50                           0.15   
2                                     0.50                           0.15   
3                                     0.50                           0.15   
4                                     0.50                           0.15   

   costSettings.purchasePrice  costSettings.estimateLifespan  \
0                         500                          43800   
1                         500                          43800   
2                         500                          43800   
3                         500                          43800   
4                         500                          43800   

   costSettings.maintenanceCosts               job.file.name  \
0                           0.25  CE3_Artem Apfel Gold.gcode   
1                           0.25      CE3_Ivanna Blume.gcode   
2                           0.25      CE3_Ivanna Blume.gcode   
3                           0.25      CE3_Ivanna Blume.gcode   
4                           0.25      CE3_Ivanna Blume.gcode   

                job.file.path            job.file.display job.file.origin  \
0  CE3_Artem Apfel Gold.gcode  CE3_Artem Apfel Gold.gcode           local   
1      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode           local   
2      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode           local   
3      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode           local   
4      CE3_Ivanna Blume.gcode      CE3_Ivanna Blume.gcode           local   

   job.file.size  job.file.date      job.file.length  job.estimatedPrintTime  \
0        1144756     1671133332  [3245.410669999999]                 4712.66   
1        1993728     1672655364                  NaN                 2757.76   
2        1993728     1672655364                  NaN                 2757.76   
3        1993728     1672655364                  NaN                 2757.76   
4        1993728     1672655364                  NaN                 2757.76   

   job.averagePrintTime  job.lastPrintTime  job.filament.tool0.length  \
0                   NaN                NaN   

# <font color="red"><b>CONVERTING DATE COLUMNS TO DATETIME FORMAT</b></font>

In [16]:
# Convert the startDate and endDate columns in the history DataFrame to datetime
history["startDate"] = pd.to_datetime(history["startDate"], errors="coerce")
history["endDate"]   = pd.to_datetime(history["endDate"],   errors="coerce")
history.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 217 entries, 0 to 216
Data columns (total 38 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   historyIndex                   217 non-null    int64         
 1   printerID                      217 non-null    object        
 2   printerName                    217 non-null    object        
 3   success                        217 non-null    bool          
 4   reason                         85 non-null     object        
 5   fileName                       217 non-null    object        
 6   filePath                       217 non-null    object        
 7   startDate                      217 non-null    datetime64[ns]
 8   endDate                        217 non-null    datetime64[ns]
 9   thumbnail                      217 non-null    object        
 10  printTime                      217 non-null    int64         
 11  filamentSelection  

# <font color="red"><b>🧹🗂️ DROPPED UNNECESSARY COLUMNS</b></font>


To keep the dataset clean and focused, unnecessary or irrelevant columns have been removed.

> 🧼 This helps simplify analysis, reduce noise, and improve model performance.



# <font color="red"><b>🔄 REPLACING A SPECIFIC PRINTER NAME 🖨️</b></font>


As part of targeted data cleaning:

🛠️ **Identified and replaced a specific printer name:**
- **`printerName`** was 'Prusar1'
- **Replaced with 'Prusa1'** to maintain consistency in naming.

🧼 **This step ensures uniformity** across the dataset, eliminating any discrepancies caused by misspellings or variations in naming conventions.

In [17]:
history['printerName'] = history['printerName'].replace('Prusar1', 'Prusa1')

# <font color="red"><b>🧹 REMOVING THE `printerName` = 'Creality 1' RECORD 🖨️</b></font>

As part of targeted data cleaning:

🛠️ **Filtered and removed rows where:**
- **`printerName`** was **'Creality 1'**.

🧼 **This step removes any records associated with the 'Creality 1' printer**, helping to refine the dataset by eliminating unwanted entries.


In [18]:
history = history.drop(history[history['printerName'] == 'Creality 1'].index)
history.head()

historyIndex                 printerID printerName  success reason  \
8              8  63af118fd41d203cfc2d5193      Prusa1    False  error   
9              9  66a632292531d16acc9b398d     Prusa33    False  error   
10            10  66a632772531d16acc9b3a00      Prusa1    False  error   
11            11  66a632772531d16acc9b3a00      Prusa1    False  error   
12            12  66a632772531d16acc9b3a00      Prusa1    False  error   

                                             fileName  \
8   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
9              1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
10                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
11                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
12                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                             filePath           startDate  \
8   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
9              1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode 2024-07-28 14:32:14   
10                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
11                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
12                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   

               endDate thumbnail  printTime filamentSelection  \
8  2023-02-19 12:00:37                  244                []   
9  2024-07-28 14:32:31                   17                []   
10 2024-07-28 14:37:26                  298                []   
11 2024-07-28 14:55:34                 1019                []   
12 2024-07-28 15:17:20                  361                []   

   previousFilamentSelection notes snapshot timelapse  \
8                         []                            
9                         []                            
10                        []                            
11                        []                            
12                        []                            

    costSettings.powerConsumption  costSettings.electricityCosts  \
8                            0.50                           0.15   
9                            0.50                           0.15   
10                           0.50                           0.15   
11                           0.50                           0.15   
12                           0.50                           0.15   

    costSettings.purchasePrice  costSettings.estimateLifespan  \
8                          500                          43800   
9                          500                          43800   
10                         500                          43800   
11                         500                          43800   
12                         500                          43800   

    costSettings.maintenanceCosts  \
8                            0.25   
9                            0.25   
10                           0.25   
11                           0.25   
12                           0.25   

                                        job.file.name  \
8   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
9              1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
10                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
11                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
12                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                        job.file.path  \
8   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
9              1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
10                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
11                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
12                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                     job.file.display job.file.origin  \
8   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...           local   
9              1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode           local   
10                 1xfilled_0.15mm_PLA_MINI_44m.gcode           local   
11                

# <font color="red"><b>🧹 REMOVING MULTIPLE UNNECESSARY COLUMNS IN A SINGLE STEP 🗑️</b></font>

As part of data cleaning:

🛠️ **Dropped multiple columns** in one operation:
- These include columns related to **filament selection, cost settings, job details, file metadata, and other unnecessary information**.

🧼 **This step ensures a cleaner and more focused dataset** by efficiently removing a variety of irrelevant columns all at once, streamlining the analysis process.


In [19]:
history = history.drop(columns=[
    "filamentSelection", "previousFilamentSelection", "costSettings.powerConsumption",
    "costSettings.electricityCosts", "costSettings.purchasePrice", "costSettings.estimateLifespan",
    "costSettings.maintenanceCosts", "job.estimatedPrintTime", "job.averagePrintTime",
    "job.lastPrintTime", "job.filament.tool0.length", "job.filament.tool0.volume", "job.user",
    "resends.count", "resends.transmitted", "resends.ratio", "job.filament", "job.file.name",
    "job.file.path", "job.file.display", "job.file.origin", "job.file.size", "job.file.date",
    "job.file.length", "historyIndex", "thumbnail", "notes", "snapshot", "timelapse"],
    errors='ignore')
history.head()



printerID printerName  success reason  \
8   63af118fd41d203cfc2d5193      Prusa1    False  error   
9   66a632292531d16acc9b398d     Prusa33    False  error   
10  66a632772531d16acc9b3a00      Prusa1    False  error   
11  66a632772531d16acc9b3a00      Prusa1    False  error   
12  66a632772531d16acc9b3a00      Prusa1    False  error   

                                             fileName  \
8   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
9              1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
10                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
11                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
12                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                             filePath           startDate  \
8   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
9              1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode 2024-07-28 14:32:14   
10                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
11                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
12                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   

               endDate  printTime  
8  2023-02-19 12:00:37        244  
9  2024-07-28 14:32:31         17  
10 2024-07-28 14:37:26        298  
11 2024-07-28 14:55:34       1019  
12 2024-07-28 15:17:20        361

# <font color="red"><b>📊 CHECKING DATAFRAME STRUCTURE 🧐</b></font>


As part of data exploration:

🛠️ **Used `history.info()`** to examine the structure of the DataFrame:
- This command provides insights into **the number of entries, column data types, and the count of non-null values**.

🧼 **This step helps verify the integrity and structure of the dataset**, ensuring that columns have been appropriately processed and missing values are accounted for.


In [20]:
history.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 209 entries, 8 to 216
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   printerID    209 non-null    object        
 1   printerName  209 non-null    object        
 2   success      209 non-null    bool          
 3   reason       77 non-null     object        
 4   fileName     209 non-null    object        
 5   filePath     209 non-null    object        
 6   startDate    209 non-null    datetime64[ns]
 7   endDate      209 non-null    datetime64[ns]
 8   printTime    209 non-null    int64         
dtypes: bool(1), datetime64[ns](2), int64(1), object(5)
memory usage: 13.4+ KB


## <font color="#00008B"><b>🔍 IDENTIFYING AND FILTERING DUPLICATE ROWS IN THE `history` DATAFRAME</b></font>

⚠️ **Note**: We already **<font color="red"><b>removed</b></font>** **duplicate values** during preprocessing. This step is just a validation check to ensure that no duplicates remain in the dataset.

As part of data cleaning:

🛠️ **Identified duplicate rows based on specified columns**:  
- The **<mark style="background-color: yellow;">`duplicated_rows`</mark>** variable is used to check for duplicates in the **`history`** DataFrame, considering columns like **<mark style="background-color: yellow;">`'printerName'`</mark>**, **<mark style="background-color: yellow;">`'success'`</mark>**, **<mark style="background-color: yellow;">`'reason'`</mark>**, **<mark style="background-color: yellow;">`'fileName'`</mark>**, **<mark style="background-color: yellow;">`'filePath'`</mark>**, **<mark style="background-color: yellow;">`'startDate'`</mark>**, **<mark style="background-color: yellow;">`'endDate'`</mark>**, and **<mark style="background-color: yellow;">`'printTime'`</mark>**.

🔄 **Stored the duplicate rows in a separate DataFrame**:  
- The **<mark style="background-color: yellow;">`filtered_duplicates`</mark>** DataFrame contains all rows that were identified as duplicates from the **`history`** DataFrame using the **<mark style="background-color: yellow;">`duplicated_rows`</mark>** variable.

📊 **This step helps in identifying and isolating duplicate records**, which can then be analyzed or removed for cleaner, more accurate data.



In [21]:
# Identify duplicate rows based on specified columns
duplicated_rows = history.duplicated(
    subset=["printerName", "success", "reason", "fileName", "filePath", "startDate", "endDate", "printTime"], keep=False
)

# Store the duplicate rows in a separate DataFrame
filtered_duplicates = history.loc[duplicated_rows]


filtered_duplicates

printerID printerName  success     reason  \
52   66a632772531d16acc9b3a00      Prusa1    False      error   
53   66a632772531d16acc9b3a00      Prusa1    False      error   
54   66a632772531d16acc9b3a00      Prusa1     True        NaN   
55   66a632772531d16acc9b3a00      Prusa1     True        NaN   
56   66a632772531d16acc9b3a00      Prusa1     True        NaN   
57   66a632772531d16acc9b3a00      Prusa1     True        NaN   
59   66a632772531d16acc9b3a00      Prusa1     True        NaN   
60   66a632772531d16acc9b3a00      Prusa1     True        NaN   
61   66a632772531d16acc9b3a00      Prusa1     True        NaN   
62   66a632772531d16acc9b3a00      Prusa1     True        NaN   
63   66a632772531d16acc9b3a00      Prusa1     True        NaN   
64   66a632772531d16acc9b3a00      Prusa1     True        NaN   
65   66a632772531d16acc9b3a00      Prusa1     True        NaN   
66   66a632772531d16acc9b3a00      Prusa1     True        NaN   
67   66a632772531d16acc9b3a00      Prusa1     True        NaN   
68   66a632772531d16acc9b3a00      Prusa1     True        NaN   
69   66a632772531d16acc9b3a00      Prusa1     True        NaN   
70   66a632772531d16acc9b3a00      Prusa1     True        NaN   
87   66a632772531d16acc9b3a00      Prusa1     True        NaN   
88   66a632772531d16acc9b3a00      Prusa1     True        NaN   
90   66a632772531d16acc9b3a00      Prusa1    False  cancelled   
91   66a632772531d16acc9b3a00      Prusa1    False  cancelled   
93   66a632772531d16acc9b3a00      Prusa1    False  cancelled   
94   66a632772531d16acc9b3a00      Prusa1    False  cancelled   
95   66a632772531d16acc9b3a00      Prusa1     True        NaN   
96   66a632772531d16acc9b3a00      Prusa1     True        NaN   
97   66a632772531d16acc9b3a00      Prusa1     True        NaN   
98   66a632772531d16acc9b3a00      Prusa1     True        NaN   
99   66a632772531d16acc9b3a00      Prusa1     True        NaN   
100  66a632772531d16acc9b3a00      Prusa1     True        NaN   
101  66a632772531d16acc9b3a00      Prusa1     True        NaN   
102  66a632772531d16acc9b3a00      Prusa1     True        NaN   
103  66a632772531d16acc9b3a00      Prusa1     True        NaN   
104  66a632772531d16acc9b3a00      Prusa1     True        NaN   
105  66a632772531d16acc9b3a00      Prusa1     True        NaN   
106  66a632772531d16acc9b3a00      Prusa1     True        NaN   
114  66a632292531d16acc9b398d     Prusa33     True        NaN   
115  66a632292531d16acc9b398d     Prusa33     True        NaN   
142  66a632772531d16acc9b3a00      Prusa1    False      error   
143  66a632772531d16acc9b3a00      Prusa1    False      error   
144  66a632292531d16acc9b398d     Prusa33    False      error   
145  66a632292531d16acc9b398d     Prusa33    False      error   
147  66a632772531d16acc9b3a00      Prusa1    False      error   
148  66a632772531d16acc9b3a00      Prusa1    False      error   
149  66a632772531d16acc9b3a00      Prusa1    False      error   
150  66a632772531d16acc9b3a00      Prusa1    False      error   
151  66a632772531d16acc9b3a00      Prusa1    False      error   
152  66a632772531d16acc9b3a00      Prusa1    False      error   
153  66a632772531d16acc9b3a00      Prusa1    False      error   
154  66a632772531d16acc9b3a00      Prusa1    False      error   
158  66a632772531d16acc9b3a00      Prusa1    False      error   
159  66a632772531d16acc9b3a00      Prusa1    False      error   
162  66a632772531d16acc9b3a00      Prusa1    False      error   
163  66a632772531d16acc9b3a00      Prusa1    False      error   
183  66a632772531d16acc9b3a00      Prusa1    False      error   
184  66a632772531d16acc9b3a00      Prusa1    False      error   
192  66a632772531d16acc9b3a00      Prusa1     True        NaN   
193  66a632772531d16acc9b3a00      Prusa1     True        NaN   
194  66a632772531d16acc9b3a00      Prusa1     True        NaN   
196  66a632772531d16acc9b3a00      Prusa1     True        NaN   
197  66a632772531d16acc9b3a00      Prusa1     True     

In [22]:
filtered_duplicates.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 69 entries, 52 to 212
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   printerID    69 non-null     object        
 1   printerName  69 non-null     object        
 2   success      69 non-null     bool          
 3   reason       26 non-null     object        
 4   fileName     69 non-null     object        
 5   filePath     69 non-null     object        
 6   startDate    69 non-null     datetime64[ns]
 7   endDate      69 non-null     datetime64[ns]
 8   printTime    69 non-null     int64         
dtypes: bool(1), datetime64[ns](2), int64(1), object(5)
memory usage: 4.9+ KB


## <font color="#00008B"><b>🧹 REMOVING DUPLICATE ROWS FROM THE `history` DATAFRAME</b></font>

⚠️ **Note**: This operation permanently deletes duplicate entries, keeping only the **first** occurrence of each unique record.

As part of data cleaning:

🛠️ **Executed `drop_duplicates()` on the `history` DataFrame** to ensure each record is unique.  
- Duplicates were detected across the columns  
  **<mark style="background-color: yellow;"><b>`'printerName'`</b></mark>**,  
  **<mark style="background-color: yellow;"><b>`'success'`</b></mark>**,  
  **<mark style="background-color: yellow;"><b>`'reason'`</b></mark>**,  
  **<mark style="background-color: yellow;"><b>`'fileName'`</b></mark>**,  
  **<mark style="background-color: yellow;"><b>`'filePath'`</b></mark>**,  
  **<mark style="background-color: yellow;"><b>`'startDate'`</b></mark>**,  
  **<mark style="background-color: yellow;"><b>`'endDate'`</b></mark>**, and  
  **<mark style="background-color: yellow;"><b>`'printTime'`</b></mark>**.

🔄 **Kept only the first occurrence** of each duplicate row (`keep="first"`) and reset the index (`reset_index(drop=True)`), producing an updated, de-duplicated DataFrame.

📊 **Finally, `history.info()` was called** to confirm the new shape and structure of the cleaned dataset, verifying that duplicate rows are no longer present.


In [23]:
# Remove duplicate rows based on specified columns while keeping only the first occurrence
history = history.drop_duplicates(
    subset=["printerName", "success", "reason", "fileName", "filePath", "startDate", "endDate", "printTime"],
    keep="first"
).reset_index(drop=True)

# Display updated dataset info after removing duplicates
history.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 171 entries, 0 to 170
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   printerID    171 non-null    object        
 1   printerName  171 non-null    object        
 2   success      171 non-null    bool          
 3   reason       62 non-null     object        
 4   fileName     171 non-null    object        
 5   filePath     171 non-null    object        
 6   startDate    171 non-null    datetime64[ns]
 7   endDate      171 non-null    datetime64[ns]
 8   printTime    171 non-null    int64         
dtypes: bool(1), datetime64[ns](2), int64(1), object(5)
memory usage: 11.0+ KB


## <font color="#00008B"><b>🔧 UPDATING `'reason'` VALUES BASED ON `'success'` FLAG IN THE `history` DATAFRAME</b></font>

As part of data standardisation:

🛠️ **Re-assigned the `reason` field for rows where the print was successful**:  
- For every record with **<mark style="background-color: yellow;"><b>`success`</b></mark> == 1,** the value in **<mark style="background-color: yellow;"><b>`reason`</b></mark>** is overwritten with the string **`'successful'`**.  
  ```python
  history.loc[history['success'] == 1, 'reason'] = 'successful'


In [24]:
# Update the 'reason' column to 'successful' where 'success' is 1
history.loc[history['success'] == 1, 'reason'] = 'successful'
history

printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1    False       error   
1    66a632292531d16acc9b398d     Prusa33    False       error   
2    66a632772531d16acc9b3a00      Prusa1    False       error   
3    66a632772531d16acc9b3a00      Prusa1    False       error   
4    66a632772531d16acc9b3a00      Prusa1    False       error   
5    66a632772531d16acc9b3a00      Prusa1    False       error   
6    66a632772531d16acc9b3a00      Prusa1    False       error   
7    66a632772531d16acc9b3a00      Prusa1    False       error   
8    66a632772531d16acc9b3a00      Prusa1    False       error   
9    66a632772531d16acc9b3a00      Prusa1     True  successful   
10   66a632772531d16acc9b3a00      Prusa1     True  successful   
11   66a632292531d16acc9b398d     Prusa33     True  successful   
12   66a632292531d16acc9b398d     Prusa33     True  successful   
13   66a632772531d16acc9b3a00      Prusa1     True  successful   
14   66a632292531d16acc9b398d     Prusa33     True  successful   
15   66a632772531d16acc9b3a00      Prusa1     True  successful   
16   66a632772531d16acc9b3a00      Prusa1     True  successful   
17   66a632292531d16acc9b398d     Prusa33    False       error   
18   66a632292531d16acc9b398d     Prusa33    False       error   
19   66a632292531d16acc9b398d     Prusa33     True  successful   
20   66a632772531d16acc9b3a00      Prusa1     True  successful   
21   66a632292531d16acc9b398d     Prusa33     True  successful   
22   66a632292531d16acc9b398d     Prusa33     True  successful   
23   66a632772531d16acc9b3a00      Prusa1     True  successful   
24   66a632292531d16acc9b398d     Prusa33     True  successful   
25   66a632772531d16acc9b3a00      Prusa1     True  successful   
26   66a632292531d16acc9b398d     Prusa33     True  successful   
27   66a632772531d16acc9b3a00      Prusa1     True  successful   
28   66a632772531d16acc9b3a00      Prusa1    False       error   
29   66a632772531d16acc9b3a00      Prusa1     True  successful   
30   66a632292531d16acc9b398d     Prusa33     True  successful   
31   66a632772531d16acc9b3a00      Prusa1    False       error   
32   66a632292531d16acc9b398d     Prusa33    False   cancelled   
33   66a632772531d16acc9b3a00      Prusa1    False       error   
34   66a632772531d16acc9b3a00      Prusa1    False       error   
35   66a632772531d16acc9b3a00      Prusa1     True  successful   
36   66a632292531d16acc9b398d     Prusa33     True  successful   
37   66a632292531d16acc9b398d     Prusa33     True  successful   
38   66a632772531d16acc9b3a00      Prusa1    False       error   
39   66a632772531d16acc9b3a00      Prusa1    False       error   
40   66a632772531d16acc9b3a00      Prusa1     True  successful   
41   66a632292531d16acc9b398d     Prusa33     True  successful   
42   66a632772531d16acc9b3a00      Prusa1    False       error   
43   66a632772531d16acc9b3a00      Prusa1    False       error   
44   66a632772531d16acc9b3a00      Prusa1    False       error   
45   66a632772531d16acc9b3a00      Prusa1     True  successful   
46   66a632772531d16acc9b3a00      Prusa1     True  successful   
47   66a632292531d16acc9b398d     Prusa33     True  successful   
48   66a632772531d16acc9b3a00      Prusa1     True  successful   
49   66a632772531d16acc9b3a00      Prusa1     True  successful   
50   66a632772531d16acc9b3a00      Prusa1     True  successful   
51   66a632772531d16acc9b3a00      Prusa1     True  successful   
52   66a632772531d16acc9b3a00      Prusa1     True  successful   
53   66a632772531d16acc9b3a00      Prusa1     True  successful   
54   66a632772531d16acc9b3a00      Prusa1     True  successful   
55   66a632772531d16acc9b3a00      Prusa1     True  successful   
56   66a632292531d16acc9b398d     Prusa33     True  successful   
57   66a632292531d16acc9b398d     Prusa33     True  successful   
58   66a632772531d16acc9b3a00      Prusa1     True  successful   
59   66a632292531d16acc9b398d     Prusa33     True  successf

# <font color="red"><b>📄 PREVIEWING THE `history` DATAFRAME (FIRST 5 ROWS)</b></font>

As part of data inspection:

👀 Executing **<mark style="background-color: yellow;"><b>history.head()</b></mark>** reveals the first five rows of the cleaned `history` DataFrame.  
This quick preview lets you verify:

- Column names and order  
- Data types and formats (e.g., dates, numeric fields)  
- Recent changes, such as the updated **<mark style="background-color: yellow;"><b>`reason`</b></mark>** values and the absence of duplicate records  

Use this snapshot to confirm that the dataset is ready for subsequent analysis and modelling steps.


In [25]:
history.head()

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1    False  error   
1  66a632292531d16acc9b398d     Prusa33    False  error   
2  66a632772531d16acc9b3a00      Prusa1    False  error   
3  66a632772531d16acc9b3a00      Prusa1    False  error   
4  66a632772531d16acc9b3a00      Prusa1    False  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode 2024-07-28 14:32:14   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   

              endDate  printTime  
0 2023-02-19 12:00:37        244  
1 2024-07-28 14:32:31         17  
2 2024-07-28 14:37:26        298  
3 2024-07-28 14:55:34       1019  
4 2024-07-28 15:17:20        361

## <font color="#00008B"><b>⏱️ CONVERTING `printTime` FROM SECONDS TO MINUTES</b></font>

As part of feature engineering:

🔧 **Scaled the raw print duration**  
- The column **<mark style="background-color: yellow;"><b>`printTime`</b></mark>** is divided by **60** to convert its values from seconds to minutes, ensuring consistency with other time-based metrics.

📊 **Quick verification**  
- Running **<mark style="background-color: yellow;"><b>`history.head()`</b></mark>** immediately after the conversion displays the first five rows so you can confirm that the values now represent minutes.

---

This adjustment makes time-related analyses and visualisations more intuitive and comparable across the dataset.


In [26]:
# Convert printTime from seconds to minutes
history["printTime"] = history["printTime"] / 60
history.head()


printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1    False  error   
1  66a632292531d16acc9b398d     Prusa33    False  error   
2  66a632772531d16acc9b3a00      Prusa1    False  error   
3  66a632772531d16acc9b3a00      Prusa1    False  error   
4  66a632772531d16acc9b3a00      Prusa1    False  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode 2024-07-28 14:32:14   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   

              endDate  printTime  
0 2023-02-19 12:00:37       4.07  
1 2024-07-28 14:32:31       0.28  
2 2024-07-28 14:37:26       4.97  
3 2024-07-28 14:55:34      16.98  
4 2024-07-28 15:17:20       6.02

## <font color="#00008B"><b>🔧 ENCODING `success` AND CREATING `is_error` FLAG</b></font>

As part of data preparation:

1️⃣ **Standardised the <mark style="background-color: yellow;"><b>`success`</b></mark> column**  
&nbsp;&nbsp;• Converted Boolean values to integers: **False → 0** and **True → 1**.

2️⃣ **Generated a new binary error indicator**  
&nbsp;&nbsp;• Added <mark style="background-color: yellow;"><b>`is_error`</b></mark>, where  
&nbsp;&nbsp;&nbsp;&nbsp;- **0** denotes a successful print (**`success` == 1**) and  
&nbsp;&nbsp;&nbsp;&nbsp;- **1** denotes a failed print (**`success` == 0**).

👀 **Quick check**: executing <mark style="background-color: yellow;"><b>`history.head()`</b></mark> confirms the new integer‐encoded **`success`** column and the correctly populated **`is_error`** flag in the first five rows.


In [27]:
# Convert 'success' column: False -> 0, True -> 1
history["success"] = history["success"].astype(int)

# Create 'is_error' column: success = 1 -> is_error = 0, success = 0 -> is_error = 1
history["is_error"] = history["success"].apply(lambda x: 0 if x == 1 else 1)

history.head()


printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
1  66a632292531d16acc9b398d     Prusa33        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode 2024-07-28 14:32:14   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   

              endDate  printTime  is_error  
0 2023-02-19 12:00:37       4.07         1  
1 2024-07-28 14:32:31       0.28         1  
2 2024-07-28 14:37:26       4.97         1  
3 2024-07-28 14:55:34      16.98         1  
4 2024-07-28 15:17:20       6.02         1

# <font color="red"><b>ℹ️ STEP-2 : CLEANING ERROR DATA</b></font>

## <font color="darkblue"><b>✏️ RENAMING 'REASON' COLUMN TO 'REASON_DESCRIPTION'</b></font>

The existing “reason” column in the error DataFrame is being renamed to “reason_description” to provide a clearer, more descriptive label before further analysis.


In [28]:
#if not error.empty and "reason" in error.columns:
   # error.rename(columns={"reason": "reason_description"}, inplace=True)
#display(error.head())

# <font color="red"><b>CONVERTING DATE COLUMNS TO DATETIME FORMAT</b></font>

In [30]:
#if not error.empty:
    #if "startDate" in error.columns:
       # error["startDate"] = pd.to_datetime(error["startDate"], errors="coerce")
   # if "endDate" in error.columns:
      #  error["endDate"] = pd.to_datetime(error["endDate"], errors="coerce")
#else:
   # print("No error data available to convert dates.")


In [31]:
# Specify the columns to drop from the error DataFrame
#columns_to_drop = [
   # "filamentSelection", "previousFilamentSelection", "costSettings.powerConsumption",
   # "costSettings.electricityCosts", "costSettings.purchasePrice", "costSettings.estimateLifespan",
   # "costSettings.maintenanceCosts", "job.estimatedPrintTime", "job.averagePrintTime", "job.lastPrintTime",
   # "job.filament.tool0.length", "job.filament.tool0.volume", "job.user", "resends.count",
   # "resends.transmitted", "resends.ratio", "job.filament",
   # "job.file.name", "job.file.path", "job.file.display", "job.file.origin", "job.file.size",
    #"job.file.date", "job.file.length",
    #"historyIndex", "thumbnail", "notes", "snapshot", "timelapse",
   # "printTime.$numberDouble"
#]

#if not error.empty:
    # Drop specified columns if they exist
   # error = error.drop(columns=columns_to_drop, errors='ignore')
   # display(error.head())
#else:
   # print("No error data available to display or drop columns from.")


## <font color="#00008B"><b>🔍 COUNTING THE NUMBER OF `NaT` (NOT A TIME) VALUES IN `error` DATAFRAME</b></font>

As part of data inspection:

🛠️ **Identifying missing or invalid datetime values**:  
- The **<mark style="background-color: yellow;">`error`</mark>** DataFrame is checked for rows where the **<mark style="background-color: yellow;">`'startDate'`</mark>** column contains missing or invalid datetime values (represented as **`NaT`**).  
- The **<mark style="background-color: yellow;">`isna()`</mark>** method identifies these entries, and **<mark style="background-color: yellow;">`sum()`</mark>** tallies the total number of **`NaT`** values.

📊 **Displaying the count of `NaT` values**:  
- The total count of **`NaT`** rows is output using **<mark style="background-color: yellow;">`print()`</mark>**, offering a quick snapshot of missing datetime entries.

🧼 **This step assesses the extent of missing date–time data** in the **`'startDate'`** column, guiding your next steps in data cleaning or imputation.



In [32]:
#from IPython.display import display, Markdown

#if not error.empty and 'startDate' in error.columns:
   # num_nat_rows = error['startDate'].isna().sum()
   # display(Markdown(f"**Total number of rows with missing or invalid datetime values (NaT) in 'startDate' =** "
                    # f"<font color='red' style='font-size:30px'><b>{num_nat_rows}</b></font>"))
#else:
   # display(Markdown("<font color='orange'><b>No error data or 'startDate' column available.</b></font>"))

## <font color="#00008B"><b>🔄 REPLACING 'Prusar1' WITH 'Prusa1' IN `printerName` COLUMN OF `error` DATAFRAME</b></font>

As part of data cleaning:

🛠️ **Replacing the value 'Prusar1' with 'Prusa1':**  
- The **<mark style="background-color: yellow;">`error`</mark>** DataFrame is updated by replacing occurrences of  
  **<mark style="background-color: yellow;">`'Prusar1'`</mark>** with  
  **<mark style="background-color: yellow;">`'Prusa1'`</mark>**  
  in the **<mark style="background-color: yellow;">`printerName`</mark>** column. This ensures consistency in the dataset by correcting any misspellings.

📊 **This step standardizes printer names**, which is crucial for accurate grouping, analysis, and reporting.  



In [33]:
#if not error.empty and 'printerName' in error.columns:
   # error['printerName'] = error['printerName'].replace('Prusar1', 'Prusa1')
#else:
    #print("No error data available or 'printerName' column not found.")

## <font color="#00008B"><b>🧹 DROPPING UNNECESSARY COLUMNS IN `error` DATAFRAME</b></font>

As part of data cleaning:

🛠️ **Dropped unnecessary columns from `error`:**
- **`"filamentSelection"`, `"previousFilamentSelection"`, `"costSettings.powerConsumption"`, `"costSettings.electricityCosts"`, `"costSettings.purchasePrice"`, `"costSettings.estimateLifespan"`, `"costSettings.maintenanceCosts"`, `"job.estimatedPrintTime"`, `"job.averagePrintTime"`, `"job.lastPrintTime"`, `"job.filament.tool0.length"`, `"job.filament.tool0.volume"`, `"job.user"`, `"resends.count"`, `"resends.transmitted"`, `"resends.ratio"`, `"job.filament"`**  
- **`"job.file.name"`, `"job.file.path"`, `"job.file.display"`, `"job.file.origin"`, `"job.file.size"`, `"job.file.date"`, `"job.file.length"`**  
- **`"historyIndex"`, `"thumbnail"`, `"notes"`, `"snapshot"`, `"timelapse"`**  
- **`"printTime.$numberDouble"`**

📊 **This step removes irrelevant fields** from the `error` DataFrame, decluttering the dataset for focused analysis.

🧼 **Verify the updated structure** by calling `error.head()` to confirm that unwanted columns have been dropped.


In [34]:
# Specify the columns to drop in a single step
#columns_to_drop = [
    #"filamentSelection", "previousFilamentSelection", "costSettings.powerConsumption",
   # "costSettings.electricityCosts", "costSettings.purchasePrice", "costSettings.estimateLifespan",
   # "costSettings.maintenanceCosts", "job.estimatedPrintTime", "job.averagePrintTime", "job.lastPrintTime",
   # "job.filament.tool0.length", "job.filament.tool0.volume", "job.user", "resends.count",
   # "resends.transmitted", "resends.ratio", "job.filament",
   # "job.file.name", "job.file.path", "job.file.display", "job.file.origin", "job.file.size",
   # "job.file.date", "job.file.length",
   # "historyIndex", "thumbnail", "notes", "snapshot", "timelapse",
   # "printTime.$numberDouble"
#]

# Drop the specified columns from the error DataFrame
#error = error.drop(columns=columns_to_drop, errors='ignore')

# Display the first few rows to verify the result
#error.head()


## <font color="darkblue"><b>✨ MISSING VALUES ANALYSIS FOR ERROR DATAFRAME</b></font>


In [35]:
# Calculate null value counts and percentages for the error DataFrame by column
#null_counts = error.isnull().sum()

#print("Null value counts in error DataFrame:")
#null_counts

## <font color="darkblue"><b>✨ REMOVING PRINTER 'Creality 1' </b></font>

In [36]:
#if not error.empty and 'printerName' in error.columns:
    #error = error.drop(error[error['printerName'] == 'Creality 1'].index)
   # display(error.head())
#else:
    #print("No error data available or 'printerName' column not found.")


## <font color="darkblue"><b>✨ CONVERT TO SUCCESS COLUMN AS BOOLEAN </b></font>

In [37]:
#if not error.empty and 'success' in error.columns:
  #  error['success'] = error['success'].astype(int)
#else:
    #print("No error data available or 'success' column not found.")

## <font color="darkblue"><b>✨ IDENTIFY & REMOVE DUPLICATES </b></font>

In [38]:
#subset_cols = ["printerName", "success", "reason_description", "startDate", "endDate"]

#if not error.empty and all(col in error.columns for col in subset_cols):
    #duplicated_rows = error.duplicated(subset=subset_cols, keep=False)
    #filtered_duplicates = error.loc[duplicated_rows]
    #display(filtered_duplicates)
#else:
   # print("No error data available or required columns are missing.")


## <font color="#00008B"><b>🧹 REMOVING DUPLICATE ROWS</b></font>


In [39]:
#subset_cols = ["printerName", "success", "reason_description", "startDate", "endDate"]

#if not error.empty and all(col in error.columns for col in subset_cols):
    #error = error.drop_duplicates(
    #    subset=subset_cols,
      #  keep="first"
    #).reset_index(drop=True)
   # error.info()
#else:
   # print("No error data available or required columns are missing.")


## <font color="#ff0000"><b>🧹 MERGING HISTORY(LAB) DATA AND ERROR DATA</b></font>

In [40]:
# MERGE ONLY IF ERROR HAS DATA
#if not error.empty:
    #history = history.merge(
       # error[["printerID", "printerName", "reason_description", "endDate"]],
        #on=["printerID", "printerName", "endDate"],
       # how="left"
  #  )
#else:
   # print("Error log is empty; skipping merge.")


In [41]:
history

printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1        0       error   
1    66a632292531d16acc9b398d     Prusa33        0       error   
2    66a632772531d16acc9b3a00      Prusa1        0       error   
3    66a632772531d16acc9b3a00      Prusa1        0       error   
4    66a632772531d16acc9b3a00      Prusa1        0       error   
5    66a632772531d16acc9b3a00      Prusa1        0       error   
6    66a632772531d16acc9b3a00      Prusa1        0       error   
7    66a632772531d16acc9b3a00      Prusa1        0       error   
8    66a632772531d16acc9b3a00      Prusa1        0       error   
9    66a632772531d16acc9b3a00      Prusa1        1  successful   
10   66a632772531d16acc9b3a00      Prusa1        1  successful   
11   66a632292531d16acc9b398d     Prusa33        1  successful   
12   66a632292531d16acc9b398d     Prusa33        1  successful   
13   66a632772531d16acc9b3a00      Prusa1        1  successful   
14   66a632292531d16acc9b398d     Prusa33        1  successful   
15   66a632772531d16acc9b3a00      Prusa1        1  successful   
16   66a632772531d16acc9b3a00      Prusa1        1  successful   
17   66a632292531d16acc9b398d     Prusa33        0       error   
18   66a632292531d16acc9b398d     Prusa33        0       error   
19   66a632292531d16acc9b398d     Prusa33        1  successful   
20   66a632772531d16acc9b3a00      Prusa1        1  successful   
21   66a632292531d16acc9b398d     Prusa33        1  successful   
22   66a632292531d16acc9b398d     Prusa33        1  successful   
23   66a632772531d16acc9b3a00      Prusa1        1  successful   
24   66a632292531d16acc9b398d     Prusa33        1  successful   
25   66a632772531d16acc9b3a00      Prusa1        1  successful   
26   66a632292531d16acc9b398d     Prusa33        1  successful   
27   66a632772531d16acc9b3a00      Prusa1        1  successful   
28   66a632772531d16acc9b3a00      Prusa1        0       error   
29   66a632772531d16acc9b3a00      Prusa1        1  successful   
30   66a632292531d16acc9b398d     Prusa33        1  successful   
31   66a632772531d16acc9b3a00      Prusa1        0       error   
32   66a632292531d16acc9b398d     Prusa33        0   cancelled   
33   66a632772531d16acc9b3a00      Prusa1        0       error   
34   66a632772531d16acc9b3a00      Prusa1        0       error   
35   66a632772531d16acc9b3a00      Prusa1        1  successful   
36   66a632292531d16acc9b398d     Prusa33        1  successful   
37   66a632292531d16acc9b398d     Prusa33        1  successful   
38   66a632772531d16acc9b3a00      Prusa1        0       error   
39   66a632772531d16acc9b3a00      Prusa1        0       error   
40   66a632772531d16acc9b3a00      Prusa1        1  successful   
41   66a632292531d16acc9b398d     Prusa33        1  successful   
42   66a632772531d16acc9b3a00      Prusa1        0       error   
43   66a632772531d16acc9b3a00      Prusa1        0       error   
44   66a632772531d16acc9b3a00      Prusa1        0       error   
45   66a632772531d16acc9b3a00      Prusa1        1  successful   
46   66a632772531d16acc9b3a00      Prusa1        1  successful   
47   66a632292531d16acc9b398d     Prusa33        1  successful   
48   66a632772531d16acc9b3a00      Prusa1        1  successful   
49   66a632772531d16acc9b3a00      Prusa1        1  successful   
50   66a632772531d16acc9b3a00      Prusa1        1  successful   
51   66a632772531d16acc9b3a00      Prusa1        1  successful   
52   66a632772531d16acc9b3a00      Prusa1        1  successful   
53   66a632772531d16acc9b3a00      Prusa1        1  successful   
54   66a632772531d16acc9b3a00      Prusa1        1  successful   
55   66a632772531d16acc9b3a00      Prusa1        1  successful   
56   66a632292531d16acc9b398d     Prusa33        1  successful   
57   66a632292531d16acc9b398d     Prusa33        1  successful   
58   66a632772531d16acc9b3a00      Prusa1        1  successful   
59   66a632292531d16acc9b398d     Prusa33        1  successf

# <font color="#ff0000"><b> RUL & FEATURE CALCULATION </b></font>

## <font color="#00008B"><b>📈 CALCULATING `cumulativePrintTime` PER PRINTER</b></font>

As part of feature engineering:

🛠️ **Computed a running total of print time for each printer**  
- Used **`groupby("printerName")`** combined with **`cumsum()`** to create the column  
  **<mark style="background-color: yellow;"><b>`cumulativePrintTime`</b></mark>**, which accumulates the minutes printed by each individual printer over time.

```python
history["cumulativePrintTime"] = (
    history.groupby("printerName")["printTime"].cumsum()
)


In [42]:
import pandas as pd

# Calculate cumulative print time per printerName
history["cumulativePrintTime"] = history.groupby("printerName")["printTime"].cumsum()

# Display the updated DataFrame
history  # Show the first few rows to verify the new column


printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1        0       error   
1    66a632292531d16acc9b398d     Prusa33        0       error   
2    66a632772531d16acc9b3a00      Prusa1        0       error   
3    66a632772531d16acc9b3a00      Prusa1        0       error   
4    66a632772531d16acc9b3a00      Prusa1        0       error   
5    66a632772531d16acc9b3a00      Prusa1        0       error   
6    66a632772531d16acc9b3a00      Prusa1        0       error   
7    66a632772531d16acc9b3a00      Prusa1        0       error   
8    66a632772531d16acc9b3a00      Prusa1        0       error   
9    66a632772531d16acc9b3a00      Prusa1        1  successful   
10   66a632772531d16acc9b3a00      Prusa1        1  successful   
11   66a632292531d16acc9b398d     Prusa33        1  successful   
12   66a632292531d16acc9b398d     Prusa33        1  successful   
13   66a632772531d16acc9b3a00      Prusa1        1  successful   
14   66a632292531d16acc9b398d     Prusa33        1  successful   
15   66a632772531d16acc9b3a00      Prusa1        1  successful   
16   66a632772531d16acc9b3a00      Prusa1        1  successful   
17   66a632292531d16acc9b398d     Prusa33        0       error   
18   66a632292531d16acc9b398d     Prusa33        0       error   
19   66a632292531d16acc9b398d     Prusa33        1  successful   
20   66a632772531d16acc9b3a00      Prusa1        1  successful   
21   66a632292531d16acc9b398d     Prusa33        1  successful   
22   66a632292531d16acc9b398d     Prusa33        1  successful   
23   66a632772531d16acc9b3a00      Prusa1        1  successful   
24   66a632292531d16acc9b398d     Prusa33        1  successful   
25   66a632772531d16acc9b3a00      Prusa1        1  successful   
26   66a632292531d16acc9b398d     Prusa33        1  successful   
27   66a632772531d16acc9b3a00      Prusa1        1  successful   
28   66a632772531d16acc9b3a00      Prusa1        0       error   
29   66a632772531d16acc9b3a00      Prusa1        1  successful   
30   66a632292531d16acc9b398d     Prusa33        1  successful   
31   66a632772531d16acc9b3a00      Prusa1        0       error   
32   66a632292531d16acc9b398d     Prusa33        0   cancelled   
33   66a632772531d16acc9b3a00      Prusa1        0       error   
34   66a632772531d16acc9b3a00      Prusa1        0       error   
35   66a632772531d16acc9b3a00      Prusa1        1  successful   
36   66a632292531d16acc9b398d     Prusa33        1  successful   
37   66a632292531d16acc9b398d     Prusa33        1  successful   
38   66a632772531d16acc9b3a00      Prusa1        0       error   
39   66a632772531d16acc9b3a00      Prusa1        0       error   
40   66a632772531d16acc9b3a00      Prusa1        1  successful   
41   66a632292531d16acc9b398d     Prusa33        1  successful   
42   66a632772531d16acc9b3a00      Prusa1        0       error   
43   66a632772531d16acc9b3a00      Prusa1        0       error   
44   66a632772531d16acc9b3a00      Prusa1        0       error   
45   66a632772531d16acc9b3a00      Prusa1        1  successful   
46   66a632772531d16acc9b3a00      Prusa1        1  successful   
47   66a632292531d16acc9b398d     Prusa33        1  successful   
48   66a632772531d16acc9b3a00      Prusa1        1  successful   
49   66a632772531d16acc9b3a00      Prusa1        1  successful   
50   66a632772531d16acc9b3a00      Prusa1        1  successful   
51   66a632772531d16acc9b3a00      Prusa1        1  successful   
52   66a632772531d16acc9b3a00      Prusa1        1  successful   
53   66a632772531d16acc9b3a00      Prusa1        1  successful   
54   66a632772531d16acc9b3a00      Prusa1        1  successful   
55   66a632772531d16acc9b3a00      Prusa1        1  successful   
56   66a632292531d16acc9b398d     Prusa33        1  successful   
57   66a632292531d16acc9b398d     Prusa33        1  successful   
58   66a632772531d16acc9b3a00      Prusa1        1  successful   
59   66a632292531d16acc9b398d     Prusa33        1  successf

## <font color="#00008B"><b>🧮 CALCULATING TOTAL PRINT TIME PER PRINTER</b></font>

As part of feature engineering:

🛠️ **Aggregated total print minutes for each printer**  
1. Summed **<mark style="background-color: yellow;"><b>`printTime`</b></mark>** for each **<mark style="background-color: yellow;"><b>`printerName`</b></mark>** to obtain a per-printer total.  
2. Broadcast that total back to every record via the new column **<mark style="background-color: yellow;"><b>`totalPrintTime`</b></mark>**, so each row now carries its printer’s lifetime print duration.

📊 **Why this matters**  
- Enables quick comparison of overall workload between printers.  
- Serves as a useful feature for utilisation analysis and predictive modelling.

👀 **Next step**  
- Inspect **`history.head()`** to verify that **`totalPrintTime`** appears and is constant across rows belonging to the same printer.


In [43]:
# Sum the printTime for each printerName
total_print_time_per_printer = history.groupby("printerName")["printTime"].sum()

# Map the total print time back to the original DataFrame
history["totalPrintTime"] = history["printerName"].map(total_print_time_per_printer)


history.head()

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
1  66a632292531d16acc9b398d     Prusa33        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode 2024-07-28 14:32:14   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37       4.07         1                 4.07   
1 2024-07-28 14:32:31       0.28         1                 0.28   
2 2024-07-28 14:37:26       4.97         1                 9.03   
3 2024-07-28 14:55:34      16.98         1                26.02   
4 2024-07-28 15:17:20       6.02         1                32.03   

   totalPrintTime  
0        11082.20  
1         9440.13  
2        11082.20  
3        11082.20  
4        11082.20

## <font color="#00008B"><b>🔢 CALCULATING TOTAL PRINT COUNT PER PRINTER</b></font>

As part of feature engineering:

🛠️ **Computed the number of print jobs for each device**  
1. Tallied rows for every **<mark style="background-color: yellow;"><b>`printerName`</b></mark>**, producing **<mark style="background-color: yellow;"><b>`total_prints_per_printer`</b></mark>**.  
2. Propagated this count back to every record via the new column **<mark style="background-color: yellow;"><b>`total_prints`</b></mark>**, giving each row its printer’s lifetime job total.

📊 **Why this matters**  
- Quickly reveals overall workload distribution across printers.  
- Acts as a valuable input for utilisation metrics and predictive models.

👀 **Next step**  
- Use **`history.head()`** to verify that **`total_prints`** appears and remains constant for all rows associated with the same printer.


In [44]:
import pandas as pd

# Count the number of occurrences (rows) per printerName
total_prints_per_printer = history["printerName"].value_counts()

# Map the total print count back to the original DataFrame
history["total_prints"] = history["printerName"].map(total_prints_per_printer)

# Display the updated DataFrame
history  # This will show the first few rows to verify the new column


printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1        0       error   
1    66a632292531d16acc9b398d     Prusa33        0       error   
2    66a632772531d16acc9b3a00      Prusa1        0       error   
3    66a632772531d16acc9b3a00      Prusa1        0       error   
4    66a632772531d16acc9b3a00      Prusa1        0       error   
5    66a632772531d16acc9b3a00      Prusa1        0       error   
6    66a632772531d16acc9b3a00      Prusa1        0       error   
7    66a632772531d16acc9b3a00      Prusa1        0       error   
8    66a632772531d16acc9b3a00      Prusa1        0       error   
9    66a632772531d16acc9b3a00      Prusa1        1  successful   
10   66a632772531d16acc9b3a00      Prusa1        1  successful   
11   66a632292531d16acc9b398d     Prusa33        1  successful   
12   66a632292531d16acc9b398d     Prusa33        1  successful   
13   66a632772531d16acc9b3a00      Prusa1        1  successful   
14   66a632292531d16acc9b398d     Prusa33        1  successful   
15   66a632772531d16acc9b3a00      Prusa1        1  successful   
16   66a632772531d16acc9b3a00      Prusa1        1  successful   
17   66a632292531d16acc9b398d     Prusa33        0       error   
18   66a632292531d16acc9b398d     Prusa33        0       error   
19   66a632292531d16acc9b398d     Prusa33        1  successful   
20   66a632772531d16acc9b3a00      Prusa1        1  successful   
21   66a632292531d16acc9b398d     Prusa33        1  successful   
22   66a632292531d16acc9b398d     Prusa33        1  successful   
23   66a632772531d16acc9b3a00      Prusa1        1  successful   
24   66a632292531d16acc9b398d     Prusa33        1  successful   
25   66a632772531d16acc9b3a00      Prusa1        1  successful   
26   66a632292531d16acc9b398d     Prusa33        1  successful   
27   66a632772531d16acc9b3a00      Prusa1        1  successful   
28   66a632772531d16acc9b3a00      Prusa1        0       error   
29   66a632772531d16acc9b3a00      Prusa1        1  successful   
30   66a632292531d16acc9b398d     Prusa33        1  successful   
31   66a632772531d16acc9b3a00      Prusa1        0       error   
32   66a632292531d16acc9b398d     Prusa33        0   cancelled   
33   66a632772531d16acc9b3a00      Prusa1        0       error   
34   66a632772531d16acc9b3a00      Prusa1        0       error   
35   66a632772531d16acc9b3a00      Prusa1        1  successful   
36   66a632292531d16acc9b398d     Prusa33        1  successful   
37   66a632292531d16acc9b398d     Prusa33        1  successful   
38   66a632772531d16acc9b3a00      Prusa1        0       error   
39   66a632772531d16acc9b3a00      Prusa1        0       error   
40   66a632772531d16acc9b3a00      Prusa1        1  successful   
41   66a632292531d16acc9b398d     Prusa33        1  successful   
42   66a632772531d16acc9b3a00      Prusa1        0       error   
43   66a632772531d16acc9b3a00      Prusa1        0       error   
44   66a632772531d16acc9b3a00      Prusa1        0       error   
45   66a632772531d16acc9b3a00      Prusa1        1  successful   
46   66a632772531d16acc9b3a00      Prusa1        1  successful   
47   66a632292531d16acc9b398d     Prusa33        1  successful   
48   66a632772531d16acc9b3a00      Prusa1        1  successful   
49   66a632772531d16acc9b3a00      Prusa1        1  successful   
50   66a632772531d16acc9b3a00      Prusa1        1  successful   
51   66a632772531d16acc9b3a00      Prusa1        1  successful   
52   66a632772531d16acc9b3a00      Prusa1        1  successful   
53   66a632772531d16acc9b3a00      Prusa1        1  successful   
54   66a632772531d16acc9b3a00      Prusa1        1  successful   
55   66a632772531d16acc9b3a00      Prusa1        1  successful   
56   66a632292531d16acc9b398d     Prusa33        1  successful   
57   66a632292531d16acc9b398d     Prusa33        1  successful   
58   66a632772531d16acc9b3a00      Prusa1        1  successful   
59   66a632292531d16acc9b398d     Prusa33        1  successf

## <font color="#00008B"><b>🏆 CALCULATING TOTAL SUCCESSFUL PRINTS PER PRINTER</b></font>

As part of feature engineering:

🛠️ **Counted successful jobs for each device**  
1. Filtered rows where **<mark style="background-color: yellow;"><b>`success`</b></mark> == 1** and tallied them per **<mark style="background-color: yellow;"><b>`printerName`</b></mark>**, yielding **<mark style="background-color: yellow;"><b>`total_success_per_printer`</b></mark>**.  
2. Broadcast this count to every record via the new column **<mark style="background-color: yellow;"><b>`total_success`</b></mark>** so each row now shows its printer’s cumulative number of successful prints.  
3. Replaced any missing values with **0** for printers that have yet to register a successful job.

📊 **Why this matters**  
- Enables quick comparison of reliability across printers.  
- Serves as a key feature for performance dashboards and predictive maintenance models.

👀 **Next step**  
- Preview **`history.head()`** to confirm that **`total_success`** appears and is correctly populated for each printer.


In [45]:
import pandas as pd

# Count the number of successful prints per printerName
total_success_per_printer = history[history["success"] == 1]["printerName"].value_counts()

# Map the total success count back to the original DataFrame
history["total_success"] = history["printerName"].map(total_success_per_printer)

# Fill NaN values with 0 (in case some printers have no successful prints)
history["total_success"] = history["total_success"].fillna(0).astype(int)

# Display the updated DataFrame
history  # Show the first few rows to verify the new column


printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1        0       error   
1    66a632292531d16acc9b398d     Prusa33        0       error   
2    66a632772531d16acc9b3a00      Prusa1        0       error   
3    66a632772531d16acc9b3a00      Prusa1        0       error   
4    66a632772531d16acc9b3a00      Prusa1        0       error   
5    66a632772531d16acc9b3a00      Prusa1        0       error   
6    66a632772531d16acc9b3a00      Prusa1        0       error   
7    66a632772531d16acc9b3a00      Prusa1        0       error   
8    66a632772531d16acc9b3a00      Prusa1        0       error   
9    66a632772531d16acc9b3a00      Prusa1        1  successful   
10   66a632772531d16acc9b3a00      Prusa1        1  successful   
11   66a632292531d16acc9b398d     Prusa33        1  successful   
12   66a632292531d16acc9b398d     Prusa33        1  successful   
13   66a632772531d16acc9b3a00      Prusa1        1  successful   
14   66a632292531d16acc9b398d     Prusa33        1  successful   
15   66a632772531d16acc9b3a00      Prusa1        1  successful   
16   66a632772531d16acc9b3a00      Prusa1        1  successful   
17   66a632292531d16acc9b398d     Prusa33        0       error   
18   66a632292531d16acc9b398d     Prusa33        0       error   
19   66a632292531d16acc9b398d     Prusa33        1  successful   
20   66a632772531d16acc9b3a00      Prusa1        1  successful   
21   66a632292531d16acc9b398d     Prusa33        1  successful   
22   66a632292531d16acc9b398d     Prusa33        1  successful   
23   66a632772531d16acc9b3a00      Prusa1        1  successful   
24   66a632292531d16acc9b398d     Prusa33        1  successful   
25   66a632772531d16acc9b3a00      Prusa1        1  successful   
26   66a632292531d16acc9b398d     Prusa33        1  successful   
27   66a632772531d16acc9b3a00      Prusa1        1  successful   
28   66a632772531d16acc9b3a00      Prusa1        0       error   
29   66a632772531d16acc9b3a00      Prusa1        1  successful   
30   66a632292531d16acc9b398d     Prusa33        1  successful   
31   66a632772531d16acc9b3a00      Prusa1        0       error   
32   66a632292531d16acc9b398d     Prusa33        0   cancelled   
33   66a632772531d16acc9b3a00      Prusa1        0       error   
34   66a632772531d16acc9b3a00      Prusa1        0       error   
35   66a632772531d16acc9b3a00      Prusa1        1  successful   
36   66a632292531d16acc9b398d     Prusa33        1  successful   
37   66a632292531d16acc9b398d     Prusa33        1  successful   
38   66a632772531d16acc9b3a00      Prusa1        0       error   
39   66a632772531d16acc9b3a00      Prusa1        0       error   
40   66a632772531d16acc9b3a00      Prusa1        1  successful   
41   66a632292531d16acc9b398d     Prusa33        1  successful   
42   66a632772531d16acc9b3a00      Prusa1        0       error   
43   66a632772531d16acc9b3a00      Prusa1        0       error   
44   66a632772531d16acc9b3a00      Prusa1        0       error   
45   66a632772531d16acc9b3a00      Prusa1        1  successful   
46   66a632772531d16acc9b3a00      Prusa1        1  successful   
47   66a632292531d16acc9b398d     Prusa33        1  successful   
48   66a632772531d16acc9b3a00      Prusa1        1  successful   
49   66a632772531d16acc9b3a00      Prusa1        1  successful   
50   66a632772531d16acc9b3a00      Prusa1        1  successful   
51   66a632772531d16acc9b3a00      Prusa1        1  successful   
52   66a632772531d16acc9b3a00      Prusa1        1  successful   
53   66a632772531d16acc9b3a00      Prusa1        1  successful   
54   66a632772531d16acc9b3a00      Prusa1        1  successful   
55   66a632772531d16acc9b3a00      Prusa1        1  successful   
56   66a632292531d16acc9b398d     Prusa33        1  successful   
57   66a632292531d16acc9b398d     Prusa33        1  successful   
58   66a632772531d16acc9b3a00      Prusa1        1  successful   
59   66a632292531d16acc9b398d     Prusa33        1  successf

## <font color="#00008B"><b>🚨 TRACKING CUMULATIVE ERROR COUNT PER PRINTER</b></font>

As part of feature engineering:

🛠️ **Converted the error flag to integers and accumulated errors**  
1. Ensured **<mark style="background-color: yellow;"><b>`is_error`</b></mark>** is integer-typed (0 = no error, 1 = error).  
2. Computed a running total of errors for each **<mark style="background-color: yellow;"><b>`printerName`</b></mark>** using **`groupby`** + **`cumsum()`**, storing the result in the new column **<mark style="background-color: yellow;"><b>`ErrorCountSoFar`</b></mark>**.

📊 **Why this matters**  
- Provides an at-a-glance measure of how many errors each printer has encountered over time.  
- Useful for reliability analysis and scheduling proactive maintenance.

👀 **Next step**  
- Execute **`history.head()`** to verify that **`ErrorCountSoFar`** is increasing sequentially for each printer as expected.


In [46]:
history["is_error"] = history["is_error"].astype(int)
history["ErrorCountSoFar"] = history.groupby("printerName")["is_error"].cumsum()
history.head()

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
1  66a632292531d16acc9b398d     Prusa33        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode 2024-07-28 14:32:14   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37       4.07         1                 4.07   
1 2024-07-28 14:32:31       0.28         1                 0.28   
2 2024-07-28 14:37:26       4.97         1                 9.03   
3 2024-07-28 14:55:34      16.98         1                26.02   
4 2024-07-28 15:17:20       6.02         1                32.03   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  
0        11082.20           112             64                1  
1         9440.13            59             45                1  
2        11082.20           112             64                2  
3        11082.20           112             64                3  
4        11082.20           112             64                4

## <font color="#00008B"><b>📉 CALCULATING CUMULATIVE FAILURES PER PRINTER</b></font>

As part of feature engineering:

🛠️ **Derived each printer’s cumulative failure count**  
- Created **<mark style="background-color: yellow;"><b>`CumFailure`</b></mark>** by subtracting total successful jobs from total print jobs for every **<mark style="background-color: yellow;"><b>`printerName`</b></mark>**:  
  **<mark style="background-color: yellow;"><b>`total_prints` − `total_success` = `CumFailure`</b></mark>**.

📊 **Why this matters**  
- Quantifies how many prints did **not** succeed for each printer, giving a direct measure of failure frequency.  
- Supports reliability dashboards and root-cause investigations.

👀 **Next step**  
- View **`history.head()`** to confirm that the new **`CumFailure`** column appears and equals the difference between **`total_prints`** and **`total_success`** for each row.


In [47]:
history["CumFailure"] = history["total_prints"] - history["total_success"]
history.head()

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
1  66a632292531d16acc9b398d     Prusa33        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode 2024-07-28 14:32:14   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37       4.07         1                 4.07   
1 2024-07-28 14:32:31       0.28         1                 0.28   
2 2024-07-28 14:37:26       4.97         1                 9.03   
3 2024-07-28 14:55:34      16.98         1                26.02   
4 2024-07-28 15:17:20       6.02         1                32.03   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  
0        11082.20           112             64                1          48  
1         9440.13            59             45                1          14  
2        11082.20           112             64                2          48  
3        11082.20           112             64                3          48  
4        11082.20           112             64                4          48

## <font color="#00008B"><b>📆 GROUPING RECORDS BY PRINTER AND CALENDAR DATE</b></font>

As part of temporal analysis:

🛠️ **Prepared a daily-level view of each printer’s activity**  
1. Converted **<mark style="background-color: yellow;"><b>`endDate`</b></mark>** to true `datetime` and derived a pure-date column **<mark style="background-color: yellow;"><b>`date`</b></mark>** (time removed).  
2. Grouped the dataset by **<mark style="background-color: yellow;"><b>`printerName`</b></mark>** and **<mark style="background-color: yellow;"><b>`date`</b></mark>**, preserving all original rows within each daily group.  
3. Assembled the groups into **`result`**, a flattened DataFrame ready for inspection or further aggregation.

📊 **Why this matters**  
- Facilitates day-by-day comparisons of key metrics (e.g., uptime, print volume) per printer.  
- Provides a convenient foundation for daily dashboards, utilisation calculations, or time-series forecasting.

👀 **Preview**  
- The first 10 rows printed from **`result.head(10)`** confirm that each record now carries its printer identifier and the corresponding calendar date, grouped appropriately.


In [48]:
import pandas as pd

# Ensure 'endDate' is datetime
history['endDate'] = pd.to_datetime(history['endDate'])

# Extract date (without time)
history['date'] = history['endDate'].dt.date

# Group by printerName and date
grouped = history.groupby(['printerName', 'date'])

# Convert groups to a DataFrame for display
result = grouped.apply(lambda x: x).reset_index(drop=True)

# Display the table (first 10 rows)
result.head(10)

printerID printerName  success      reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0       error   
1  66a632292531d16acc9b398d     Prusa33        0       error   
2  66a632772531d16acc9b3a00      Prusa1        0       error   
3  66a632772531d16acc9b3a00      Prusa1        0       error   
4  66a632772531d16acc9b3a00      Prusa1        0       error   
5  66a632772531d16acc9b3a00      Prusa1        0       error   
6  66a632772531d16acc9b3a00      Prusa1        0       error   
7  66a632772531d16acc9b3a00      Prusa1        0       error   
8  66a632772531d16acc9b3a00      Prusa1        0       error   
9  66a632772531d16acc9b3a00      Prusa1        1  successful   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
6                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
7                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
8             aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode   
9             aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
1             1.5xfilled_0.15mm_PLA_MINI_1h45m.gcode 2024-07-28 14:32:14   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   
6                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:35:52   
7                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:38:03   
8             aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode 2024-07-29 18:44:28   
9             aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode 2024-07-29 20:02:19   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37       4.07         1                 4.07   
1 2024-07-28 14:32:31       0.28         1                 0.28   
2 2024-07-28 14:37:26       4.97         1                 9.03   
3 2024-07-28 14:55:34      16.98         1                26.02   
4 2024-07-28 15:17:20       6.02         1                32.03   
5 2024-07-28 15:32:44       0.20         1                32.23   
6 2024-07-28 15:36:46       0.90         1                33.13   
7 2024-07-28 15:45:26       7.38         1                40.52   
8 2024-07-29 20:01:33      77.08         1               117.60   
9 2024-07-29 22:47:57     165.63         0               283.23   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  \
0        11082.20           112             64                1          48   
1         9440.13            59             45                1          14   
2        11082.20           112             64                2          48   
3        11082.20           112             64                3          48   
4        11082.20           112             64                4          48   
5        11082.20           112             64                5          48   
6        11082.20           112             64                6          48   
7        11082.20           112             64                7          48   
8        11082.20           112             64                8          48   
9        11082.20           112             64                8          48   

         date  
0  2023-02-19  
1  2024-07-28  
2  2024-07-28  
3  2024-07-28  
4  2024-07-28  
5  2024-07-28  
6  2024-07-28  
7  2024-07-28  
8  2024-07-29  
9  2024-07-29

## <font color="#00008B"><b>🔀 SORTING THE `history` DATAFRAME BY PRINTER AND START DATE</b></font>

As part of data preparation:

🛠️ **Ordered records chronologically for each device**  
- Sorted the dataset by **<mark style="background-color: yellow;"><b>`printerName`</b></mark>** and then by **<mark style="background-color: yellow;"><b>`startDate`</b></mark>**, ensuring that every printer’s jobs appear in proper time sequence.

📊 **Why this matters**  
- Guarantees consistent temporal ordering, vital for cumulative calculations (e.g., `cumulativePrintTime`, `ErrorCountSoFar`).  
- Facilitates accurate time-series plots and predictive modelling by removing out-of-order entries.

👀 **Next step**  
- Use **`history.head()`** or **`history.tail()`** to visually confirm that rows for each printer now progress in ascending start-date order.


In [49]:
history = history.sort_values(['printerName', 'startDate'])

## <font color="#00008B"><b>⚙️ COMPUTING MEAN TIME BETWEEN FAILURES (**MTBF**)</b></font>

As part of reliability analysis:

🛠️ **Derived the Mean Time Between Failures for each record**  
- Calculated **<mark style="background-color: yellow;"><b>`MTBF`</b></mark>** as  
  **<mark style="background-color: yellow;"><b>`totalPrintTime` ÷ `CumFailure`</b></mark>**,  
  where:  
  * **<mark style="background-color: yellow;"><b>`totalPrintTime`</b></mark>** is each printer’s lifetime print duration (in minutes), and  
  * **<mark style="background-color: yellow;"><b>`CumFailure`</b></mark>** is the cumulative number of failed jobs to date.

📊 **Why this matters**  
- **MTBF** quantifies average operational time between failures, serving as a key reliability KPI.  
- Higher values indicate more dependable printers, while lower values flag units needing maintenance or deeper investigation.

👀 **Verify**  
- Inspect **`history.head()`** to confirm that the new **`MTBF`** column is present and populated with meaningful, non-infinite values.


In [50]:
history["MTBF"] = history["totalPrintTime"] / history["CumFailure"]
history.head()

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   
5  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37       4.07         1                 4.07   
2 2024-07-28 14:37:26       4.97         1                 9.03   
3 2024-07-28 14:55:34      16.98         1                26.02   
4 2024-07-28 15:17:20       6.02         1                32.03   
5 2024-07-28 15:32:44       0.20         1                32.23   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  \
0        11082.20           112             64                1          48   
2        11082.20           112             64                2          48   
3        11082.20           112             64                3          48   
4        11082.20           112             64                4          48   
5        11082.20           112             64                5          48   

         date   MTBF  
0  2023-02-19 230.88  
2  2024-07-28 230.88  
3  2024-07-28 230.88  
4  2024-07-28 230.88  
5  2024-07-28 230.88

## <font color="#00008B"><b>🛠️ CALCULATING `MTBF_per_Print` FOR EACH PRINTER</b></font>

As part of reliability analysis:

- **Created the metric** **<mark style="background-color: yellow;">`MTBF_per_Print`</mark>** by dividing  
  **<mark style="background-color: yellow;">`cumulativePrintTime`</mark>** (total minutes printed so far) by  
  **<mark style="background-color: yellow;">`ErrorCountSoFar`</mark>** (total errors encountered so far).  
  This yields the **average print-time (in minutes) between consecutive failures** for every printer at each point in time.

📊 **Why this matters**  
- A lower value indicates more frequent failures, signalling a need for maintenance or deeper investigation.  
- A higher value implies better reliability and longer uninterrupted printing periods.

👀 **Next step**  
- Execute **<mark style="background-color: yellow;">`history.head()`</mark>** to verify the new **`MTBF_per_Print`** column and ensure values populate correctly across rows.


In [51]:
history["MTBF_per_Print"] = history["cumulativePrintTime"] / history["ErrorCountSoFar"]
history.head()

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   
5  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37       4.07         1                 4.07   
2 2024-07-28 14:37:26       4.97         1                 9.03   
3 2024-07-28 14:55:34      16.98         1                26.02   
4 2024-07-28 15:17:20       6.02         1                32.03   
5 2024-07-28 15:32:44       0.20         1                32.23   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  \
0        11082.20           112             64                1          48   
2        11082.20           112             64                2          48   
3        11082.20           112             64                3          48   
4        11082.20           112             64                4          48   
5        11082.20           112             64                5          48   

         date   MTBF  MTBF_per_Print  
0  2023-02-19 230.88            4.07  
2  2024-07-28 230.88            4.52  
3  2024-07-28 230.88            8.67  
4  2024-07-28 230.88            8.01  
5  2024-07-28 230.88            6.45

## <font color="#00008B"><b>📉 DERIVING `FailureRate` FROM `MTBF`</b></font>

As part of reliability diagnostics:

- **Calculated the metric** **<mark style="background-color: yellow;">`FailureRate`</mark>** as the reciprocal of  
  **<mark style="background-color: yellow;">`MTBF`</mark>** (Mean Time Between Failures):  
  > **FailureRate = 1 / MTBF**  

📊 **Interpretation**  
- Expresses the **expected number of failures per minute of operation**.  
- A **higher** value signals more frequent failures, whereas a **lower** value indicates greater reliability.

👀 **Next step**  
- Preview **<mark style="background-color: yellow;">`history`</mark>** (e.g., with `history.head()`) to confirm the new **`FailureRate`** column is present and populated correctly for every record.


In [52]:
history["FailureRate"] = 1 / history["MTBF"]
history

printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1        0       error   
2    66a632772531d16acc9b3a00      Prusa1        0       error   
3    66a632772531d16acc9b3a00      Prusa1        0       error   
4    66a632772531d16acc9b3a00      Prusa1        0       error   
5    66a632772531d16acc9b3a00      Prusa1        0       error   
6    66a632772531d16acc9b3a00      Prusa1        0       error   
7    66a632772531d16acc9b3a00      Prusa1        0       error   
8    66a632772531d16acc9b3a00      Prusa1        0       error   
9    66a632772531d16acc9b3a00      Prusa1        1  successful   
10   66a632772531d16acc9b3a00      Prusa1        1  successful   
13   66a632772531d16acc9b3a00      Prusa1        1  successful   
15   66a632772531d16acc9b3a00      Prusa1        1  successful   
16   66a632772531d16acc9b3a00      Prusa1        1  successful   
20   66a632772531d16acc9b3a00      Prusa1        1  successful   
23   66a632772531d16acc9b3a00      Prusa1        1  successful   
25   66a632772531d16acc9b3a00      Prusa1        1  successful   
27   66a632772531d16acc9b3a00      Prusa1        1  successful   
28   66a632772531d16acc9b3a00      Prusa1        0       error   
29   66a632772531d16acc9b3a00      Prusa1        1  successful   
31   66a632772531d16acc9b3a00      Prusa1        0       error   
33   66a632772531d16acc9b3a00      Prusa1        0       error   
34   66a632772531d16acc9b3a00      Prusa1        0       error   
35   66a632772531d16acc9b3a00      Prusa1        1  successful   
38   66a632772531d16acc9b3a00      Prusa1        0       error   
39   66a632772531d16acc9b3a00      Prusa1        0       error   
40   66a632772531d16acc9b3a00      Prusa1        1  successful   
42   66a632772531d16acc9b3a00      Prusa1        0       error   
43   66a632772531d16acc9b3a00      Prusa1        0       error   
44   66a632772531d16acc9b3a00      Prusa1        0       error   
45   66a632772531d16acc9b3a00      Prusa1        1  successful   
46   66a632772531d16acc9b3a00      Prusa1        1  successful   
48   66a632772531d16acc9b3a00      Prusa1        1  successful   
49   66a632772531d16acc9b3a00      Prusa1        1  successful   
50   66a632772531d16acc9b3a00      Prusa1        1  successful   
51   66a632772531d16acc9b3a00      Prusa1        1  successful   
52   66a632772531d16acc9b3a00      Prusa1        1  successful   
53   66a632772531d16acc9b3a00      Prusa1        1  successful   
54   66a632772531d16acc9b3a00      Prusa1        1  successful   
55   66a632772531d16acc9b3a00      Prusa1        1  successful   
58   66a632772531d16acc9b3a00      Prusa1        1  successful   
60   66a632772531d16acc9b3a00      Prusa1        1  successful   
62   66a632772531d16acc9b3a00      Prusa1        1  successful   
64   66a632772531d16acc9b3a00      Prusa1        1  successful   
65   66a632772531d16acc9b3a00      Prusa1        1  successful   
67   66a632772531d16acc9b3a00      Prusa1        0       error   
68   66a632772531d16acc9b3a00      Prusa1        1  successful   
69   66a632772531d16acc9b3a00      Prusa1        1  successful   
70   66a632772531d16acc9b3a00      Prusa1        1  successful   
72   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
74   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
75   66a632772531d16acc9b3a00      Prusa1        1  successful   
76   66a632772531d16acc9b3a00      Prusa1        1  successful   
77   66a632772531d16acc9b3a00      Prusa1        1  successful   
78   66a632772531d16acc9b3a00      Prusa1        1  successful   
79   66a632772531d16acc9b3a00      Prusa1        1  successful   
80   66a632772531d16acc9b3a00      Prusa1        1  successful   
81   66a632772531d16acc9b3a00      Prusa1        1  successful   
82   66a632772531d16acc9b3a00      Prusa1        1  successful   
83   66a632772531d16acc9b3a00      Prusa1        1  successful   
84   66a632772531d16acc9b3a00      Prusa1        1  successf

## <font color="#00008B"><b>📉 CALCULATING <mark style="background-color: yellow;">**`FailureRate_per_Print`**</mark> FROM <mark style="background-color: yellow;">**`MTBF_per_Print`**</mark></b></font>

As part of reliability diagnostics:

- **Formatted numeric output**:  
  `pd.options.display.float_format = '{:.4f}'.format` limits all floating-point values in subsequent displays to **four decimal places**, making tables easier to read and compare.

- **Derived the new metric** <mark style="background-color: yellow;">**`FailureRate_per_Print`**</mark>:  
  \[
  \text{FailureRate\_per\_Print} \;=\; \dfrac{1}{\text{MTBF\_per\_Print}}
  \]  
  where <mark style="background-color: yellow;">**`MTBF_per_Print`**</mark> is the average print-time (in minutes) between consecutive failures for each printer.

📊 **Interpretation**  
- A **higher** <mark style="background-color: yellow;">**`FailureRate_per_Print`**</mark> indicates failures occur more frequently relative to print duration.  
- A **lower** value signals better reliability, with longer average print-times separating failures.

👀 **Next step**  
- Preview the dataset with `history.head()` to confirm that the new column appears and is formatted to four decimal places.


In [53]:
pd.options.display.float_format = '{:.4f}'.format
history["FailureRate_per_Print"] = 1 / history["MTBF_per_Print"]
history.head()


printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   
5  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37     4.0667         1               4.0667   
2 2024-07-28 14:37:26     4.9667         1               9.0333   
3 2024-07-28 14:55:34    16.9833         1              26.0167   
4 2024-07-28 15:17:20     6.0167         1              32.0333   
5 2024-07-28 15:32:44     0.2000         1              32.2333   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  \
0      11082.2000           112             64                1          48   
2      11082.2000           112             64                2          48   
3      11082.2000           112             64                3          48   
4      11082.2000           112             64                4          48   
5      11082.2000           112             64                5          48   

         date     MTBF  MTBF_per_Print  FailureRate  FailureRate_per_Print  
0  2023-02-19 230.8792          4.0667       0.0043                 0.2459  
2  2024-07-28 230.8792          4.5167       0.0043                 0.2214  
3  2024-07-28 230.8792          8.6722       0.0043                 0.1153  
4  2024-07-28 230.8792          8.0083       0.0043                 0.1249  
5  2024-07-28 230.8792          6.4467       0.0043                 0.1551

## <font color="#00008B"><b>✅ CALCULATING <mark style="background-color: yellow;">`SuccessRate`</mark> PER PRINTER</b></font>

As part of performance analysis:

- **Computed the success ratio** by dividing each printer’s cumulative successful jobs  
  <mark style="background-color: yellow;"><b>`total_success`</b></mark> by its cumulative job count  
  <mark style="background-color: yellow;"><b>`total_prints`</b></mark>.

- **Converted the result to a percentage** (× 100) and stored it in the new column  
  <mark style="background-color: yellow;"><b>`SuccessRate`</b></mark>.

📊 **Why this matters**  
- Offers a straightforward reliability KPI: a higher percentage denotes a greater share of successful prints.  
- Facilitates quick comparison of printer performance and supports predictive-maintenance thresholds.

👀 **Quick check**  
- Run `history.head()` to verify that the new **`SuccessRate`** column appears and values are expressed as percentages.


In [54]:
history["SuccessRate"] = history["total_success"] / history["total_prints"]
history["SuccessRate"] = history["SuccessRate"] * 100
history.head()

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   
5  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37     4.0667         1               4.0667   
2 2024-07-28 14:37:26     4.9667         1               9.0333   
3 2024-07-28 14:55:34    16.9833         1              26.0167   
4 2024-07-28 15:17:20     6.0167         1              32.0333   
5 2024-07-28 15:32:44     0.2000         1              32.2333   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  \
0      11082.2000           112             64                1          48   
2      11082.2000           112             64                2          48   
3      11082.2000           112             64                3          48   
4      11082.2000           112             64                4          48   
5      11082.2000           112             64                5          48   

         date     MTBF  MTBF_per_Print  FailureRate  FailureRate_per_Print  \
0  2023-02-19 230.8792          4.0667       0.0043                 0.2459   
2  2024-07-28 230.8792          4.5167       0.0043                 0.2214   
3  2024-07-28 230.8792          8.6722       0.0043                 0.1153   
4  2024-07-28 230.8792          8.0083       0.0043                 0.1249   
5  2024-07-28 230.8792          6.4467       0.0043                 0.1551   

   SuccessRate  
0      57.1429  
2      57.1429  
3      57.1429  
4      57.1429  
5      57.1429

## <font color="#00008B"><b>⏲️ DEFINING <mark style="background-color: yellow;">`TotalOperatingTimeExpected`</mark></b></font>

As part of model preparation:

🛠️ **Assigned a constant benchmark operating time**  
- Set **<mark style="background-color: yellow;"><b>`TotalOperatingTimeExpected`</b></mark>** to **43 800** minutes for every record.  
  This value represents an assumed lifetime operating target (≈ 730 hours) against which actual usage and utilisation rates will later be compared.

📊 **Why this matters**  
- Provides a uniform baseline for calculating KPIs such as utilisation percentage and remaining useful life (RUL).  
- Ensures subsequent metrics that depend on expected operating time are coherent across all printers.

👀 **Next step**  
- Review `history.head()` to confirm the new constant column is present and populated with **43 800** for all rows.


In [55]:
history["TotalOperatingTimeExpected"] = 43800
history.head()

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   
5  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
5                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37     4.0667         1               4.0667   
2 2024-07-28 14:37:26     4.9667         1               9.0333   
3 2024-07-28 14:55:34    16.9833         1              26.0167   
4 2024-07-28 15:17:20     6.0167         1              32.0333   
5 2024-07-28 15:32:44     0.2000         1              32.2333   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  \
0      11082.2000           112             64                1          48   
2      11082.2000           112             64                2          48   
3      11082.2000           112             64                3          48   
4      11082.2000           112             64                4          48   
5      11082.2000           112             64                5          48   

         date     MTBF  MTBF_per_Print  FailureRate  FailureRate_per_Print  \
0  2023-02-19 230.8792          4.0667       0.0043                 0.2459   
2  2024-07-28 230.8792          4.5167       0.0043                 0.2214   
3  2024-07-28 230.8792          8.6722       0.0043                 0.1153   
4  2024-07-28 230.8792          8.0083       0.0043                 0.1249   
5  2024-07-28 230.8792          6.4467       0.0043                 0.1551   

   SuccessRate  TotalOperatingTimeExpected  
0      57.1429                       43800  
2      57.1429                       43800  
3      57.1429                       43800  
4      57.1429                       43800  
5      57.1429                       43800

## <font color="#00008B"><b>📈 ESTIMATING <mark style="background-color: yellow;">`TotalExpectedFailure`</mark></b></font>

As part of reliability forecasting:

🛠️ **Calculated the expected number of failures over the printer’s design lifetime**  
- Divided the benchmark lifetime (**<mark style="background-color: yellow;">`TotalOperatingTimeExpected`</mark>** = 43 800 min) by each record’s mean time between failures per print (**<mark style="background-color: yellow;">`MTBF_per_Print`</mark>**) to derive  
  **<mark style="background-color: yellow;"><b>`TotalExpectedFailure`</b></mark>**.

\[
\text{TotalExpectedFailure} \;=\; \dfrac{\text{TotalOperatingTimeExpected}}{\text{MTBF\_per\_Print}}
\]

📊 **Why this matters**  
- Projects **how many failures a printer is likely to experience** across its expected lifetime.  
- Enables proactive maintenance scheduling and spare-parts planning based on quantitative forecasts.

👀 **Quick check**  
- View `history.head(10)` to verify that **`TotalExpectedFailure`** appears and reflects realistic counts (higher when **`MTBF_per_Print`** is low, lower when reliability is strong).


In [56]:
history["TotalExpectedFailure"] = history["TotalOperatingTimeExpected"] / history["MTBF_per_Print"]
history.head(10)

printerID printerName  success      reason  \
0   63af118fd41d203cfc2d5193      Prusa1        0       error   
2   66a632772531d16acc9b3a00      Prusa1        0       error   
3   66a632772531d16acc9b3a00      Prusa1        0       error   
4   66a632772531d16acc9b3a00      Prusa1        0       error   
5   66a632772531d16acc9b3a00      Prusa1        0       error   
6   66a632772531d16acc9b3a00      Prusa1        0       error   
7   66a632772531d16acc9b3a00      Prusa1        0       error   
8   66a632772531d16acc9b3a00      Prusa1        0       error   
9   66a632772531d16acc9b3a00      Prusa1        1  successful   
10  66a632772531d16acc9b3a00      Prusa1        1  successful   

                                             fileName  \
0   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
2                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
5                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
6                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
7                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
8              aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode   
9              aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode   
10                    Ghost_0.25mm_PLA_MINI_41m.gcode   

                                             filePath           startDate  \
0   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
2                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
5                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   
6                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:35:52   
7                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:38:03   
8              aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode 2024-07-29 18:44:28   
9              aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode 2024-07-29 20:02:19   
10                    Ghost_0.25mm_PLA_MINI_41m.gcode 2024-11-05 14:48:13   

               endDate  printTime  is_error  cumulativePrintTime  \
0  2023-02-19 12:00:37     4.0667         1               4.0667   
2  2024-07-28 14:37:26     4.9667         1               9.0333   
3  2024-07-28 14:55:34    16.9833         1              26.0167   
4  2024-07-28 15:17:20     6.0167         1              32.0333   
5  2024-07-28 15:32:44     0.2000         1              32.2333   
6  2024-07-28 15:36:46     0.9000         1              33.1333   
7  2024-07-28 15:45:26     7.3833         1              40.5167   
8  2024-07-29 20:01:33    77.0833         1             117.6000   
9  2024-07-29 22:47:57   165.6333         0             283.2333   
10 2024-11-05 15:31:39    43.4333         0             326.6667   

    totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  \
0       11082.2000           112             64                1          48   
2       11082.2000           112             64                2          48   
3       11082.2000           112             64                3          48   
4       11082.2000           112             64                4          48   
5       11082.2000           112             64                5          48   
6       11082.2000           112             64                6          48   
7       11082.2000           112             64                7          48   
8       11082.2000           112             64                8          48   
9       11082.2000           112             64                8          48   
10      11082.2000           112             64                8          48   

          date     MTBF  MTBF_per_Print  FailureRate  FailureRate_per_Print  \
0   2023-02-19 230.8792          4.0667       0.0043                 0.2459   
2   2024-07-28 230.8792          4.5167

## <font color="#00008B"><b>🔮 CALCULATING <mark style="background-color: yellow;">`RUL`</mark> — REMAINING USEFUL LIFE</b></font>

As part of predictive-maintenance metrics:

Steps performed:

1. Computed the expected remaining failures for each printer.  
2. Multiplied by average minutes between failures (**`MTBF_per_Print`**) to obtain remaining minutes of operation.  
3. Converted minutes to hours for easier interpretation.  
4. Replaced any *NaN* with **0**, ensuring printers that have already exceeded their expected failures show a zero RUL instead of missing data.

📊 **Why this matters**

- **RUL** indicates **how many operating hours a printer has left** before it reaches its expected failure quota, enabling proactive scheduling of maintenance or part replacement.  
- Integrates cumulative performance (**`ErrorCountSoFar`**) with design expectations (**`TotalExpectedFailure`**) and reliability trends (**`MTBF_per_Print`**).

👀 **Quick check**

- Use `history.head(20)` (already executed) to verify sensible **`RUL`** values:  
  higher for reliable printers with few failures, lower for those nearing their expected failure count.


In [57]:
# RUL=[(Total Expected Failures − Cumulative Failures)/Total Expected Failures​]×MTBF
history["RUL"] = (history["TotalExpectedFailure"] - history["ErrorCountSoFar"]) * history["MTBF_per_Print"]
history["RUL"] = history["RUL"] / 60
history["RUL"].fillna(0, inplace=True)
history.head(20)

printerID printerName  success      reason  \
0   63af118fd41d203cfc2d5193      Prusa1        0       error   
2   66a632772531d16acc9b3a00      Prusa1        0       error   
3   66a632772531d16acc9b3a00      Prusa1        0       error   
4   66a632772531d16acc9b3a00      Prusa1        0       error   
5   66a632772531d16acc9b3a00      Prusa1        0       error   
6   66a632772531d16acc9b3a00      Prusa1        0       error   
7   66a632772531d16acc9b3a00      Prusa1        0       error   
8   66a632772531d16acc9b3a00      Prusa1        0       error   
9   66a632772531d16acc9b3a00      Prusa1        1  successful   
10  66a632772531d16acc9b3a00      Prusa1        1  successful   
13  66a632772531d16acc9b3a00      Prusa1        1  successful   
15  66a632772531d16acc9b3a00      Prusa1        1  successful   
16  66a632772531d16acc9b3a00      Prusa1        1  successful   
20  66a632772531d16acc9b3a00      Prusa1        1  successful   
23  66a632772531d16acc9b3a00      Prusa1        1  successful   
25  66a632772531d16acc9b3a00      Prusa1        1  successful   
27  66a632772531d16acc9b3a00      Prusa1        1  successful   
28  66a632772531d16acc9b3a00      Prusa1        0       error   
29  66a632772531d16acc9b3a00      Prusa1        1  successful   
31  66a632772531d16acc9b3a00      Prusa1        0       error   

                                             fileName  \
0   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
2                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
5                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
6                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
7                  1xfilled_0.15mm_PLA_MINI_44m.gcode   
8              aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode   
9              aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode   
10                    Ghost_0.25mm_PLA_MINI_41m.gcode   
13                    Ghost_0.25mm_PLA_MINI_41m.gcode   
15                    Ghost_0.25mm_PLA_MINI_41m.gcode   
16                    Ghost_0.25mm_PLA_MINI_41m.gcode   
20                    Ghost_0.25mm_PLA_MINI_41m.gcode   
23             Mini_Horse_0.25mm_PLA_MINI_1h54m.gcode   
25             Mini_Horse_0.25mm_PLA_MINI_1h54m.gcode   
27              Bookshelf_0.25mm_PLA_MINI_6h45m.gcode   
28             Mini_Horse_0.25mm_PLA_MINI_1h54m.gcode   
29                    Ghost_0.25mm_PLA_MINI_41m.gcode   
31                    vase_0.25mm_PLA_MINI_5h9m.gcode   

                                             filePath           startDate  \
0   Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ... 2023-02-19 11:56:33   
2                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
3                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
4                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
5                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   
6                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:35:52   
7                  1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:38:03   
8              aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode 2024-07-29 18:44:28   
9              aLLxfilled_0.15mm_PLA_MINI_2h44m.gcode 2024-07-29 20:02:19   
10                    Ghost_0.25mm_PLA_MINI_41m.gcode 2024-11-05 14:48:13   
13                    Ghost_0.25mm_PLA_MINI_41m.gcode 2024-11-06 08:13:39   
15                    Ghost_0.25mm_PLA_MINI_41m.gcode 2024-11-08 16:11:37   
16                    Ghost_0.25mm_PLA_MINI_41m.gcode 2024-11-10 10:28:26   
20                    Ghost_0.25mm_PLA_MINI_41m.gcode 2024-11-11 11:48:07   
23             Mini_Horse_0.25mm_PLA_MINI_1h54m.gcode 2024-11-14 09:13:25   
25             Mini_Horse_0.25mm_PLA_MINI_1h54m.gcode 2024-11-14 11:31:10   
27              Bookshelf_0.25mm_PLA_MINI_6h45m.gcode 2024-11-29 15:34:18   
28             Mini_Horse_0.25mm_PLA_MINI_1h54m.gcode 2024-12-10 11:2

## <font color="#00008B"><b>🔮 CALCULATING <mark style="background-color: yellow;"><b><font color="black">`RUL`</font></b></mark> — REMAINING USEFUL LIFE</b></font>

As part of predictive-maintenance metrics:
 converted from **minutes → hours** (÷ 60).

**Steps performed**

1. Calculated expected remaining failures  
   <mark style="background-color: yellow;"><b><font color="black">`TotalExpectedFailure` − `ErrorCountSoFar`</font></b></mark>.  
2. Multiplied by average minutes between failures  
   <mark style="background-color: yellow;"><b><font color="black">`MTBF_per_Print`</font></b></mark> to obtain remaining **minutes** of operation.  
3. Converted minutes → hours for easier interpretation.  
4. Replaced any *NaN* with **0** so printers that already exceeded expectations show **zero** instead of missing data.

📊 **Why this matters**

- <mark style="background-color: yellow;"><b><font color="black">`RUL`</font></b></mark> tells **how many operating hours a printer has left** before reaching its expected-failure quota, enabling proactive maintenance planning.  
- Integrates cumulative performance  
  (<mark style="background-color: yellow;"><b><font color="black">`ErrorCountSoFar`</font></b></mark>)  
  with design expectations  
  (<mark style="background-color: yellow;"><b><font color="black">`TotalExpectedFailure`</font></b></mark>)  
  and reliability trends  
  (<mark style="background-color: yellow;"><b><font color="black">`MTBF_per_Print`</font></b></mark>).

👀 **Quick check**

Run `history.head(20)` to inspect **<mark style="background-color: yellow;"><b><font color="black">`RUL`</font></b></mark>** values:
- Higher for reliable printers with few failures.  
- Lower where the expected-failure limit is near.


In [59]:
# Ensure datetime format
history['startDate'] = pd.to_datetime(history['startDate'])
history['endDate'] = pd.to_datetime(history['endDate'])

# Extract only the date part
history['print_day'] = history['startDate'].dt.date

# Ensure daily_cumulativePrintTime column exists and is initialized to 0
history['daily_cumulativePrintTime'] = 0.0  # Explicitly setting as float

# Identify the last print job of the day
last_print_per_day = history.groupby('print_day')['endDate'].transform('max') == history['endDate']

# Assign the cumulativePrintTime value only for the last print of the day
history.loc[last_print_per_day, 'daily_cumulativePrintTime'] = history.loc[last_print_per_day, 'cumulativePrintTime'].astype(float)

# Identify the first print of the day and set its daily_cumulativePrintTime to its first printTime
first_print_per_day = history.groupby('print_day')['startDate'].transform('min') == history['startDate']
history.loc[first_print_per_day, 'daily_cumulativePrintTime'] = history.loc[first_print_per_day, 'printTime']

# Drop helper column
history.drop(columns=['print_day'], inplace=True)


## <font color="#00008B"><b>📅 BUILDING DAILY, WEEKLY & MONTHLY PRINT-TIME FEATURES + UTILISATION RATES</b></font>

This cell engineers time-based KPIs for every printer:

1. **Timestamp normalisation**  
   - Converts <mark style="background-color: yellow;"><b><font color="black">`startDate`</font></b></mark> and <mark style="background-color: yellow;"><b><font color="black">`endDate`</font></b></mark> to **`datetime`** objects.  
   - Creates a helper <mark style="background-color: yellow;"><b><font color="black">`print_day`</font></b></mark> (calendar date only).

2. **Daily metrics**  
   - Computes a running sum <mark style="background-color: yellow;"><b><font color="black">`daily_cumulativePrintTime`</font></b></mark> per printer/day.  
   - Stores the day’s total minutes in <mark style="background-color: yellow;"><b><font color="black">`daily_TotalPrintTime`</font></b></mark> on the **last row** of each day; all other rows are set to 0.

3. **Weekly metrics**  
   - Adds <mark style="background-color: yellow;"><b><font color="black">`calendar_week`</font></b></mark> & `year`, then aggregates per ISO-week:  
     - <mark style="background-color: yellow;"><b><font color="black">`weekly_cumulativePrintTime`</font></b></mark>  
     - <mark style="background-color: yellow;"><b><font color="black">`weekly_TotalPrintTime`</font></b></mark> (written once on the week’s final row).

4. **Monthly metrics**  
   - Adds <mark style="background-color: yellow;"><b><font color="black">`month`</font></b></mark> and calculates:  
     - <mark style="background-color: yellow;"><b><font color="black">`monthly_cumulativePrintTime`</font></b></mark>  
     - <mark style="background-color: yellow;"><b><font color="black">`monthly_TotalPrintTime`</font></b></mark> on the month’s last row.

5. **Utilisation-rate KPIs**  
   Using theoretical capacity—**1 440 min/day**, **10 080 min/week**, **43 200 min/month**—computes:  
   - <mark style="background-color: yellow;"><b><font color="black">`daily_utilization_rate`</font></b></mark>  
   - <mark style="background-color: yellow;"><b><font color="black">`weekly_utilization_rate`</font></b></mark>  
   - <mark style="background-color: yellow;"><b><font color="black">`monthly_utilization_rate`</font></b></mark>

6. **Cleanup & ordering**  
   - Drops helper <mark style="background-color: yellow;"><b><font color="black">`print_day`</font></b></mark>.  
   - Sorts by printer and <mark style="background-color: yellow;"><b><font color="black">`startDate`</font></b></mark>, ensuring chronological integrity for downstream models & dashboards.

> These enriched features provide granular insight into printer workload, efficiency trends, and capacity planning across daily, weekly, and monthly horizons.


In [60]:
import pandas as pd

# Ensure datetime format
history['startDate'] = pd.to_datetime(history['startDate'])
history['endDate'] = pd.to_datetime(history['endDate'])

# Extract only the date part
history['print_day'] = history['startDate'].dt.date

# Initialize daily, weekly, and monthly cumulative and total print time columns
history['daily_cumulativePrintTime'] = 0.0
history['daily_TotalPrintTime'] = 0.0
history['weekly_cumulativePrintTime'] = 0.0
history['monthly_cumulativePrintTime'] = 0.0

# Compute cumulative print time per printer per day
history['daily_cumulativePrintTime'] = history.groupby(['printerName', 'print_day'])['printTime'].cumsum()

# Identify the last print job of each printer for the day
last_print_per_day = history.groupby(['printerName', 'print_day'])['endDate'].transform('max') == history['endDate']

# Assign the cumulativePrintTime value only for the last print of the day
history.loc[last_print_per_day, 'daily_cumulativePrintTime'] = history.loc[last_print_per_day, 'cumulativePrintTime'].astype(float)

# Ensure all other rows have zero
history.loc[~last_print_per_day, 'daily_cumulativePrintTime'] = 0.0

# Compute total print time per printer per day, but only set it at the last row of the day
history['daily_TotalPrintTime'] = history.groupby(['printerName', 'print_day'])['printTime'].transform('sum')

# Ensure only the last row of the day retains the value
history.loc[~last_print_per_day, 'daily_TotalPrintTime'] = 0.0

# Drop helper column
history.drop(columns=['print_day'], inplace=True)

# Ensure the DataFrame is sorted by printerName and startDate
history = history.sort_values(by=['printerName', 'startDate']).reset_index(drop=True)

# Create the day column (date part of startDate)
history['day'] = history['startDate'].dt.date

# Create the calendar_week column (ISO week number)
history['calendar_week'] = history['startDate'].dt.isocalendar().week

# Create a month column (and also a year column to group correctly over multiple years)
history['month'] = history['startDate'].dt.month
history['year'] = history['startDate'].dt.year

# --- Weekly Cumulative Print Time ---
history['weekly_cumulativePrintTime'] = history.groupby(['printerName', 'year', 'calendar_week'])['printTime'].cumsum()
last_print_per_week = history.groupby(['printerName', 'year', 'calendar_week'])['endDate'].transform('max') == history['endDate']
history.loc[last_print_per_week, 'weekly_cumulativePrintTime'] = history.loc[last_print_per_week, 'cumulativePrintTime'].astype(float)
history.loc[~last_print_per_week, 'weekly_cumulativePrintTime'] = 0.0

# --- Weekly Total Print Time ---
def assign_weekly_total(group):
    total = group['printTime'].sum()
    group['weekly_TotalPrintTime'] = 0.0
    # Assign the total to the last row in the week group
    group.iloc[-1, group.columns.get_loc('weekly_TotalPrintTime')] = total
    return group

history = history.groupby(
    ['printerName', 'year', 'calendar_week'], group_keys=False
).apply(assign_weekly_total)

# --- Monthly Cumulative Print Time ---
history['monthly_cumulativePrintTime'] = history.groupby(['printerName', 'year', 'month'])['printTime'].cumsum()
last_print_per_month = history.groupby(['printerName', 'year', 'month'])['endDate'].transform('max') == history['endDate']
history.loc[last_print_per_month, 'monthly_cumulativePrintTime'] = history.loc[last_print_per_month, 'cumulativePrintTime'].astype(float)
history.loc[~last_print_per_month, 'monthly_cumulativePrintTime'] = 0.0

# --- Monthly Total Print Time ---
def assign_monthly_total(group):
    total = group['printTime'].sum()
    group['monthly_TotalPrintTime'] = 0.0
    # Assign the total only to the last row of the month group
    group.iloc[-1, group.columns.get_loc('monthly_TotalPrintTime')] = total
    return group

history = history.groupby(
    ['printerName', 'year', 'month'], group_keys=False
).apply(assign_monthly_total)

# --- Utilization Rate Calculation ---
# Define total available time in minutes per day, week, and month (assuming 24-hour operation)
DAILY_AVAILABLE_MINUTES = 24 * 60
WEEKLY_AVAILABLE_MINUTES = 7 * 24 * 60
MONTHLY_AVAILABLE_MINUTES = 30 * 24 * 60  # Approximate for monthly calculation

history['daily_utilization_rate'] = (history['daily_TotalPrintTime'] / DAILY_AVAILABLE_MINUTES) * 100
history['weekly_utilization_rate'] = (history['weekly_TotalPrintTime'] / WEEKLY_AVAILABLE_MINUTES) * 100
history['monthly_utilization_rate'] = (history['monthly_TotalPrintTime'] / MONTHLY_AVAILABLE_MINUTES) * 100

# Display the DataFrame with the desired columns
display_columns = ["printerName", "startDate", "endDate", "printTime", "cumulativePrintTime",
                   "day", "calendar_week", "month", "daily_cumulativePrintTime", "daily_TotalPrintTime",
                   "weekly_cumulativePrintTime", "weekly_TotalPrintTime", "monthly_cumulativePrintTime", "monthly_TotalPrintTime",
                   "daily_utilization_rate", "weekly_utilization_rate", "monthly_utilization_rate"]

history[display_columns]



printerName           startDate             endDate  printTime  \
0        Prusa1 2023-02-19 11:56:33 2023-02-19 12:00:37     4.0667   
1        Prusa1 2024-07-28 14:32:28 2024-07-28 14:37:26     4.9667   
2        Prusa1 2024-07-28 14:38:34 2024-07-28 14:55:34    16.9833   
3        Prusa1 2024-07-28 15:11:19 2024-07-28 15:17:20     6.0167   
4        Prusa1 2024-07-28 15:32:32 2024-07-28 15:32:44     0.2000   
5        Prusa1 2024-07-28 15:35:52 2024-07-28 15:36:46     0.9000   
6        Prusa1 2024-07-28 15:38:03 2024-07-28 15:45:26     7.3833   
7        Prusa1 2024-07-29 18:44:28 2024-07-29 20:01:33    77.0833   
8        Prusa1 2024-07-29 20:02:19 2024-07-29 22:47:57   165.6333   
9        Prusa1 2024-11-05 14:48:13 2024-11-05 15:31:39    43.4333   
10       Prusa1 2024-11-06 08:13:39 2024-11-06 08:56:21    42.7000   
11       Prusa1 2024-11-08 16:11:37 2024-11-08 16:55:24    43.8000   
12       Prusa1 2024-11-10 10:28:26 2024-11-10 11:12:28    44.0333   
13       Prusa1 2024-11-11 11:48:07 2024-11-11 12:31:09    43.0167   
14       Prusa1 2024-11-14 09:13:25 2024-11-14 11:09:56   116.5167   
15       Prusa1 2024-11-14 11:31:10 2024-11-14 13:27:28   116.2833   
16       Prusa1 2024-11-29 15:34:18 2024-11-29 22:20:41   406.4000   
17       Prusa1 2024-12-10 11:20:48 2024-12-10 11:22:33     1.7667   
18       Prusa1 2024-12-10 11:24:27 2024-12-10 12:06:57    42.5000   
19       Prusa1 2024-12-12 11:01:23 2024-12-12 13:50:01   168.6333   
20       Prusa1 2024-12-12 14:22:09 2024-12-12 14:52:55    30.7667   
21       Prusa1 2024-12-12 15:07:51 2024-12-12 15:08:50     0.9833   
22       Prusa1 2024-12-12 15:10:16 2024-12-12 17:04:25   114.1500   
23       Prusa1 2024-12-18 10:30:02 2024-12-18 10:48:30    18.4667   
24       Prusa1 2024-12-18 10:55:54 2024-12-18 10:57:58     2.0667   
25       Prusa1 2024-12-18 10:59:19 2024-12-18 11:41:44    42.4167   
26       Prusa1 2024-12-18 12:31:42 2024-12-18 12:34:12     2.4833   
27       Prusa1 2024-12-18 12:36:30 2024-12-18 12:36:57     0.4500   
28       Prusa1 2024-12-19 08:28:10 2024-12-19 08:48:24    20.2333   
29       Prusa1 2024-12-19 09:01:40 2024-12-19 09:44:13    42.5333   
30       Prusa1 2024-12-19 10:24:29 2024-12-19 11:08:22    43.8833   
31       Prusa1 2024-12-19 12:17:22 2024-12-19 14:14:58   117.6000   
32       Prusa1 2024-12-19 14:19:31 2024-12-19 15:02:36    43.0667   
33       Prusa1 2024-12-19 15:23:55 2024-12-19 16:07:30    43.5833   
34       Prusa1 2024-12-19 16:17:15 2024-12-19 17:00:33    43.3000   
35       Prusa1 2024-12-19 17:13:36 2024-12-19 17:57:02    43.4333   
36       Prusa1 2024-12-19 19:43:51 2024-12-19 20:27:38    43.7833   
37       Prusa1 2024-12-20 09:11:44 2024-12-20 09:55:51    44.1167   
38       Prusa1 2024-12-22 12:13:08 2024-12-22 13:05:38    52.4833   
39       Prusa1 2024-12-23 10:24:01 2024-12-23 17:10:27   406.4333   
40       Prusa1 2024-12-23 17:32:21 2024-12-24 00:18:37   406.2667   
41       Prusa1 2024-12-24 12:46:23 2024-12-24 19:32:58   406.6000   
42       Prusa1 2024-12-25 19:17:54 2024-12-26 02:04:28   406.5667   
43       Prusa1 2024-12-26 14:23:58 2024-12-26 21:10:32   406.5667   
44       Prusa1 2024-12-30 12:57:23 2024-12-30 12:57:25     0.0500   
45       Prusa1 2024-12-30 13:11:05 2024-12-30 16:08:01   176.9333   
46       Prusa1 2024-12-30 16:52:28 2024-12-30 19:54:03   181.5833   
47       Prusa1 2024-12-31 11:14:02 2024-12-31 14:12:22   178.3333   
48       Prusa1 2024-12-31 14:30:57 2024-12-31 14:41:06    10.1500   
49       Prusa1 2024-12-31 14:45:41 2024-12-31 14:52:21     6.6667   
50       Prusa1 2024-12-31 14:53:31 2024-12-31 17:53:07   179.5833   
51       Prusa1 2024-12-31 17:56:48 2024-12-31 20:57:57   181.1500   
52       Prusa1 2024-12-31 21:05:13 2025-01-01 00:07:02   181.8167   
53       Prusa1 2025-01-02 09:56:05 2025-01-02 12:59:22   183.2833   
54       Prusa1 2025-01-02 13:22:48 2025-01-02 16:25:49   183.0167   
55       Prusa1 2025-01-02 17:07:04 2025-01-02 20:10:14   183.1667   
56       Prusa

## <font color="#00008B"><b>📋 LISTING AVAILABLE COLUMNS IN THE <mark style="background-color: yellow;"><b><font color="black">`history`</font></b></mark> DATAFRAME</b></font>

**What this cell does**

1. Retrieves all current column names from the <mark style="background-color: yellow;"><b><font color="black">`history`</font></b></mark> DataFrame with  
   `history.columns.tolist()`.

2. Stores them in <mark style="background-color: yellow;"><b><font color="black">`columns_list`</font></b></mark> for easy inspection, reuse, or debugging.

> Printing <mark style="background-color: yellow;"><b><font color="black">`columns_list`</font></b></mark> shows every field now available after all preprocessing and feature-engineering steps.


In [61]:
# Check available column names
columns_list = history.columns.tolist()
columns_list


['printerID',
 'printerName',
 'success',
 'reason',
 'fileName',
 'filePath',
 'startDate',
 'endDate',
 'printTime',
 'is_error',
 'cumulativePrintTime',
 'totalPrintTime',
 'total_prints',
 'total_success',
 'ErrorCountSoFar',
 'CumFailure',
 'date',
 'MTBF',
 'MTBF_per_Print',
 'FailureRate',
 'FailureRate_per_Print',
 'SuccessRate',
 'TotalOperatingTimeExpected',
 'TotalExpectedFailure',
 'RUL',
 'daily_cumulativePrintTime',
 'daily_TotalPrintTime',
 'weekly_cumulativePrintTime',
 'monthly_cumulativePrintTime',
 'day',
 'calendar_week',
 'month',
 'year',
 'weekly_TotalPrintTime',
 'monthly_TotalPrintTime',
 'daily_utilization_rate',
 'weekly_utilization_rate',
 'monthly_utilization_rate']

## <font color="#00008B"><b>📝 UPDATING THE FIRST ROW’S <mark style="background-color: yellow;"><b><font color="black">`filePath`</font></b></mark></b></font>

**What happens in this cell**

- Directly **over-writes** the value in the first row (`index 0`) of the  
  <mark style="background-color: yellow;"><b><font color="black">`filePath`</font></b></mark> column inside the  
  <mark style="background-color: yellow;"><b><font color="black">`history`</font></b></mark> DataFrame:

  ```python
  history.at[0, 'filePath'] = "Game_tray_thick_tapered_0.25mm_ABS_MINI_36m.gcode"


In [62]:
history.at[0, 'filePath'] = "Game_tray_thick_tapered_0.25mm_ABS_MINI_36m.gcode"
history.head()

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
1  66a632772531d16acc9b3a00      Prusa1        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m.gcode 2023-02-19 11:56:33   
1                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37     4.0667         1               4.0667   
1 2024-07-28 14:37:26     4.9667         1               9.0333   
2 2024-07-28 14:55:34    16.9833         1              26.0167   
3 2024-07-28 15:17:20     6.0167         1              32.0333   
4 2024-07-28 15:32:44     0.2000         1              32.2333   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  \
0      11082.2000           112             64                1          48   
1      11082.2000           112             64                2          48   
2      11082.2000           112             64                3          48   
3      11082.2000           112             64                4          48   
4      11082.2000           112             64                5          48   

         date     MTBF  MTBF_per_Print  FailureRate  FailureRate_per_Print  \
0  2023-02-19 230.8792          4.0667       0.0043                 0.2459   
1  2024-07-28 230.8792          4.5167       0.0043                 0.2214   
2  2024-07-28 230.8792          8.6722       0.0043                 0.1153   
3  2024-07-28 230.8792          8.0083       0.0043                 0.1249   
4  2024-07-28 230.8792          6.4467       0.0043                 0.1551   

   SuccessRate  TotalOperatingTimeExpected  TotalExpectedFailure      RUL  \
0      57.1429                       43800            10770.4918 729.9322   
1      57.1429                       43800             9697.4170 729.8494   
2      57.1429                       43800             5050.6086 729.5664   
3      57.1429                       43800             5469.3028 729.4661   
4      57.1429                       43800             6794.2089 729.4628   

   daily_cumulativePrintTime  daily_TotalPrintTime  \
0                     4.0667                4.0667   
1                     0.0000                0.0000   
2                     0.0000                0.0000   
3                     0.0000                0.0000   
4                     0.0000                0.0000   

   weekly_cumulativePrintTime  monthly_cumulativePrintTime         day  \
0                      4.0667                       4.0667  2023-02-19   
1                      0.0000                       0.0000  2024-07-28   
2                      0.0000                       0.0000  2024-07-28   
3                      0.0000                       0.0000  2024-07-28   
4                      0.0000                       0.0000  2024-07-28   

   calendar_week  month  year  weekly_TotalPrintTime  monthly_TotalPrintTime  \
0              7      2  2023                 4.0667                  4.0667   
1             30      7  2024                 0.0000                  0.0000   
2             30      7  2024                 0.0

## <font color="#00008B"><b>🕒 PARSING EXPECTED PRINT-TIME FROM <mark style="background-color: yellow;"><b><font color="black">`filePath`</font></b></mark></b></font>

This step enriches the dataset by **decoding the build-time embedded in each G-code filename**:

1. **Regex extraction**  
   - Looks for the pattern **`MINI_… .gcode`** and captures the alphanumeric duration that sits between them.  
   - Example: `MINI_36m.gcode` → **36 minutes**, `MINI_2h15m.gcode` → **135 minutes**.

2. **Time-string conversion**  
   - Converts any **h m s** components to **total minutes**:
     - `2h` → 120 min  
     - `15m` → 15 min  
     - `30s` → 0.5 min

3. **Creates a new numeric column**  
   - Stores the result in <mark style="background-color: yellow;"><b><font color="black">`print_time_expected`</font></b></mark> for every row.  
   - Non-matching filenames are assigned **0 min** (no duration info).

4. **Why it matters**  
   - Gives a **quick estimator of planned print duration** without parsing slicer metadata.  
   - Useful for validating actual vs. expected runtime, scheduling, and capacity planning.

> Check: **`history.head()`** now shows a populated <mark style="background-color: yellow;"><b><font color="black">`print_time_expected`</font></b></mark> column alongside the original <mark style="background-color: yellow;"><b><font color="black">`filePath`</font></b></mark>.


In [63]:
import pandas as pd
import re

# Assume the DataFrame `history` is already loaded

# Function to extract the duration between MINI_ and .gcode
def extract_print_time(file_path):
    match = re.search(r"MINI_([0-9hms]+)\.gcode", file_path)
    if match:
        time_str = match.group(1)

        # Convert the duration to minutes
        hours = re.search(r"(\d+)h", time_str)
        minutes = re.search(r"(\d+)m", time_str)
        seconds = re.search(r"(\d+)s", time_str)

        total_minutes = 0
        if hours:
            total_minutes += int(hours.group(1)) * 60
        if minutes:
            total_minutes += int(minutes.group(1))
        if seconds:
            total_minutes += int(seconds.group(1)) / 60  # Convert seconds to minutes

        return total_minutes
    return None

# Apply the function to the entire dataset
history["print_time_expected"] = history["filePath"].apply(extract_print_time)

# Fill NaN values with 0
history["print_time_expected"].fillna(0, inplace=True)

history



printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1        0       error   
1    66a632772531d16acc9b3a00      Prusa1        0       error   
2    66a632772531d16acc9b3a00      Prusa1        0       error   
3    66a632772531d16acc9b3a00      Prusa1        0       error   
4    66a632772531d16acc9b3a00      Prusa1        0       error   
5    66a632772531d16acc9b3a00      Prusa1        0       error   
6    66a632772531d16acc9b3a00      Prusa1        0       error   
7    66a632772531d16acc9b3a00      Prusa1        0       error   
8    66a632772531d16acc9b3a00      Prusa1        1  successful   
9    66a632772531d16acc9b3a00      Prusa1        1  successful   
10   66a632772531d16acc9b3a00      Prusa1        1  successful   
11   66a632772531d16acc9b3a00      Prusa1        1  successful   
12   66a632772531d16acc9b3a00      Prusa1        1  successful   
13   66a632772531d16acc9b3a00      Prusa1        1  successful   
14   66a632772531d16acc9b3a00      Prusa1        1  successful   
15   66a632772531d16acc9b3a00      Prusa1        1  successful   
16   66a632772531d16acc9b3a00      Prusa1        1  successful   
17   66a632772531d16acc9b3a00      Prusa1        0       error   
18   66a632772531d16acc9b3a00      Prusa1        1  successful   
19   66a632772531d16acc9b3a00      Prusa1        0       error   
20   66a632772531d16acc9b3a00      Prusa1        0       error   
21   66a632772531d16acc9b3a00      Prusa1        0       error   
22   66a632772531d16acc9b3a00      Prusa1        1  successful   
23   66a632772531d16acc9b3a00      Prusa1        0       error   
24   66a632772531d16acc9b3a00      Prusa1        0       error   
25   66a632772531d16acc9b3a00      Prusa1        1  successful   
26   66a632772531d16acc9b3a00      Prusa1        0       error   
27   66a632772531d16acc9b3a00      Prusa1        0       error   
28   66a632772531d16acc9b3a00      Prusa1        0       error   
29   66a632772531d16acc9b3a00      Prusa1        1  successful   
30   66a632772531d16acc9b3a00      Prusa1        1  successful   
31   66a632772531d16acc9b3a00      Prusa1        1  successful   
32   66a632772531d16acc9b3a00      Prusa1        1  successful   
33   66a632772531d16acc9b3a00      Prusa1        1  successful   
34   66a632772531d16acc9b3a00      Prusa1        1  successful   
35   66a632772531d16acc9b3a00      Prusa1        1  successful   
36   66a632772531d16acc9b3a00      Prusa1        1  successful   
37   66a632772531d16acc9b3a00      Prusa1        1  successful   
38   66a632772531d16acc9b3a00      Prusa1        1  successful   
39   66a632772531d16acc9b3a00      Prusa1        1  successful   
40   66a632772531d16acc9b3a00      Prusa1        1  successful   
41   66a632772531d16acc9b3a00      Prusa1        1  successful   
42   66a632772531d16acc9b3a00      Prusa1        1  successful   
43   66a632772531d16acc9b3a00      Prusa1        1  successful   
44   66a632772531d16acc9b3a00      Prusa1        0       error   
45   66a632772531d16acc9b3a00      Prusa1        1  successful   
46   66a632772531d16acc9b3a00      Prusa1        1  successful   
47   66a632772531d16acc9b3a00      Prusa1        1  successful   
48   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
49   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
50   66a632772531d16acc9b3a00      Prusa1        1  successful   
51   66a632772531d16acc9b3a00      Prusa1        1  successful   
52   66a632772531d16acc9b3a00      Prusa1        1  successful   
53   66a632772531d16acc9b3a00      Prusa1        1  successful   
54   66a632772531d16acc9b3a00      Prusa1        1  successful   
55   66a632772531d16acc9b3a00      Prusa1        1  successful   
56   66a632772531d16acc9b3a00      Prusa1        1  successful   
57   66a632772531d16acc9b3a00      Prusa1        1  successful   
58   66a632772531d16acc9b3a00      Prusa1        1  successful   
59   66a632772531d16acc9b3a00      Prusa1        1  successf

## <font color="#00008B"><b>🧮 AGGREGATING <mark style="background-color: yellow;"><b><font color="black">`print_time_expected`</font></b></mark> INTO A PER-PRINTER KPI</b></font>

This cell creates a **printer-level workload metric** by summing the expected print time of every job:

1. **Group & aggregate**  
   - Uses **`groupby`** on <mark style="background-color: yellow;"><b><font color="black">`printerName`</font></b></mark> to obtain the **total minutes** of <mark style="background-color: yellow;"><b><font color="black">`print_time_expected`</font></b></mark> for each machine.  
   - Result stored in the helper series <mark style="background-color: yellow;"><b><font color="black">`total_print_time_expected`</font></b></mark>.

2. **Map back to every row**  
   - Adds a new column <mark style="background-color: yellow;"><b><font color="black">`total_print_time_expected`</font></b></mark> to **`history`**, so each record carries its printer’s overall expected workload (useful for joins and modelling).

3. **Quick sanity check**  
   - Prints rows where <mark style="background-color: yellow;"><b><font color="black">`printerName`</font></b></mark> equals **Prusa1** to verify the metric appears correctly.

> By embedding this cumulative KPI, downstream analyses can compare actual usage against the **expected total runtime** for each printer, aiding capacity planning and utilisation benchmarking.


In [64]:
import pandas as pd

# Örnek bir history DataFrame oluşturduğunu varsayalım veya mevcut DataFrame'i kullan
# history = pd.read_csv("history_dataset.csv")  # Eğer CSV'den yüklüyorsan

# PrinterName bazında print_time_expected toplamını hesaplayalım
total_print_time_expected = history.groupby("printerName")["print_time_expected"].sum()

# Bu toplam değeri tekrar orijinal DataFrame'e ekleyelim
history["total_print_time_expected"] = history["printerName"].map(total_print_time_expected)

history[history["printerName"] == "Prusa1"]

printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1        0       error   
1    66a632772531d16acc9b3a00      Prusa1        0       error   
2    66a632772531d16acc9b3a00      Prusa1        0       error   
3    66a632772531d16acc9b3a00      Prusa1        0       error   
4    66a632772531d16acc9b3a00      Prusa1        0       error   
5    66a632772531d16acc9b3a00      Prusa1        0       error   
6    66a632772531d16acc9b3a00      Prusa1        0       error   
7    66a632772531d16acc9b3a00      Prusa1        0       error   
8    66a632772531d16acc9b3a00      Prusa1        1  successful   
9    66a632772531d16acc9b3a00      Prusa1        1  successful   
10   66a632772531d16acc9b3a00      Prusa1        1  successful   
11   66a632772531d16acc9b3a00      Prusa1        1  successful   
12   66a632772531d16acc9b3a00      Prusa1        1  successful   
13   66a632772531d16acc9b3a00      Prusa1        1  successful   
14   66a632772531d16acc9b3a00      Prusa1        1  successful   
15   66a632772531d16acc9b3a00      Prusa1        1  successful   
16   66a632772531d16acc9b3a00      Prusa1        1  successful   
17   66a632772531d16acc9b3a00      Prusa1        0       error   
18   66a632772531d16acc9b3a00      Prusa1        1  successful   
19   66a632772531d16acc9b3a00      Prusa1        0       error   
20   66a632772531d16acc9b3a00      Prusa1        0       error   
21   66a632772531d16acc9b3a00      Prusa1        0       error   
22   66a632772531d16acc9b3a00      Prusa1        1  successful   
23   66a632772531d16acc9b3a00      Prusa1        0       error   
24   66a632772531d16acc9b3a00      Prusa1        0       error   
25   66a632772531d16acc9b3a00      Prusa1        1  successful   
26   66a632772531d16acc9b3a00      Prusa1        0       error   
27   66a632772531d16acc9b3a00      Prusa1        0       error   
28   66a632772531d16acc9b3a00      Prusa1        0       error   
29   66a632772531d16acc9b3a00      Prusa1        1  successful   
30   66a632772531d16acc9b3a00      Prusa1        1  successful   
31   66a632772531d16acc9b3a00      Prusa1        1  successful   
32   66a632772531d16acc9b3a00      Prusa1        1  successful   
33   66a632772531d16acc9b3a00      Prusa1        1  successful   
34   66a632772531d16acc9b3a00      Prusa1        1  successful   
35   66a632772531d16acc9b3a00      Prusa1        1  successful   
36   66a632772531d16acc9b3a00      Prusa1        1  successful   
37   66a632772531d16acc9b3a00      Prusa1        1  successful   
38   66a632772531d16acc9b3a00      Prusa1        1  successful   
39   66a632772531d16acc9b3a00      Prusa1        1  successful   
40   66a632772531d16acc9b3a00      Prusa1        1  successful   
41   66a632772531d16acc9b3a00      Prusa1        1  successful   
42   66a632772531d16acc9b3a00      Prusa1        1  successful   
43   66a632772531d16acc9b3a00      Prusa1        1  successful   
44   66a632772531d16acc9b3a00      Prusa1        0       error   
45   66a632772531d16acc9b3a00      Prusa1        1  successful   
46   66a632772531d16acc9b3a00      Prusa1        1  successful   
47   66a632772531d16acc9b3a00      Prusa1        1  successful   
48   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
49   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
50   66a632772531d16acc9b3a00      Prusa1        1  successful   
51   66a632772531d16acc9b3a00      Prusa1        1  successful   
52   66a632772531d16acc9b3a00      Prusa1        1  successful   
53   66a632772531d16acc9b3a00      Prusa1        1  successful   
54   66a632772531d16acc9b3a00      Prusa1        1  successful   
55   66a632772531d16acc9b3a00      Prusa1        1  successful   
56   66a632772531d16acc9b3a00      Prusa1        1  successful   
57   66a632772531d16acc9b3a00      Prusa1        1  successful   
58   66a632772531d16acc9b3a00      Prusa1        1  successful   
59   66a632772531d16acc9b3a00      Prusa1        1  successf

## <font color="#00008B"><b>⚙️ COMPUTING OVERALL PRINTER-FLEET EFFICIENCY</b></font>

A concise KPI that blends **throughput, capacity & quality** into a single percentage.

---

### 🔄 **Data Normalisation**  
The columns  
<mark style="background-color: yellow;"><b><font color="black">`daily_TotalPrintTime`</font></b></mark>,  
<mark style="background-color: yellow;"><b><font color="black">`TotalOperatingTimeExpected`</font></b></mark> and  
<mark style="background-color: yellow;"><b><font color="black">`SuccessRate`</font></b></mark>  
are coerced to numeric (invalids → 0) to guarantee clean arithmetic.

---

### 📊 **Fleet-level Aggregates**

| KPI                                                                                                   | Definition                                       | Purpose                                  |
|-------------------------------------------------------------------------------------------------------|--------------------------------------------------|------------------------------------------|
| <mark style="background-color: yellow;"><b><font color="black">`total_print_time`</font></b></mark>            | Σ of all daily printing minutes                  | Measures **actual** utilisation          |
| <mark style="background-color: yellow;"><b><font color="black">`total_operating_time_expected`</font></b></mark> | Σ of design-spec operating minutes (capacity)    | Represents theoretical capacity          |
| <mark style="background-color: yellow;"><b><font color="black">`average_success_rate`</font></b></mark>         | Mean job success ratio (%)                       | Quality factor weighting utilisation     |


> **Robustness rule**: if <mark style="background-color: yellow;"><b><font color="black">`total_operating_time_expected`</font></b></mark> = 0,  
> the formula safely returns **0 %** to avoid division-by-zero.

---

### ✅ **Result Persistence**  
The computed figure is written to  
<mark style="background-color: yellow;"><b><font color="black">`Efficiency`</font></b></mark>  
for every row, enabling effortless filtering, charting and export.

> **Why it matters:** this KPI distils **capacity utilisation** *and* **print quality** into one actionable score.


In [65]:
import pandas as pd

# Ensure relevant columns are numeric
history["daily_TotalPrintTime"] = pd.to_numeric(history["daily_TotalPrintTime"], errors='coerce').fillna(0)
history["TotalOperatingTimeExpected"] = pd.to_numeric(history["TotalOperatingTimeExpected"], errors='coerce').fillna(0)
history["SuccessRate"] = pd.to_numeric(history["SuccessRate"], errors='coerce').fillna(0)

# Calculate total print time
total_print_time = history["daily_TotalPrintTime"].sum()

# Calculate total expected operating time
total_operating_time_expected = history["TotalOperatingTimeExpected"].sum()

# Calculate average success rate
average_success_rate = history["SuccessRate"].mean()

# Compute overall efficiency
if total_operating_time_expected > 0:
    overall_efficiency = (total_print_time / total_operating_time_expected) * average_success_rate * 100
else:
    overall_efficiency = 0  # Avoid division by zero

# Add overall efficiency column to the dataset
history["Efficiency"] = overall_efficiency

# Print the result
print(f"Overall Efficiency: {overall_efficiency:.2f}%")
history

Overall Efficiency: 17.47%


printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1        0       error   
1    66a632772531d16acc9b3a00      Prusa1        0       error   
2    66a632772531d16acc9b3a00      Prusa1        0       error   
3    66a632772531d16acc9b3a00      Prusa1        0       error   
4    66a632772531d16acc9b3a00      Prusa1        0       error   
5    66a632772531d16acc9b3a00      Prusa1        0       error   
6    66a632772531d16acc9b3a00      Prusa1        0       error   
7    66a632772531d16acc9b3a00      Prusa1        0       error   
8    66a632772531d16acc9b3a00      Prusa1        1  successful   
9    66a632772531d16acc9b3a00      Prusa1        1  successful   
10   66a632772531d16acc9b3a00      Prusa1        1  successful   
11   66a632772531d16acc9b3a00      Prusa1        1  successful   
12   66a632772531d16acc9b3a00      Prusa1        1  successful   
13   66a632772531d16acc9b3a00      Prusa1        1  successful   
14   66a632772531d16acc9b3a00      Prusa1        1  successful   
15   66a632772531d16acc9b3a00      Prusa1        1  successful   
16   66a632772531d16acc9b3a00      Prusa1        1  successful   
17   66a632772531d16acc9b3a00      Prusa1        0       error   
18   66a632772531d16acc9b3a00      Prusa1        1  successful   
19   66a632772531d16acc9b3a00      Prusa1        0       error   
20   66a632772531d16acc9b3a00      Prusa1        0       error   
21   66a632772531d16acc9b3a00      Prusa1        0       error   
22   66a632772531d16acc9b3a00      Prusa1        1  successful   
23   66a632772531d16acc9b3a00      Prusa1        0       error   
24   66a632772531d16acc9b3a00      Prusa1        0       error   
25   66a632772531d16acc9b3a00      Prusa1        1  successful   
26   66a632772531d16acc9b3a00      Prusa1        0       error   
27   66a632772531d16acc9b3a00      Prusa1        0       error   
28   66a632772531d16acc9b3a00      Prusa1        0       error   
29   66a632772531d16acc9b3a00      Prusa1        1  successful   
30   66a632772531d16acc9b3a00      Prusa1        1  successful   
31   66a632772531d16acc9b3a00      Prusa1        1  successful   
32   66a632772531d16acc9b3a00      Prusa1        1  successful   
33   66a632772531d16acc9b3a00      Prusa1        1  successful   
34   66a632772531d16acc9b3a00      Prusa1        1  successful   
35   66a632772531d16acc9b3a00      Prusa1        1  successful   
36   66a632772531d16acc9b3a00      Prusa1        1  successful   
37   66a632772531d16acc9b3a00      Prusa1        1  successful   
38   66a632772531d16acc9b3a00      Prusa1        1  successful   
39   66a632772531d16acc9b3a00      Prusa1        1  successful   
40   66a632772531d16acc9b3a00      Prusa1        1  successful   
41   66a632772531d16acc9b3a00      Prusa1        1  successful   
42   66a632772531d16acc9b3a00      Prusa1        1  successful   
43   66a632772531d16acc9b3a00      Prusa1        1  successful   
44   66a632772531d16acc9b3a00      Prusa1        0       error   
45   66a632772531d16acc9b3a00      Prusa1        1  successful   
46   66a632772531d16acc9b3a00      Prusa1        1  successful   
47   66a632772531d16acc9b3a00      Prusa1        1  successful   
48   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
49   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
50   66a632772531d16acc9b3a00      Prusa1        1  successful   
51   66a632772531d16acc9b3a00      Prusa1        1  successful   
52   66a632772531d16acc9b3a00      Prusa1        1  successful   
53   66a632772531d16acc9b3a00      Prusa1        1  successful   
54   66a632772531d16acc9b3a00      Prusa1        1  successful   
55   66a632772531d16acc9b3a00      Prusa1        1  successful   
56   66a632772531d16acc9b3a00      Prusa1        1  successful   
57   66a632772531d16acc9b3a00      Prusa1        1  successful   
58   66a632772531d16acc9b3a00      Prusa1        1  successful   
59   66a632772531d16acc9b3a00      Prusa1        1  successf

## <font color="#00008B"><b>⚙️ PER-PRINTER EFFICIENCY KPI</b></font>

This step builds a **printer-level efficiency score** that blends **throughput, capacity, and quality** for each machine.

---

### 🛠️ **Data normalisation**  
The columns  
<mark style="background-color: yellow;"><b><font color="black">`daily_TotalPrintTime`</font></b></mark>,  
<mark style="background-color: yellow;"><b><font color="black">`TotalOperatingTimeExpected`</font></b></mark>, and  
<mark style="background-color: yellow;"><b><font color="black">`SuccessRate`</font></b></mark>  
are coerced to numeric and NaNs filled with 0 to guarantee robust arithmetic.

---

### 📊 **Fleet-to-printer aggregation**  

| Derived metric | How it’s computed (per printer) | Why it matters |
|----------------|---------------------------------|----------------|
| <mark style="background-color: yellow;"><b><font color="black">`total_print_time`</font></b></mark> | Σ of <mark style="background-color: yellow;"><b><font color="black">`daily_TotalPrintTime`</font></b></mark> | Actual minutes spent printing |
| <mark style="background-color: yellow;"><b><font color="black">`total_operating_time_expected`</font></b></mark> | Σ of <mark style="background-color: yellow;"><b><font color="black">`TotalOperatingTimeExpected`</font></b></mark> | Design-spec capacity |
| <mark style="background-color: yellow;"><b><font color="black">`average_success_rate`</font></b></mark> | Mean of <mark style="background-color: yellow;"><b><font color="black">`SuccessRate`</font></b></mark> | Quality weighting |

---

> The calculated value is stored in  
> <mark style="background-color: yellow;"><b><font color="black">`Efficiency_per_printer`</font></b></mark>  
> and merged back into **`history`** so it is available for dashboards, alerts, and further modelling.  
>  
> *(If `total_operating_time_expected` is zero, efficiency is automatically set to **0 %** to avoid division-by-zero.)*


In [67]:
import pandas as pd

# Ensure relevant columns are numeric
history["daily_TotalPrintTime"] = pd.to_numeric(history["daily_TotalPrintTime"], errors='coerce').fillna(0)
history["TotalOperatingTimeExpected"] = pd.to_numeric(history["TotalOperatingTimeExpected"], errors='coerce').fillna(0)
history["SuccessRate"] = pd.to_numeric(history["SuccessRate"], errors='coerce').fillna(0)

# Group by printerName and calculate required values
printer_efficiency = history.groupby("printerName").agg(
    total_print_time=("daily_TotalPrintTime", "sum"),
    total_operating_time_expected=("TotalOperatingTimeExpected", "sum"),
    average_success_rate=("SuccessRate", "mean")
)

# Compute efficiency per printer
printer_efficiency["Efficiency_per_printer"] = (
    (printer_efficiency["total_print_time"] / printer_efficiency["total_operating_time_expected"]) *
    printer_efficiency["average_success_rate"] * 100
).fillna(0)  # Avoid NaN values if division by zero occurs

# Merge the calculated efficiency back into history dataset
history = history.merge(
    printer_efficiency[["Efficiency_per_printer"]],
    on="printerName",
    how="left"
)

# Confirm the new column is added
history  # Display the first few rows to check the new column


printerID printerName  success      reason  \
0    63af118fd41d203cfc2d5193      Prusa1        0       error   
1    66a632772531d16acc9b3a00      Prusa1        0       error   
2    66a632772531d16acc9b3a00      Prusa1        0       error   
3    66a632772531d16acc9b3a00      Prusa1        0       error   
4    66a632772531d16acc9b3a00      Prusa1        0       error   
5    66a632772531d16acc9b3a00      Prusa1        0       error   
6    66a632772531d16acc9b3a00      Prusa1        0       error   
7    66a632772531d16acc9b3a00      Prusa1        0       error   
8    66a632772531d16acc9b3a00      Prusa1        1  successful   
9    66a632772531d16acc9b3a00      Prusa1        1  successful   
10   66a632772531d16acc9b3a00      Prusa1        1  successful   
11   66a632772531d16acc9b3a00      Prusa1        1  successful   
12   66a632772531d16acc9b3a00      Prusa1        1  successful   
13   66a632772531d16acc9b3a00      Prusa1        1  successful   
14   66a632772531d16acc9b3a00      Prusa1        1  successful   
15   66a632772531d16acc9b3a00      Prusa1        1  successful   
16   66a632772531d16acc9b3a00      Prusa1        1  successful   
17   66a632772531d16acc9b3a00      Prusa1        0       error   
18   66a632772531d16acc9b3a00      Prusa1        1  successful   
19   66a632772531d16acc9b3a00      Prusa1        0       error   
20   66a632772531d16acc9b3a00      Prusa1        0       error   
21   66a632772531d16acc9b3a00      Prusa1        0       error   
22   66a632772531d16acc9b3a00      Prusa1        1  successful   
23   66a632772531d16acc9b3a00      Prusa1        0       error   
24   66a632772531d16acc9b3a00      Prusa1        0       error   
25   66a632772531d16acc9b3a00      Prusa1        1  successful   
26   66a632772531d16acc9b3a00      Prusa1        0       error   
27   66a632772531d16acc9b3a00      Prusa1        0       error   
28   66a632772531d16acc9b3a00      Prusa1        0       error   
29   66a632772531d16acc9b3a00      Prusa1        1  successful   
30   66a632772531d16acc9b3a00      Prusa1        1  successful   
31   66a632772531d16acc9b3a00      Prusa1        1  successful   
32   66a632772531d16acc9b3a00      Prusa1        1  successful   
33   66a632772531d16acc9b3a00      Prusa1        1  successful   
34   66a632772531d16acc9b3a00      Prusa1        1  successful   
35   66a632772531d16acc9b3a00      Prusa1        1  successful   
36   66a632772531d16acc9b3a00      Prusa1        1  successful   
37   66a632772531d16acc9b3a00      Prusa1        1  successful   
38   66a632772531d16acc9b3a00      Prusa1        1  successful   
39   66a632772531d16acc9b3a00      Prusa1        1  successful   
40   66a632772531d16acc9b3a00      Prusa1        1  successful   
41   66a632772531d16acc9b3a00      Prusa1        1  successful   
42   66a632772531d16acc9b3a00      Prusa1        1  successful   
43   66a632772531d16acc9b3a00      Prusa1        1  successful   
44   66a632772531d16acc9b3a00      Prusa1        0       error   
45   66a632772531d16acc9b3a00      Prusa1        1  successful   
46   66a632772531d16acc9b3a00      Prusa1        1  successful   
47   66a632772531d16acc9b3a00      Prusa1        1  successful   
48   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
49   66a632772531d16acc9b3a00      Prusa1        0   cancelled   
50   66a632772531d16acc9b3a00      Prusa1        1  successful   
51   66a632772531d16acc9b3a00      Prusa1        1  successful   
52   66a632772531d16acc9b3a00      Prusa1        1  successful   
53   66a632772531d16acc9b3a00      Prusa1        1  successful   
54   66a632772531d16acc9b3a00      Prusa1        1  successful   
55   66a632772531d16acc9b3a00      Prusa1        1  successful   
56   66a632772531d16acc9b3a00      Prusa1        1  successful   
57   66a632772531d16acc9b3a00      Prusa1        1  successful   
58   66a632772531d16acc9b3a00      Prusa1        1  successful   
59   66a632772531d16acc9b3a00      Prusa1        1  successf

## <font color="#00008B"><b>🔄 COMPUTING <mark style="background-color: yellow;"><b><font color="black">`usage_since_last_error`</font></b></mark> FOR EVERY PRINTER</b></font>

This step creates a **running-time counter** that shows **how many minutes each machine has printed since its last failure**, enabling smarter maintenance triggers.

---

### 🛠️ **Workflow**

1. **Timestamp guarantee**  
   - Coerces <mark style="background-color: yellow;"><b><font color="black">`startDate`</font></b></mark> to `datetime` and **sorts** the dataset by <mark style="background-color: yellow;"><b><font color="black">`printerName`</font></b></mark> ➜ <mark style="background-color: yellow;"><b><font color="black">`startDate`</font></b></mark> to ensure chronological order.

2. **Per-printer cumulative loop**  
   - For each printer, iterates row-by-row:  
     - When <mark style="background-color: yellow;"><b><font color="black">`is_error`</font></b></mark> = 1, the counter resets to **0**.  
     - Otherwise, adds that job’s <mark style="background-color: yellow;"><b><font color="black">`printTime`</font></b></mark> to a running total.

3. **Column creation**  
   - Writes the rolling total to a new field  
     <mark style="background-color: yellow;"><b><font color="black">`usage_since_last_error`</font></b></mark>  
     for every row. NaNs are replaced with **0** for consistency.

---

**Why it matters**

- Highlights printers approaching critical runtime without an intervening fault.  
- Feeds dashboards & predictive-maintenance models with a fresh **“time-since-failure”** signal.

> After execution the new metric is fully integrated into the **`history`** DataFrame, ready for analysis (`history.head()` confirms the addition).


In [68]:
# Ensure 'startDate' is in datetime format
history["startDate"] = pd.to_datetime(history["startDate"], errors='coerce')

# Sort history by 'printerName' and 'startDate' to ensure correct sequencing
history = history.sort_values(by=["printerName", "startDate"]).reset_index(drop=True)

# Define function to calculate 'usage_since_last_error' for each printer group
def calculate_usage_since_last_error(group):
    usage = []
    cumulative_time = 0

    for _, row in group.iterrows():
        if row["is_error"] == 1:  # Reset counter on error
            cumulative_time = 0
        cumulative_time += row["printTime"]
        usage.append(cumulative_time)

    group["usage_since_last_error"] = usage
    return group

# Apply function to each printer group
history = history.groupby("printerName", group_keys=False).apply(calculate_usage_since_last_error)

# Fill NaN values with 0 to ensure consistency
history["usage_since_last_error"].fillna(0, inplace=True)

history.head()


printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
1  66a632772531d16acc9b3a00      Prusa1        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath           startDate  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m.gcode 2023-02-19 11:56:33   
1                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:32:28   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 14:38:34   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:11:19   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode 2024-07-28 15:32:32   

              endDate  printTime  is_error  cumulativePrintTime  \
0 2023-02-19 12:00:37     4.0667         1               4.0667   
1 2024-07-28 14:37:26     4.9667         1               9.0333   
2 2024-07-28 14:55:34    16.9833         1              26.0167   
3 2024-07-28 15:17:20     6.0167         1              32.0333   
4 2024-07-28 15:32:44     0.2000         1              32.2333   

   totalPrintTime  total_prints  total_success  ErrorCountSoFar  CumFailure  \
0      11082.2000           112             64                1          48   
1      11082.2000           112             64                2          48   
2      11082.2000           112             64                3          48   
3      11082.2000           112             64                4          48   
4      11082.2000           112             64                5          48   

         date     MTBF  MTBF_per_Print  FailureRate  FailureRate_per_Print  \
0  2023-02-19 230.8792          4.0667       0.0043                 0.2459   
1  2024-07-28 230.8792          4.5167       0.0043                 0.2214   
2  2024-07-28 230.8792          8.6722       0.0043                 0.1153   
3  2024-07-28 230.8792          8.0083       0.0043                 0.1249   
4  2024-07-28 230.8792          6.4467       0.0043                 0.1551   

   SuccessRate  TotalOperatingTimeExpected  TotalExpectedFailure      RUL  \
0      57.1429                       43800            10770.4918 729.9322   
1      57.1429                       43800             9697.4170 729.8494   
2      57.1429                       43800             5050.6086 729.5664   
3      57.1429                       43800             5469.3028 729.4661   
4      57.1429                       43800             6794.2089 729.4628   

   daily_cumulativePrintTime  daily_TotalPrintTime  \
0                     4.0667                4.0667   
1                     0.0000                0.0000   
2                     0.0000                0.0000   
3                     0.0000                0.0000   
4                     0.0000                0.0000   

   weekly_cumulativePrintTime  monthly_cumulativePrintTime         day  \
0                      4.0667                       4.0667  2023-02-19   
1                      0.0000                       0.0000  2024-07-28   
2                      0.0000                       0.0000  2024-07-28   
3                      0.0000                       0.0000  2024-07-28   
4                      0.0000                       0.0000  2024-07-28   

   calendar_week  month  year  weekly_TotalPrintTime  monthly_TotalPrintTime  \
0              7      2  2023                 4.0667                  4.0667   
1             30      7  2024                 0.0000                  0.0000   
2             30      7  2024                 0.0

## <font color="red"><b>📊 CHECKING HISTORY DATAFRAME STRUCTURE 🧐</b></font>

Running  
<mark style="background-color: yellow;"><b><font color="black">`history.info()`</font></b></mark>  
prints a concise summary of the **`history`** table:

- **Row count** & memory footprint  
- Each column’s **dtype** (`int64`, `float64`, `object`, `datetime64[ns]`, …)  
- The **non-null tally** per field (quick missing-value scan)

> Use this snapshot to verify that earlier transformations (type casting, new-feature engineering, NaN handling) were applied correctly before building models or creating visualisations.


In [69]:
history.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 171 entries, 0 to 170
Data columns (total 44 columns):
 #   Column                       Non-Null Count  Dtype         
---  ------                       --------------  -----         
 0   printerID                    171 non-null    object        
 1   printerName                  171 non-null    object        
 2   success                      171 non-null    int32         
 3   reason                       171 non-null    object        
 4   fileName                     171 non-null    object        
 5   filePath                     171 non-null    object        
 6   startDate                    171 non-null    datetime64[ns]
 7   endDate                      171 non-null    datetime64[ns]
 8   printTime                    171 non-null    float64       
 9   is_error                     171 non-null    int32         
 10  cumulativePrintTime          171 non-null    float64       
 11  totalPrintTime               171 non-null    

## <font color="#00008B"><b>🗂️ RE-ARRANGING HISTORY DATAFRAME COLUMNS FOR REPORT-READY OUTPUT</b></font>

This step tidies the **`history`** table into a reader-friendly left-to-right flow:

1. **Blueprint of the desired layout**  
   A curated list — <mark style="background-color: yellow;"><b><font color="black">`column_order`</font></b></mark> — groups fields by theme  
   (identification → metrics → diagnostics → time features), ending with longevity KPI  
   <mark style="background-color: yellow;"><b><font color="black">`RUL`</font></b></mark> for emphasis.

2. **Safety check**  
   Only columns that actually exist are selected via  
   <mark style="background-color: yellow;"><b><font color="black">`existing_columns`</font></b></mark>, eliminating the risk of **KeyError** if a column is missing.

3. **Re-indexing**  
   The dataframe is re-ordered with  
   <mark style="background-color: yellow;"><b><font color="black">`history = history[existing_columns]`</font></b></mark>  
   and immediately previewed using **`.head()`**.

> Result: a clean, logically grouped dataset that’s ready for export, dashboard ingestion, or modelling pipelines.


In [70]:
# Define an optimized column order based on the available columns
column_order = [
    # Identification and Basic Information
    "printerID", "printerName", "startDate", "endDate",

    # Print Summary & Performance Metrics
    "total_prints", "total_success", "SuccessRate", "Efficiency", "Efficiency_per_printer",

    # Print Job Information
    "printTime", "totalPrintTime", "cumulativePrintTime",
    "daily_TotalPrintTime", "weekly_TotalPrintTime", "monthly_TotalPrintTime",
    "daily_cumulativePrintTime", "weekly_cumulativePrintTime", "monthly_cumulativePrintTime",

    # Print Success & Failure Analysis
    "success", "reason", "reason_description", "is_error", "ErrorCountSoFar", "CumFailure", "usage_since_last_error",
    "FailureRate", "FailureRate_per_Print",

    # Utilization and Operational Metrics
    "TotalOperatingTimeExpected", "TotalExpectedFailure", "MTBF", "MTBF_per_Print",
    "daily_utilization_rate", "weekly_utilization_rate", "monthly_utilization_rate",

    # Expected and Predicted Print Time
    "print_time_expected", "total_print_time_expected",

    # Remaining Useful Life (Placed at the end to emphasize longevity of the machine)
    "RUL",

    # Additional Columns
    "fileName", "filePath", "calendar_week", "day", "month", "year"
]

# Ensure all columns exist before reordering
existing_columns = [col for col in column_order if col in history.columns]
history = history[existing_columns]
history.head()


printerID printerName           startDate  \
0  63af118fd41d203cfc2d5193      Prusa1 2023-02-19 11:56:33   
1  66a632772531d16acc9b3a00      Prusa1 2024-07-28 14:32:28   
2  66a632772531d16acc9b3a00      Prusa1 2024-07-28 14:38:34   
3  66a632772531d16acc9b3a00      Prusa1 2024-07-28 15:11:19   
4  66a632772531d16acc9b3a00      Prusa1 2024-07-28 15:32:32   

              endDate  total_prints  total_success  SuccessRate  Efficiency  \
0 2023-02-19 12:00:37           112             64      57.1429     17.4657   
1 2024-07-28 14:37:26           112             64      57.1429     17.4657   
2 2024-07-28 14:55:34           112             64      57.1429     17.4657   
3 2024-07-28 15:17:20           112             64      57.1429     17.4657   
4 2024-07-28 15:32:44           112             64      57.1429     17.4657   

   printTime  totalPrintTime  cumulativePrintTime  daily_TotalPrintTime  \
0     4.0667      11082.2000               4.0667                4.0667   
1     4.9667      11082.2000               9.0333                0.0000   
2    16.9833      11082.2000              26.0167                0.0000   
3     6.0167      11082.2000              32.0333                0.0000   
4     0.2000      11082.2000              32.2333                0.0000   

   weekly_TotalPrintTime  monthly_TotalPrintTime  daily_cumulativePrintTime  \
0                 4.0667                  4.0667                     4.0667   
1                 0.0000                  0.0000                     0.0000   
2                 0.0000                  0.0000                     0.0000   
3                 0.0000                  0.0000                     0.0000   
4                 0.0000                  0.0000                     0.0000   

   weekly_cumulativePrintTime  monthly_cumulativePrintTime  success reason  \
0                      4.0667                       4.0667        0  error   
1                      0.0000                       0.0000        0  error   
2                      0.0000                       0.0000        0  error   
3                      0.0000                       0.0000        0  error   
4                      0.0000                       0.0000        0  error   

   is_error  ErrorCountSoFar  CumFailure  usage_since_last_error  FailureRate  \
0         1                1          48                  4.0667       0.0043   
1         1                2          48                  4.9667       0.0043   
2         1                3          48                 16.9833       0.0043   
3         1                4          48                  6.0167       0.0043   
4         1                5          48                  0.2000       0.0043   

   FailureRate_per_Print  TotalOperatingTimeExpected  TotalExpectedFailure  \
0                 0.2459                       43800            10770.4918   
1                 0.2214                       43800             9697.4170   
2                 0.1153                       43800             5050.6086   
3                 0.1249                       43800             5469.3028   
4                 0.1551                       43800             6794.2089   

      MTBF  MTBF_per_Print  daily_utilization_rate  weekly_utilization_rate  \
0 230.8792          4.0667                  0.2824                   0.0403   
1 230.8792          4.5167                  0.0000                   0.0000   
2 230.8792          8.6722                  0.0000                   0.0000   
3 230.8792          8.0083                  0.0000                   0.0000   
4 230.8792          6.4467                  0.0000                   0.0000   

   monthly_utilization_rate  print_time_expected  total_print_time_expected  \
0                    0.0094                   36                      18897   
1                    0.0000                   44                      18897   
2                    0.0000                   44                      18897   
3                    0

## <font color="#00008B"><b>⏳ CALCULATING 24 HOURS (MINUTES) = 1440 AS A COLUMN <mark style="background-color: yellow;">'total_available_time'</mark> TO ADD EACH ROW IN THE `history` DATAFRAME</b></font>

As part of the data preparation:

🛠️ **Added a new column** <mark style="background-color: yellow;">`'total_available_time'`</mark> to the **`history`** DataFrame, where each row is assigned a value of **1440** (representing 24 hours in minutes) for further time-based calculations.


In [71]:
history['total_available_time'] = 24 * 60

In [72]:
# -----------------------------------------------------------
# 🔍 CHECK DAILY UPTIME / DOWNTIME / IDLE-TIME COLUMNS
# -----------------------------------------------------------
cols_to_inspect = ["daily_uptime", "daily_downtime", "idle_time"]
missing_cols    = [c for c in cols_to_inspect if c not in history.columns]

if missing_cols:
    print(f"❌ Missing column(s): {', '.join(missing_cols)}")
else:
    print("✅ All specified columns are present.\n")

    # Preview the first few records
    display(history[cols_to_inspect].head())

    # Quick descriptive statistics
    print("\nDescriptive statistics:")
    display(history[cols_to_inspect].describe())


❌ Missing column(s): daily_uptime, daily_downtime, idle_time


## <font color="#00008B"><b>🔧 CALCULATING <mark style="background-color: yellow;">'daily_uptime'</mark>, <mark style="background-color: yellow;">'daily_downtime'</mark>, AND <mark style="background-color: yellow;">'idle_time'</mark> FOR EACH PRINTER</b></font>

As part of data processing:

🛠️ **Sorted the <mark style="background-color: yellow;">`history`</mark> DataFrame**:
- The <mark style="background-color: yellow;">`history`</mark> DataFrame is sorted by <mark style="background-color: yellow;">`'printerName'`</mark> and <mark style="background-color: yellow;">`'startDate'`</mark> to ensure correct sequential processing.

📅 **Processed each printer separately**:
- The data is grouped by <mark style="background-color: yellow;">`'printerName'`</mark>, and for each printer, the full date range between the first <mark style="background-color: yellow;">`'startDate'`</mark> and the last <mark style="background-color: yellow;">`'endDate'`</mark> is calculated using <mark style="background-color: yellow;">`pd.date_range()`</mark>.


📉 **Updated <mark style="background-color: yellow;">'RUL'</mark> (Remaining Useful Life)**:
- The most recent <mark style="background-color: yellow;">`'RUL'`</mark> (Remaining Useful Life) value is extracted for each day and appended to the daily records.

📈 **Generated the final DataFrame**:
- A new DataFrame <mark style="background-color: yellow;">`'daily_df'`</mark> is created with the calculated values for each printer and each day, including <mark style="background-color: yellow;">`'daily_uptime'`</mark>, <mark style="background-color: yellow;">`'daily_downtime'`</mark>, <mark style="background-color: yellow;">`'idle_time'`</mark>, and <mark style="background-color: yellow;">`'RUL'`</mark>.

🧼 **This step ensures that daily operational metrics** like uptime, downtime, and idle time are accurately tracked and stored for each printer, providing insights into printer performance and remaining useful life.


In [73]:
# @title
import pandas as pd
# Ensure all datetimes are timezone-naive for comparison
history['startDate'] = pd.to_datetime(history['startDate']).dt.tz_localize(None)
history['endDate'] = pd.to_datetime(history['endDate']).dt.tz_localize(None)

# Ensure sorting
history = history.sort_values(by=['printerName', 'startDate']).reset_index(drop=True)

daily_records = []

# Process each printer separately
for printer, group in history.groupby('printerName'):
    group = group.reset_index(drop=True)

    # Create full date range between first start and last end
    all_days = pd.date_range(group['startDate'].min().normalize(), group['endDate'].max().normalize())

    unresolved_error_carry = False

    for day in all_days:
        day_start = pd.Timestamp.combine(day, pd.Timestamp.min.time()) + pd.Timedelta(seconds=1)
        day_end = pd.Timestamp.combine(day, pd.Timestamp.max.time())

        day_rows = group[(group['startDate'] <= day_end) & (group['endDate'] >= day_start)]
        total_downtime = 0
        total_uptime = 0

        # ✅ Uptime: sum of successful jobs overlapping with the day
        success_jobs = day_rows[day_rows['is_error'] == 0]
        for _, job in success_jobs.iterrows():
            job_start = max(job['startDate'], day_start)
            job_end = min(job['endDate'], day_end)
            duration = (job_end - job_start).total_seconds() / 60
            total_uptime += duration

        # ✅ Downtime
        if unresolved_error_carry:
            success_today = day_rows[day_rows['is_error'] == 0]
            if not success_today.empty:
                success_start = success_today['startDate'].min()
                downtime_start = day_start
                downtime_end = success_start
                unresolved_error_carry = False
            else:
                downtime_start = day_start
                downtime_end = day_end
                unresolved_error_carry = True

            total_downtime += (downtime_end - downtime_start).total_seconds() / 60

            # Get closest RUL from history
            rul_val = group.loc[(group['startDate'] <= day_end), 'RUL']
            rul_val = rul_val.iloc[-1] if not rul_val.empty else None

            daily_records.append({
                'printerName': printer,
                'year': day.year,
                'month': day.month,
                'day': day.day,
                'date': day,
                'daily_uptime': round(total_uptime, 2),
                'daily_downtime': round(total_downtime, 2),
                'idle_time': round(1440 - total_uptime - total_downtime, 2),
                'RUL': rul_val
            })
            continue

        # Check for errors
        errors_today = day_rows[day_rows['is_error'] == 1]
        if not errors_today.empty:
            first_error = errors_today['startDate'].min()
            next_success = group[(group['startDate'] > first_error) & (group['is_error'] == 0)]
            if not next_success.empty:
                success_start = next_success['startDate'].iloc[0]
                downtime_end = min(success_start, day_end)
                unresolved_error_carry = success_start > day_end
            else:
                downtime_end = day_end
                unresolved_error_carry = True

            downtime_start = first_error
            total_downtime += (downtime_end - downtime_start).total_seconds() / 60

        # Get closest RUL from history
        rul_val = group.loc[(group['startDate'] <= day_end), 'RUL']
        rul_val = rul_val.iloc[-1] if not rul_val.empty else None

        daily_records.append({
            'printerName': printer,
            'year': day.year,
            'month': day.month,
            'day': day.day,
            'date': day,
            'daily_uptime': round(total_uptime, 2),
            'daily_downtime': round(total_downtime, 2),
            'idle_time': round(1440 - total_uptime - total_downtime, 2),
            'RUL': rul_val
        })

# Final DataFrame with RUL
daily_df = pd.DataFrame(daily_records)


## <font color="#00008B"><b>👀 Observing <mark style="background-color: yellow;">'daily_df'</mark></b></font>

As part of data exploration:

🛠️ **Displayed the DataFrame** <mark style="background-color: yellow;">`'daily_df'`</mark> to inspect the calculated values such as <mark style="background-color: yellow;">`'daily_uptime'`</mark>, <mark style="background-color: yellow;">`'daily_downtime'`</mark>, <mark style="background-color: yellow;">`'idle_time'`</mark>, and <mark style="background-color: yellow;">`'RUL'`</mark> for each printer.

🧼 **This step helps verify** the data and ensure that all the calculated metrics are correctly included and formatted in the final DataFrame.


In [74]:
daily_df

printerName  year  month  day       date  daily_uptime  daily_downtime  \
0         Prusa1  2023      2   19 2023-02-19        0.0000        710.7300   
1         Prusa1  2023      2   20 2023-02-20        0.0000       1414.5500   
2         Prusa1  2023      2   21 2023-02-21        0.0000       1414.5500   
3         Prusa1  2023      2   22 2023-02-22        0.0000       1414.5500   
4         Prusa1  2023      2   23 2023-02-23        0.0000       1414.5500   
5         Prusa1  2023      2   24 2023-02-24        0.0000       1414.5500   
6         Prusa1  2023      2   25 2023-02-25        0.0000       1414.5500   
7         Prusa1  2023      2   26 2023-02-26        0.0000       1414.5500   
8         Prusa1  2023      2   27 2023-02-27        0.0000       1414.5500   
9         Prusa1  2023      2   28 2023-02-28        0.0000       1414.5500   
10        Prusa1  2023      3    1 2023-03-01        0.0000       1414.5500   
11        Prusa1  2023      3    2 2023-03-02        0.0000       1414.5500   
12        Prusa1  2023      3    3 2023-03-03        0.0000       1414.5500   
13        Prusa1  2023      3    4 2023-03-04        0.0000       1414.5500   
14        Prusa1  2023      3    5 2023-03-05        0.0000       1414.5500   
15        Prusa1  2023      3    6 2023-03-06        0.0000       1414.5500   
16        Prusa1  2023      3    7 2023-03-07        0.0000       1414.5500   
17        Prusa1  2023      3    8 2023-03-08        0.0000       1414.5500   
18        Prusa1  2023      3    9 2023-03-09        0.0000       1414.5500   
19        Prusa1  2023      3   10 2023-03-10        0.0000       1414.5500   
20        Prusa1  2023      3   11 2023-03-11        0.0000       1414.5500   
21        Prusa1  2023      3   12 2023-03-12        0.0000       1414.5500   
22        Prusa1  2023      3   13 2023-03-13        0.0000       1414.5500   
23        Prusa1  2023      3   14 2023-03-14        0.0000       1414.5500   
24        Prusa1  2023      3   15 2023-03-15        0.0000       1414.5500   
25        Prusa1  2023      3   16 2023-03-16        0.0000       1414.5500   
26        Prusa1  2023      3   17 2023-03-17        0.0000       1414.5500   
27        Prusa1  2023      3   18 2023-03-18        0.0000       1414.5500   
28        Prusa1  2023      3   19 2023-03-19        0.0000       1414.5500   
29        Prusa1  2023      3   20 2023-03-20        0.0000       1414.5500   
30        Prusa1  2023      3   21 2023-03-21        0.0000       1414.5500   
31        Prusa1  2023      3   22 2023-03-22        0.0000       1414.5500   
32        Prusa1  2023      3   23 2023-03-23        0.0000       1414.5500   
33        Prusa1  2023      3   24 2023-03-24        0.0000       1414.5500   
34        Prusa1  2023      3   25 2023-03-25        0.0000       1414.5500   
35        Prusa1  2023      3   26 2023-03-26        0.0000       1414.5500   
36        Prusa1  2023      3   27 2023-03-27        0.0000       1414.5500   
37        Prusa1  2023      3   28 2023-03-28        0.0000       1414.5500   
38        Prusa1  2023      3   29 2023-03-29        0.0000       1414.5500   
39        Prusa1  2023      3   30 2023-03-30        0.0000       1414.5500   
40        Prusa1  2023      3   31 2023-03-31        0.0000       1414.5500   
41        Prusa1  2023      4    1 2023-04-01        0.0000       1414.5500   
42        Prusa1  2023      4    2 2023-04-02        0.0000       1414.5500   
43        Prusa1  2023      4    3 2023-04-03        0.0000       1414.5500   
44        Prusa1  2023      4    4 2023-04-04        0.0000       1414.5500   
45        Prusa1  2023      4    5 2023-04-05        0.0000       1414.5500   
46        Prusa1  2023      4    6 2023-04-06        0.0000       1414.5500   
47        Prusa1  2023      4    7 2023-04-07        0.0000       1414.5500   
48        Prusa1  2023      4    8 2023-04-08        0.0000       1414.5500   
49        Prusa1  2023      4    9 2023-04-09        0.

## <font color="#00008B"><b>📈 COMPUTING DAILY, WEEKLY & MONTHLY UPTIME / DOWNTIME / IDLE METRICS</b></font>

This cell calculates operational availability metrics at three temporal resolutions—**daily**, **weekly**, and **monthly**—for each printer. It helps quantify printer health by breaking down each period into:

1. **<mark style="background-color: yellow;"><b><font color="black">daily_uptime</font></b></mark>**, **<mark style="background-color: yellow;"><b><font color="black">daily_downtime</font></b></mark>** & **<mark style="background-color: yellow;"><b><font color="black">idle_time</font></b></mark>**  
   - Sums minutes of successful jobs per day.  
   - Tracks minutes lost to errors.  
   - Computes the remaining idle minutes (1 440 min/day minus uptime & downtime).

2. **<mark style="background-color: yellow;"><b><font color="black">weekly_uptime</font></b></mark>**, **<mark style="background-color: yellow;"><b><font color="black">weekly_downtime</font></b></mark>** & **<mark style="background-color: yellow;"><b><font color="black">weekly_idle</font></b></mark>**  
   - Aggregates the same calculations over ISO-weeks (7×1 440 min = 10 080 min/week).

3. **<mark style="background-color: yellow;"><b><font color="black">monthly_uptime</font></b></mark>**, **<mark style="background-color: yellow;"><b><font color="black">monthly_downtime</font></b></mark>** & **<mark style="background-color: yellow;"><b><font color="black">monthly_idle</font></b></mark>**  
   - Aggregates over calendar months (variable days × 1 440 min).

> **Note:**  
> - A carry-over flag handles error periods that span across day/week/month boundaries.  
> - All computed values are assigned to the **last record** of each period to simplify downstream joins and visualization.

This comprehensive breakdown ensures you can monitor printer performance trends and preemptively flag under-utilized or error-prone intervals.


In [76]:
import pandas as pd
from datetime import datetime, timedelta

# Ensure datetime columns are correct
history['startDate'] = pd.to_datetime(history['startDate'], errors='coerce')
history['endDate']   = pd.to_datetime(history['endDate'], errors='coerce')

# Sort and reset index
history = history.sort_values(by=['printerName', 'startDate']).reset_index(drop=True)

# Initialize new columns
for col in ['daily_uptime', 'daily_downtime', 'idle_time',
            'weekly_uptime', 'weekly_downtime', 'weekly_idle',
            'monthly_uptime', 'monthly_downtime', 'monthly_idle']:
    history[col] = 0.0

# ----------------------
# DAILY CALCULATION
# ----------------------
for printer, group in history.groupby('printerName'):
    group = group.reset_index()  # preserves original index in 'index'
    all_days = pd.date_range(group['startDate'].min().normalize(),
                             group['endDate'].max().normalize())
    unresolved_error_carry = False

    for day in all_days:
        day_start = pd.Timestamp.combine(day, datetime.min.time()) + pd.Timedelta(seconds=1)
        day_end   = pd.Timestamp.combine(day, datetime.max.time())

        day_rows = group[(group['startDate'] <= day_end) & (group['endDate'] >= day_start)]
        total_uptime   = 0.0
        total_downtime = 0.0

        # UPTIME: sum durations of successful jobs
        for _, job in day_rows[day_rows['is_error'] == 0].iterrows():
            js = max(job['startDate'], day_start)
            je = min(job['endDate'],   day_end)
            total_uptime += (je - js).total_seconds() / 60

        # DOWNTIME calculation
        if unresolved_error_carry:
            success_today = day_rows[day_rows['is_error'] == 0]
            if not success_today.empty:
                success_start = success_today['startDate'].min()
                dt_start = day_start
                dt_end   = success_start
                unresolved_error_carry = False
            else:
                dt_start = day_start
                dt_end   = day_end
                unresolved_error_carry = True
            total_downtime += (dt_end - dt_start).total_seconds() / 60
        else:
            errors_today = day_rows[day_rows['is_error'] == 1]
            if not errors_today.empty:
                first_error = errors_today['startDate'].min()
                next_success = group[(group['startDate'] > first_error) & (group['is_error'] == 0)]
                if not next_success.empty:
                    success_start = next_success['startDate'].iloc[0]
                    dt_end   = min(success_start, day_end)
                    unresolved_error_carry = success_start > day_end
                else:
                    dt_end   = day_end
                    unresolved_error_carry = True
                dt_start = first_error
                total_downtime += (dt_end - dt_start).total_seconds() / 60

        idle = 1440 - total_uptime - total_downtime
        daily_vals = {
            'daily_uptime':   round(total_uptime, 2),
            'daily_downtime': round(total_downtime, 2),
            'idle_time':      round(idle,       2)
        }

        if not day_rows.empty:
            last_row = day_rows.iloc[-1]
            orig_idx = last_row['index']
            history.loc[orig_idx, 'daily_uptime']   = daily_vals['daily_uptime']
            history.loc[orig_idx, 'daily_downtime']= daily_vals['daily_downtime']
            history.loc[orig_idx, 'idle_time']     = daily_vals['idle_time']

# ----------------------
# WEEKLY CALCULATION
# ----------------------
for printer, group in history.groupby('printerName'):
    group = group.reset_index()
    week_ends = pd.date_range(group['startDate'].min().normalize(),
                              group['endDate'].max().normalize(), freq='W-SUN')
    unresolved_error_carry = False

    for week_end in week_ends:
        week_start = week_end - timedelta(days=6)
        ws_full = pd.Timestamp.combine(week_start, datetime.min.time()) + pd.Timedelta(seconds=1)
        we_full = pd.Timestamp.combine(week_end,  datetime.max.time())

        week_rows = group[(group['startDate'] <= we_full) & (group['endDate'] >= ws_full)]
        total_uptime = 0.0
        total_downtime = 0.0

        for _, job in week_rows[week_rows['is_error'] == 0].iterrows():
            js = max(job['startDate'], ws_full)
            je = min(job['endDate'],   we_full)
            total_uptime += (je - js).total_seconds() / 60

        if unresolved_error_carry:
            success_week = week_rows[week_rows['is_error'] == 0]
            if not success_week.empty:
                success_start = success_week['startDate'].min()
                dt_start = ws_full
                dt_end   = success_start
                unresolved_error_carry = False
            else:
                dt_start = ws_full
                dt_end   = we_full
                unresolved_error_carry = True
            total_downtime += (dt_end - dt_start).total_seconds() / 60
        else:
            errors_week = week_rows[week_rows['is_error'] == 1]
            if not errors_week.empty:
                first_error = errors_week['startDate'].min()
                next_success = group[(group['startDate'] > first_error) & (group['is_error'] == 0)]
                if not next_success.empty:
                    success_start = next_success['startDate'].iloc[0]
                    dt_end   = min(success_start, we_full)
                    unresolved_error_carry = success_start > we_full
                else:
                    dt_end   = we_full
                    unresolved_error_carry = True
                dt_start = first_error
                total_downtime += (dt_end - dt_start).total_seconds() / 60

        weekly_minutes = 7 * 1440
        idle = weekly_minutes - total_uptime - total_downtime
        weekly_vals = {
            'weekly_uptime':   round(total_uptime,   2),
            'weekly_downtime': round(total_downtime, 2),
            'weekly_idle':     round(idle,           2)
        }

        if not week_rows.empty:
            last_row = week_rows.iloc[-1]
            orig_idx = last_row['index']
            history.loc[orig_idx, 'weekly_uptime']   = weekly_vals['weekly_uptime']
            history.loc[orig_idx, 'weekly_downtime']= weekly_vals['weekly_downtime']
            history.loc[orig_idx, 'weekly_idle']     = weekly_vals['weekly_idle']

# ----------------------
# MONTHLY CALCULATION
# ----------------------
for printer, group in history.groupby('printerName'):
    group = group.reset_index()
    month_ends = pd.date_range(group['startDate'].min().normalize(),
                               group['endDate'].max().normalize(), freq='M')
    unresolved_error_carry = False

    for month_end in month_ends:
        month_start = month_end.replace(day=1)
        ms_full = pd.Timestamp.combine(month_start, datetime.min.time()) + pd.Timedelta(seconds=1)
        me_full = pd.Timestamp.combine(month_end,  datetime.max.time())

        month_rows = group[(group['startDate'] <= me_full) & (group['endDate'] >= ms_full)]
        total_uptime   = 0.0
        total_downtime = 0.0

        for _, job in month_rows[month_rows['is_error'] == 0].iterrows():
            js = max(job['startDate'], ms_full)
            je = min(job['endDate'],   me_full)
            total_uptime += (je - js).total_seconds() / 60

        if unresolved_error_carry:
            success_month = month_rows[month_rows['is_error'] == 0]
            if not success_month.empty:
                success_start = success_month['startDate'].min()
                dt_start = ms_full
                dt_end   = success_start
                unresolved_error_carry = False
            else:
                dt_start = ms_full
                dt_end   = me_full
                unresolved_error_carry = True
            total_downtime += (dt_end - dt_start).total_seconds() / 60
        else:
            errors_month = month_rows[month_rows['is_error'] == 1]
            if not errors_month.empty:
                first_error = errors_month['startDate'].min()
                next_success = group[(group['startDate'] > first_error) & (group['is_error'] == 0)]
                if not next_success.empty:
                    success_start = next_success['startDate'].iloc[0]
                    dt_end   = min(success_start, me_full)
                    unresolved_error_carry = success_start > me_full
                else:
                    dt_end   = me_full
                    unresolved_error_carry = True
                dt_start = first_error
                total_downtime += (dt_end - dt_start).total_seconds() / 60

        days_in_month = (me_full - ms_full).days + 1
        monthly_minutes = days_in_month * 1440
        idle = monthly_minutes - total_uptime - total_downtime
        monthly_vals = {
            'monthly_uptime':   round(total_uptime,   2),
            'monthly_downtime': round(total_downtime, 2),
            'monthly_idle':     round(idle,           2)
        }

        if not month_rows.empty:
            last_row = month_rows.iloc[-1]
            orig_idx = last_row['index']
            history.loc[orig_idx, 'monthly_uptime']   = monthly_vals['monthly_uptime']
            history.loc[orig_idx, 'monthly_downtime']= monthly_vals['monthly_downtime']
            history.loc[orig_idx, 'monthly_idle']     = monthly_vals['monthly_idle']

# Display updated DataFrame
history


printerID printerName           startDate  \
0    63af118fd41d203cfc2d5193      Prusa1 2023-02-19 11:56:33   
1    66a632772531d16acc9b3a00      Prusa1 2024-07-28 14:32:28   
2    66a632772531d16acc9b3a00      Prusa1 2024-07-28 14:38:34   
3    66a632772531d16acc9b3a00      Prusa1 2024-07-28 15:11:19   
4    66a632772531d16acc9b3a00      Prusa1 2024-07-28 15:32:32   
5    66a632772531d16acc9b3a00      Prusa1 2024-07-28 15:35:52   
6    66a632772531d16acc9b3a00      Prusa1 2024-07-28 15:38:03   
7    66a632772531d16acc9b3a00      Prusa1 2024-07-29 18:44:28   
8    66a632772531d16acc9b3a00      Prusa1 2024-07-29 20:02:19   
9    66a632772531d16acc9b3a00      Prusa1 2024-11-05 14:48:13   
10   66a632772531d16acc9b3a00      Prusa1 2024-11-06 08:13:39   
11   66a632772531d16acc9b3a00      Prusa1 2024-11-08 16:11:37   
12   66a632772531d16acc9b3a00      Prusa1 2024-11-10 10:28:26   
13   66a632772531d16acc9b3a00      Prusa1 2024-11-11 11:48:07   
14   66a632772531d16acc9b3a00      Prusa1 2024-11-14 09:13:25   
15   66a632772531d16acc9b3a00      Prusa1 2024-11-14 11:31:10   
16   66a632772531d16acc9b3a00      Prusa1 2024-11-29 15:34:18   
17   66a632772531d16acc9b3a00      Prusa1 2024-12-10 11:20:48   
18   66a632772531d16acc9b3a00      Prusa1 2024-12-10 11:24:27   
19   66a632772531d16acc9b3a00      Prusa1 2024-12-12 11:01:23   
20   66a632772531d16acc9b3a00      Prusa1 2024-12-12 14:22:09   
21   66a632772531d16acc9b3a00      Prusa1 2024-12-12 15:07:51   
22   66a632772531d16acc9b3a00      Prusa1 2024-12-12 15:10:16   
23   66a632772531d16acc9b3a00      Prusa1 2024-12-18 10:30:02   
24   66a632772531d16acc9b3a00      Prusa1 2024-12-18 10:55:54   
25   66a632772531d16acc9b3a00      Prusa1 2024-12-18 10:59:19   
26   66a632772531d16acc9b3a00      Prusa1 2024-12-18 12:31:42   
27   66a632772531d16acc9b3a00      Prusa1 2024-12-18 12:36:30   
28   66a632772531d16acc9b3a00      Prusa1 2024-12-19 08:28:10   
29   66a632772531d16acc9b3a00      Prusa1 2024-12-19 09:01:40   
30   66a632772531d16acc9b3a00      Prusa1 2024-12-19 10:24:29   
31   66a632772531d16acc9b3a00      Prusa1 2024-12-19 12:17:22   
32   66a632772531d16acc9b3a00      Prusa1 2024-12-19 14:19:31   
33   66a632772531d16acc9b3a00      Prusa1 2024-12-19 15:23:55   
34   66a632772531d16acc9b3a00      Prusa1 2024-12-19 16:17:15   
35   66a632772531d16acc9b3a00      Prusa1 2024-12-19 17:13:36   
36   66a632772531d16acc9b3a00      Prusa1 2024-12-19 19:43:51   
37   66a632772531d16acc9b3a00      Prusa1 2024-12-20 09:11:44   
38   66a632772531d16acc9b3a00      Prusa1 2024-12-22 12:13:08   
39   66a632772531d16acc9b3a00      Prusa1 2024-12-23 10:24:01   
40   66a632772531d16acc9b3a00      Prusa1 2024-12-23 17:32:21   
41   66a632772531d16acc9b3a00      Prusa1 2024-12-24 12:46:23   
42   66a632772531d16acc9b3a00      Prusa1 2024-12-25 19:17:54   
43   66a632772531d16acc9b3a00      Prusa1 2024-12-26 14:23:58   
44   66a632772531d16acc9b3a00      Prusa1 2024-12-30 12:57:23   
45   66a632772531d16acc9b3a00      Prusa1 2024-12-30 13:11:05   
46   66a632772531d16acc9b3a00      Prusa1 2024-12-30 16:52:28   
47   66a632772531d16acc9b3a00      Prusa1 2024-12-31 11:14:02   
48   66a632772531d16acc9b3a00      Prusa1 2024-12-31 14:30:57   
49   66a632772531d16acc9b3a00      Prusa1 2024-12-31 14:45:41   
50   66a632772531d16acc9b3a00      Prusa1 2024-12-31 14:53:31   
51   66a632772531d16acc9b3a00      Prusa1 2024-12-31 17:56:48   
52   66a632772531d16acc9b3a00      Prusa1 2024-12-31 21:05:13   
53   66a632772531d16acc9b3a00      Prusa1 2025-01-02 09:56:05   
54   66a632772531d16acc9b3a00      Prusa1 2025-01-02 13:22:48   
55   66a632772531d16acc9b3a00      Prusa1 2025-01-02 17:07:04   
56   66a632772531d16acc9b3a00      Prusa1 2025-01-03 12:35:18   
57   66a632772531d16acc9b3a00      Prusa1 2025-01-03 18:05:56   
58   66a632772531d16acc9b3a00      Prusa1 2025-01-04 13:14:45   
59   66a632772531d16acc9b3a00      Prusa1 2025-01-04 16:20:47   
60   66a632772531d16acc9b3a00      Prusa1 2025-01-22 08

## <font color="#00008B"><b>🔄 REORDERING THE COLUMNS IN THE <mark style="background-color: yellow;">`history`</mark> DATAFRAME</b></font>

As part of data organization:

🛠️ **Defined the new column order**:
- The **<mark style="background-color: yellow;">`new_order`</mark>** list specifies the new order of columns for the **<mark style="background-color: yellow;">`history`</mark>** DataFrame. The columns are grouped into different categories for better organization:
  - **Group 1**: Identification / General Info (e.g., **<mark style="background-color: yellow;">`'printerID'`</mark>**, **<mark style="background-color: yellow;">`'printerName'`</mark>**, **<mark style="background-color: yellow;">`'success'`</mark>**).
  - **Group 2**: Date/Time Information (e.g., **<mark style="background-color: yellow;">`'startDate'`</mark>**, **<mark style="background-color: yellow;">`'endDate'`</mark>**).
  - **Group 3**: Print Time Metrics (e.g., **<mark style="background-color: yellow;">`'printTime'`</mark>**, **<mark style="background-color: yellow;">`'cumulativePrintTime'`</mark>**).
  - **Group 4**: MTBF and Failure Rates (e.g., **<mark style="background-color: yellow;">`'MTBF_per_Print'`</mark>**, **<mark style="background-color: yellow;">`'FailureRate'`</mark>**).
  - **Group 5**: Operating Times & Expectations (e.g., **<mark style="background-color: yellow;">`'TotalOperatingTimeExpected'`</mark>**).
  - **Group 6**: Daily Print Time Details (e.g., **<mark style="background-color: yellow;">`'daily_cumulativePrintTime'`</mark>**).
  - **Group 7**: Daily Performance & Utilization (e.g., **<mark style="background-color: yellow;">`'daily_uptime'`</mark>**).
  - **Group 8**: Weekly Metrics (e.g., **<mark style="background-color: yellow;">`'weekly_uptime'`</mark>**).
  - **Group 9**: Monthly Metrics (e.g., **<mark style="background-color: yellow;">`'monthly_uptime'`</mark>**).
  - **Group 10**: Efficiency (e.g., **<mark style="background-color: yellow;">`'Efficiency_per_printer'`</mark>**).

🔄 **Reordered the columns**:
- The **<mark style="background-color: yellow;">`history`</mark>** DataFrame is reordered using the **<mark style="background-color: yellow;">`new_order`</mark>** list, with the new column arrangement applied.

📊 **Checked the DataFrame info and displayed the first few rows**:
- The **<mark style="background-color: yellow;">`history.info()`</mark>** and **<mark style="background-color: yellow;">`history.head()`</mark>** functions are used to verify the structure and preview the updated DataFrame.


In [77]:
history.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 171 entries, 0 to 170
Data columns (total 51 columns):
 #   Column                       Non-Null Count  Dtype         
---  ------                       --------------  -----         
 0   printerID                    171 non-null    object        
 1   printerName                  171 non-null    object        
 2   startDate                    171 non-null    datetime64[ns]
 3   endDate                      171 non-null    datetime64[ns]
 4   total_prints                 171 non-null    int64         
 5   total_success                171 non-null    int32         
 6   SuccessRate                  171 non-null    float64       
 7   Efficiency                   171 non-null    float64       
 8   printTime                    171 non-null    float64       
 9   totalPrintTime               171 non-null    float64       
 10  cumulativePrintTime          171 non-null    float64       
 11  daily_TotalPrintTime         171 non-null    

In [78]:
# Define the new column order based on your history DataFrame’s structure
new_order = [
    # Group 1: Identification / General Info
    "printerID", "printerName", "success", "reason", "reason_description",
    "fileName", "filePath", "is_error",

    # Group 2: Date/Time Information
    "startDate", "endDate", "day", "calendar_week", "month", "year",

    # Group 3: Print Time Metrics
    "printTime", "cumulativePrintTime", "totalPrintTime",
    "total_prints", "total_success", "ErrorCountSoFar", "CumFailure",

    # Group 4: MTBF and Failure Rates
    "MTBF_per_Print", "MTBF", "FailureRate", "FailureRate_per_Print", "SuccessRate",

    # Group 5: Operating Times & Expectations
    "TotalOperatingTimeExpected", "TotalExpectedFailure", "RUL",

    # Group 6: Daily Print Time Details
    "daily_cumulativePrintTime", "daily_TotalPrintTime",
    "print_time_expected", "total_print_time_expected",
    "usage_since_last_error", "total_available_time",

    # Group 7: Daily Performance & Utilization
    "daily_uptime", "daily_downtime", "idle_time", "daily_utilization_rate",

    # Group 8: Weekly Metrics
    "weekly_cumulativePrintTime", "weekly_TotalPrintTime",
    "weekly_uptime", "weekly_downtime", "weekly_idle", "weekly_utilization_rate",

    # Group 9: Monthly Metrics
    "monthly_cumulativePrintTime", "monthly_TotalPrintTime",
    "monthly_uptime", "monthly_downtime", "monthly_idle", "monthly_utilization_rate"
]

# Only keep columns that exist in the DataFrame
existing_cols = [col for col in new_order if col in history.columns]

if existing_cols:
    history = history[existing_cols]
    history.info()
    display(history.head())
else:
    print("None of the specified columns exist in the history DataFrame.")

# Check the result
history.info()
history.head()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 171 entries, 0 to 170
Data columns (total 50 columns):
 #   Column                       Non-Null Count  Dtype         
---  ------                       --------------  -----         
 0   printerID                    171 non-null    object        
 1   printerName                  171 non-null    object        
 2   success                      171 non-null    int32         
 3   reason                       171 non-null    object        
 4   fileName                     171 non-null    object        
 5   filePath                     171 non-null    object        
 6   is_error                     171 non-null    int32         
 7   startDate                    171 non-null    datetime64[ns]
 8   endDate                      171 non-null    datetime64[ns]
 9   day                          171 non-null    object        
 10  calendar_week                171 non-null    UInt32        
 11  month                        171 non-null    

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
1  66a632772531d16acc9b3a00      Prusa1        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath  is_error  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m.gcode         1   
1                 1xfilled_0.15mm_PLA_MINI_44m.gcode         1   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode         1   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode         1   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode         1   

            startDate             endDate         day  calendar_week  month  \
0 2023-02-19 11:56:33 2023-02-19 12:00:37  2023-02-19              7      2   
1 2024-07-28 14:32:28 2024-07-28 14:37:26  2024-07-28             30      7   
2 2024-07-28 14:38:34 2024-07-28 14:55:34  2024-07-28             30      7   
3 2024-07-28 15:11:19 2024-07-28 15:17:20  2024-07-28             30      7   
4 2024-07-28 15:32:32 2024-07-28 15:32:44  2024-07-28             30      7   

   year  printTime  cumulativePrintTime  totalPrintTime  total_prints  \
0  2023     4.0667               4.0667      11082.2000           112   
1  2024     4.9667               9.0333      11082.2000           112   
2  2024    16.9833              26.0167      11082.2000           112   
3  2024     6.0167              32.0333      11082.2000           112   
4  2024     0.2000              32.2333      11082.2000           112   

   total_success  ErrorCountSoFar  CumFailure  MTBF_per_Print     MTBF  \
0             64                1          48          4.0667 230.8792   
1             64                2          48          4.5167 230.8792   
2             64                3          48          8.6722 230.8792   
3             64                4          48          8.0083 230.8792   
4             64                5          48          6.4467 230.8792   

   FailureRate  FailureRate_per_Print  SuccessRate  \
0       0.0043                 0.2459      57.1429   
1       0.0043                 0.2214      57.1429   
2       0.0043                 0.1153      57.1429   
3       0.0043                 0.1249      57.1429   
4       0.0043                 0.1551      57.1429   

   TotalOperatingTimeExpected  TotalExpectedFailure      RUL  \
0                       43800            10770.4918 729.9322   
1                       43800             9697.4170 729.8494   
2                       43800             5050.6086 729.5664   
3                       43800             5469.3028 729.4661   
4                       43800             6794.2089 729.4628   

   daily_cumulativePrintTime  daily_TotalPrintTime  print_time_expected  \
0                     4.0667                4.0667                   36   
1                     0.0000                0.0000                   44   
2                     0.0000                0.0000                   44   
3                     0.0000                0.0000                   44   
4                     0.0000                0.0000                   44   

   total_print_time_expected  usage_since_last_error  total_available_time  \
0                      18897                  4.0667                  1440   
1                      18897                  4.9667                  1440   
2                      18897                 16.9833                  1440   
3                      18897                  6.0167                  1440   
4                  

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 171 entries, 0 to 170
Data columns (total 50 columns):
 #   Column                       Non-Null Count  Dtype         
---  ------                       --------------  -----         
 0   printerID                    171 non-null    object        
 1   printerName                  171 non-null    object        
 2   success                      171 non-null    int32         
 3   reason                       171 non-null    object        
 4   fileName                     171 non-null    object        
 5   filePath                     171 non-null    object        
 6   is_error                     171 non-null    int32         
 7   startDate                    171 non-null    datetime64[ns]
 8   endDate                      171 non-null    datetime64[ns]
 9   day                          171 non-null    object        
 10  calendar_week                171 non-null    UInt32        
 11  month                        171 non-null    

printerID printerName  success reason  \
0  63af118fd41d203cfc2d5193      Prusa1        0  error   
1  66a632772531d16acc9b3a00      Prusa1        0  error   
2  66a632772531d16acc9b3a00      Prusa1        0  error   
3  66a632772531d16acc9b3a00      Prusa1        0  error   
4  66a632772531d16acc9b3a00      Prusa1        0  error   

                                            fileName  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m 2 ...   
1                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode   

                                            filePath  is_error  \
0  Game_tray_thick_tapered_0.25mm_ABS_MINI_36m.gcode         1   
1                 1xfilled_0.15mm_PLA_MINI_44m.gcode         1   
2                 1xfilled_0.15mm_PLA_MINI_44m.gcode         1   
3                 1xfilled_0.15mm_PLA_MINI_44m.gcode         1   
4                 1xfilled_0.15mm_PLA_MINI_44m.gcode         1   

            startDate             endDate         day  calendar_week  month  \
0 2023-02-19 11:56:33 2023-02-19 12:00:37  2023-02-19              7      2   
1 2024-07-28 14:32:28 2024-07-28 14:37:26  2024-07-28             30      7   
2 2024-07-28 14:38:34 2024-07-28 14:55:34  2024-07-28             30      7   
3 2024-07-28 15:11:19 2024-07-28 15:17:20  2024-07-28             30      7   
4 2024-07-28 15:32:32 2024-07-28 15:32:44  2024-07-28             30      7   

   year  printTime  cumulativePrintTime  totalPrintTime  total_prints  \
0  2023     4.0667               4.0667      11082.2000           112   
1  2024     4.9667               9.0333      11082.2000           112   
2  2024    16.9833              26.0167      11082.2000           112   
3  2024     6.0167              32.0333      11082.2000           112   
4  2024     0.2000              32.2333      11082.2000           112   

   total_success  ErrorCountSoFar  CumFailure  MTBF_per_Print     MTBF  \
0             64                1          48          4.0667 230.8792   
1             64                2          48          4.5167 230.8792   
2             64                3          48          8.6722 230.8792   
3             64                4          48          8.0083 230.8792   
4             64                5          48          6.4467 230.8792   

   FailureRate  FailureRate_per_Print  SuccessRate  \
0       0.0043                 0.2459      57.1429   
1       0.0043                 0.2214      57.1429   
2       0.0043                 0.1153      57.1429   
3       0.0043                 0.1249      57.1429   
4       0.0043                 0.1551      57.1429   

   TotalOperatingTimeExpected  TotalExpectedFailure      RUL  \
0                       43800            10770.4918 729.9322   
1                       43800             9697.4170 729.8494   
2                       43800             5050.6086 729.5664   
3                       43800             5469.3028 729.4661   
4                       43800             6794.2089 729.4628   

   daily_cumulativePrintTime  daily_TotalPrintTime  print_time_expected  \
0                     4.0667                4.0667                   36   
1                     0.0000                0.0000                   44   
2                     0.0000                0.0000                   44   
3                     0.0000                0.0000                   44   
4                     0.0000                0.0000                   44   

   total_print_time_expected  usage_since_last_error  total_available_time  \
0                      18897                  4.0667                  1440   
1                      18897                  4.9667                  1440   
2                      18897                 16.9833                  1440   
3                      18897                  6.0167                  1440   
4                  

## <font color="#00008B"><b>💾 EXPORTING THE CLEANED DATAFRAME TO GOOGLE DRIVE</b></font>

🔒 **Safeguard**  
The routine first confirms that a dataframe named  
<mark style="background-color: yellow;"><b><font color="black">`history`</font></b></mark>  
is in memory; if not, an informative error is raised so nothing is overwritten by mistake.

---

📅 **Dynamic file-naming**  
A timestamped filename is generated on-the-fly:  

``{YYYYMMDD}_processed_lab.csv``  

using **`datetime.today().strftime('%Y%m%d')`** — ensuring each export is uniquely versioned.

---

📁 **Write-out location**  
The CSV is persisted to your shared-drive path:

In [80]:
from datetime import datetime
from zoneinfo import ZoneInfo
from IPython.display import Markdown, display
import os



# === Extract folder and file base name ===
input_folder = os.path.dirname(file_path)
input_name = os.path.splitext(os.path.basename(file_path))[0]

# === Get Berlin timestamp ===
berlin_tz  = ZoneInfo("Europe/Berlin")
now        = datetime.now(berlin_tz)
now_human  = now.strftime("%d %b %Y %H:%M (CET)")
date_stamp = now.strftime("%Y%m%d")

# === Build CSV output path: same folder, timestamped name ===
csv_file_name = f"{input_name}_{date_stamp}_processed.csv"
output_path   = os.path.join(input_folder, csv_file_name)

# === Save the DataFrame ===
history.to_csv(output_path, index=False)

# === Show result ===
md = f"""
<table style="width:100%; border:2px solid #003366; border-collapse:collapse; font-family:Arial, sans-serif;">
  <thead>
    <tr style="background:#003366; color:#FFFFFF;">
      <th colspan="2" style="padding:10px; font-size:20px; text-align:left;">
        💾 <strong>DATAFRAME SAVED SUCCESSFULLY</strong>
      </th>
    </tr>
  </thead>
  <tbody style="font-size:15px;">
    <tr style="background:#F5F7FA;">
      <td style="padding:8px 12px; font-weight:600;">Export Time</td>
      <td style="padding:8px 12px;">{now_human}</td>
    </tr>
    <tr>
      <td style="padding:8px 12px; font-weight:600;">Filename</td>
      <td style="padding:8px 12px;"><code>{csv_file_name}</code></td>
    </tr>
    <tr style="background:#F5F7FA;">
      <td style="padding:8px 12px; font-weight:600;">Saved To</td>
      <td style="padding:8px 12px;"><code>{output_path}</code></td>
    </tr>
  </tbody>
</table>

<div style="margin-top:14px; font-size:14px; color:#444;">
  Your <strong>history</strong> DataFrame has been saved locally and is ready for downstream use.
</div>
"""

display(Markdown(md))



<table style="width:100%; border:2px solid #003366; border-collapse:collapse; font-family:Arial, sans-serif;">
  <thead>
    <tr style="background:#003366; color:#FFFFFF;">
      <th colspan="2" style="padding:10px; font-size:20px; text-align:left;">
        💾 <strong>DATAFRAME SAVED SUCCESSFULLY</strong>
      </th>
    </tr>
  </thead>
  <tbody style="font-size:15px;">
    <tr style="background:#F5F7FA;">
      <td style="padding:8px 12px; font-weight:600;">Export Time</td>
      <td style="padding:8px 12px;">11 Jun 2025 16:29 (CET)</td>
    </tr>
    <tr>
      <td style="padding:8px 12px; font-weight:600;">Filename</td>
      <td style="padding:8px 12px;"><code>Lab_02_20250611_processed.csv</code></td>
    </tr>
    <tr style="background:#F5F7FA;">
      <td style="padding:8px 12px; font-weight:600;">Saved To</td>
      <td style="padding:8px 12px;"><code>C:\Users\Aymen\OneDrive\Desktop\codepreprocessing\Lab_02_20250611_processed.csv</code></td>
    </tr>
  </tbody>
</table>

<div style="margin-top:14px; font-size:14px; color:#444;">
  Your <strong>history</strong> DataFrame has been saved locally and is ready for downstream use.
</div>


<h1 style="font-size:60px; color:#FF0000; font-weight:900; text-align:center; margin-top:22px;">
  🚀 <strong>NEXT&nbsp;STEP</strong> 🚀
</h1>

<ul style="font-size:20px; color:#FF0000; font-weight:700; line-height:1.6; margin-left:-10px;">
  <li>📊 A suite of refined <strong>data visualisations</strong> will be produced.</li>
  <li>🤖 A robust <strong>regression model</strong> will be trained&nbsp;&amp;&nbsp;evaluated.</li>
</ul>

<p style="font-size:19px; color:#FF0000; font-weight:700; margin-top:14px;">
  🔎 <em>Note:</em> When this stage is complete, retrieve your generated model / code artefacts from:<br>
  &nbsp;&nbsp;&nbsp;
  <a href="file:///content/drive/Shareddrives/PRAEDICTIO/Data/LAB_Data/Models/" target="_blank" style="text-decoration:underline;">
    📂 <strong>/content/drive/Shareddrives/PRAEDICTIO/Data/LAB_Data/Models/</strong>
  </a>
</p>
